In [3]:
import requests
import pandas as pd
import pymysql
from datetime import datetime, timedelta
import traceback2
import time

api_key = "a86e3326-8c8d-434e-897a-5d6becbf1f35"

symbol_tags = []
defi_symbols = []

def get_other_fields_historical_parsed_data(response_data, date, symbols):
    data = []
    date = datetime(date.year, date.month, date.day)
    for row in response_data:
        symbol = row['symbol']
        print(row)
        break
        if True:
            mcap = row['quote']['USD']['market_cap']
            volume_24h = row['quote']['USD']['volume_24h']
            price = row['quote']['USD']['price']
            symbol_data = [date, symbol, row['name'], price, mcap, row['max_supply'], row['circulating_supply'], row['total_supply'], volume_24h]
            symbol_tags.append([symbol, row['name'], row['tags']])
            tags = row['tags']
            if 'defi' in tags or 'defi-index' in tags:
                defi_symbols.append(symbol)
            data.append(symbol_data)
            
    return data


def get_other_fields_historical_data(date, symbols, count=5000):
    print('Fetching')
    url = "https://pro-api.coinmarketcap.com/v1/cryptocurrency/listings/historical"
    payload = {
        'convert': 'USD',
        'date': date,
        'limit': count,
        'cryptocurrency_type': 'all',
        'aux': 'tags,circulating_supply,total_supply,max_supply'
    }
    headers = {
        'Accepts': 'application/json',
        'X-CMC_PRO_API_KEY': api_key
    }
    try:
        response = requests.get(url, params=payload, headers=headers).json()
        data = response['data']
#         print(data)
        data = get_other_fields_historical_parsed_data(data, date, symbols)
        return data
    except Exception:
        print(traceback2.format_exc())
        if response:
            print(response)
        return []


def get_other_fields_historical_data_df(start_date, symbols):
    data = []
    now = datetime.now()
    print(start_date)
    print(now)
    print(start_date.timestamp() < now.timestamp())
    while start_date.timestamp() < now.timestamp():
        date = datetime(start_date.year, start_date.month, start_date.day)
        print(date)
        rows = get_other_fields_historical_data(date, symbols)
        time.sleep(.6)
        print(date, len(rows))
        if rows:
            data.extend(rows)
        start_date = start_date + timedelta(days=1)
    df = pd.DataFrame(data, columns=['date', 'symbol', 'name', 'price', 'mrk_cap', 'max_supply', 'circulating_supply', 'total_supply', 'volume'])
    df['date'] = pd.to_datetime(df['date'])
    return df




In [4]:
get_other_fields_historical_data_df(datetime(2021, 4, 8), [])

2021-04-08 00:00:00
2021-04-10 21:02:25.733125
True
2021-04-08 00:00:00
Fetching
{'id': 1, 'name': 'Bitcoin', 'symbol': 'BTC', 'slug': 'bitcoin', 'tags': ['mineable', 'pow', 'sha-256', 'store-of-value', 'state-channels', 'coinbase-ventures-portfolio', 'three-arrows-capital-portfolio', 'polychain-capital-portfolio', 'binance-labs-portfolio', 'arrington-xrp-capital', 'blockchain-capital-portfolio', 'boostvc-portfolio', 'cms-holdings-portfolio', 'dcg-portfolio', 'dragonfly-capital-portfolio', 'electric-capital-portfolio', 'fabric-ventures-portfolio', 'framework-ventures', 'galaxy-digital-portfolio', 'huobi-capital', 'alameda-research-portfolio', 'a16z-portfolio', '1confirmation-portfolio', 'winklevoss-capital', 'usv-portfolio', 'placeholder-ventures-portfolio', 'pantera-capital-portfolio', 'multicoin-capital-portfolio', 'paradigm-xzy-screener'], 'max_supply': 21000000, 'circulating_supply': 18677306, 'total_supply': 18677306, 'last_updated': '2021-04-08T23:00:00.000Z', 'quote': {'USD': {'

Empty DataFrame
Columns: [date, symbol, name, price, mrk_cap, max_supply, circulating_supply, total_supply, volume]
Index: []

In [25]:
",".join(defi_symbols)

'UNI,LINK,WBTC,LUNA,AAVE,AVAX,DAI,CAKE,RUNE,COMP,SNX,MKR,GRT,SUSHI,YFI,UMA,ZRX,BNT,FTM,RSR,REN,1INCH,OGN,CRV,MDX,DODO,OCEAN,LRC,KNC,RENBTC,XVS,REP,ALPHA,KAVA,REEF,SXP,BADGER,BAL,BTS,NMR,BAND,JST,WAN,SRM,COTI,GNO,POLS,INJ,XHV,FEI,DFI,KSP,MIR,NXM,ORN,KEEP,TRIBE,RAY,RLC,USDN,SCRT,AMPL,AKRO,BAKE,STAKE,BZRX,DDX,UQC,VAI,PERP,MLN,RAMP,REQ,BEL,CHR,SUSD,VSP,FLM,FRM,SURE,DIA,DEGO,DAO,SFI,OM,AUCTION,RGT,FARM,STRK,YFII,PHB,FRONT,DREP,TRB,ZEE,BEAM,HEGIC,CREAM,IDEX,SWTH,UNFI,XPR,WING,STPT,SUKU,OXEN,FXS,PNT,EASY,SWINGBY,DEXE,AST,CVP,BOR,FSN,TRU,BONDLY,CORE,MATTER,AUTO,ZAP,ANY,MTA,SUTER,POLK,NEX,DF,KP3R,PEAK,CUSD,MUSD,BOT,APY,FIS,RBC,DHT,FOR,MET,EGG,BEPRO,LTX,SHROOM,OPIUM,MARK,SOCKS,XEND,DEC,WHITE,ARMOR,UMB,APYS,STRONG,YF-DAI,SWRV,PICKLE,SWFTC,UNISTAKE,HOT,AUC,YFL,DOWS,HGET,MTRG,LUA,IDLE,TKN,FIN,DYP,SYNC,LDO,COMBO,HAKKA,SMARTCREDIT,DOUGH,CNS,NSURE,YIELD,HYPR,JRT,ALPACA,BITCNY,ALLOY,DMG,ADD,ROT,EOSDT,YVS,YFIII,DEFI++,VTX,ETHYS,PIPT,ACED,KP4R,DAM,ETHY,ORE,REB2,CDAI,CUSDC,VALUE,DPI,CUSDT,ALCX,COOK,ZDEX,D

In [24]:
len(defi_symbols)

275

In [7]:
symbol_tags

[['BTC',
  'Bitcoin',
  ['mineable',
   'pow',
   'sha-256',
   'store-of-value',
   'state-channels',
   'coinbase-ventures-portfolio',
   'three-arrows-capital-portfolio',
   'polychain-capital-portfolio',
   'binance-labs-portfolio',
   'arrington-xrp-capital',
   'blockchain-capital-portfolio',
   'boostvc-portfolio',
   'cms-holdings-portfolio',
   'dcg-portfolio',
   'dragonfly-capital-portfolio',
   'electric-capital-portfolio',
   'fabric-ventures-portfolio',
   'framework-ventures',
   'galaxy-digital-portfolio',
   'huobi-capital',
   'alameda-research-portfolio',
   'a16z-portfolio',
   '1confirmation-portfolio',
   'winklevoss-capital',
   'usv-portfolio',
   'placeholder-ventures-portfolio',
   'pantera-capital-portfolio',
   'multicoin-capital-portfolio',
   'paradigm-xzy-screener']],
 ['BTC',
  'Bitcoin',
  ['mineable',
   'pow',
   'sha-256',
   'store-of-value',
   'state-channels',
   'coinbase-ventures-portfolio',
   'three-arrows-capital-portfolio',
   'polychain-ca

In [18]:
def get_joins(symbols1, symbols2):
    symbols_list = symbols1.copy()
    for symbol in symbols2:
        if symbol not in symbols1:
            symbols_list.append(symbol)            
    return symbols_list

In [19]:
all_tags = []
for l in symbol_tags:
    all_tags = get_joins(all_tags, l[2])

In [20]:
all_tags.sort()
all_tags

['1confirmation-portfolio',
 'a16z-portfolio',
 'aave-tokens',
 'adult',
 'agriculture',
 'ai-big-data',
 'alameda-research-portfolio',
 'amm',
 'analytics',
 'argon2',
 'arrington-xrp-capital',
 'art',
 'asset-backed-coin',
 'asset-management',
 'atomic-swaps',
 'avalanche-ecosystem',
 'binance-chain',
 'binance-labs-portfolio',
 'binance-launchpad',
 'binance-launchpool',
 'binance-smart-chain',
 'blake',
 'blake256',
 'blake2b',
 'blake2s',
 'blockchain-capital-portfolio',
 'boostvc-portfolio',
 'centralized-exchange',
 'cms-holdings-portfolio',
 'coinbase-ventures-portfolio',
 'coinfund-portfolio',
 'collectibles-nfts',
 'commodities',
 'communications-social-media',
 'content-creation',
 'cosmos',
 'cosmos-ecosystem',
 'crowdfunding',
 'crowdsourcing',
 'cryptonight',
 'cryptonight-lite',
 'cuckoo-cycle',
 'cybersecurity',
 'dag',
 'dagger-hashimoto',
 'dao',
 'dao-maker',
 'dapp',
 'data-availability-proof',
 'data-provenance',
 'dcg-portfolio',
 'decentralized-exchange',
 'defi'

In [7]:
len(all_tags)

218

In [8]:
all_tags.sort()

In [9]:
all_tags

['1confirmation-portfolio',
 'a16z-portfolio',
 'aave-tokens',
 'adult',
 'agriculture',
 'ai-big-data',
 'alameda-research-portfolio',
 'amm',
 'analytics',
 'argon2',
 'arrington-xrp-capital',
 'art',
 'asset-backed-coin',
 'asset-management',
 'atomic-swaps',
 'avalanche-ecosystem',
 'binance-chain',
 'binance-labs-portfolio',
 'binance-launchpad',
 'binance-launchpool',
 'binance-smart-chain',
 'blake',
 'blake256',
 'blake2b',
 'blake2s',
 'blockchain-capital-portfolio',
 'boostvc-portfolio',
 'centralized-exchange',
 'cms-holdings-portfolio',
 'coinbase-ventures-portfolio',
 'coinfund-portfolio',
 'collectibles-nfts',
 'commodities',
 'communications-social-media',
 'content-creation',
 'cosmos',
 'cosmos-ecosystem',
 'crowdfunding',
 'crowdsourcing',
 'cryptonight',
 'cryptonight-lite',
 'cuckoo-cycle',
 'cybersecurity',
 'dag',
 'dagger-hashimoto',
 'dao',
 'dao-maker',
 'dapp',
 'data-availability-proof',
 'data-provenance',
 'dcg-portfolio',
 'decentralized-exchange',
 'defi'

In [10]:
tag_map = {}
i = 0
for tag in all_tags:
    tag_map[tag] = i
    i = i + 1

In [11]:
tag_map

{'1confirmation-portfolio': 0,
 'a16z-portfolio': 1,
 'aave-tokens': 2,
 'adult': 3,
 'agriculture': 4,
 'ai-big-data': 5,
 'alameda-research-portfolio': 6,
 'amm': 7,
 'analytics': 8,
 'argon2': 9,
 'arrington-xrp-capital': 10,
 'art': 11,
 'asset-backed-coin': 12,
 'asset-management': 13,
 'atomic-swaps': 14,
 'avalanche-ecosystem': 15,
 'binance-chain': 16,
 'binance-labs-portfolio': 17,
 'binance-launchpad': 18,
 'binance-launchpool': 19,
 'binance-smart-chain': 20,
 'blake': 21,
 'blake256': 22,
 'blake2b': 23,
 'blake2s': 24,
 'blockchain-capital-portfolio': 25,
 'boostvc-portfolio': 26,
 'centralized-exchange': 27,
 'cms-holdings-portfolio': 28,
 'coinbase-ventures-portfolio': 29,
 'coinfund-portfolio': 30,
 'collectibles-nfts': 31,
 'commodities': 32,
 'communications-social-media': 33,
 'content-creation': 34,
 'cosmos': 35,
 'cosmos-ecosystem': 36,
 'crowdfunding': 37,
 'crowdsourcing': 38,
 'cryptonight': 39,
 'cryptonight-lite': 40,
 'cuckoo-cycle': 41,
 'cybersecurity': 42

In [12]:
all_symbol_tags = []
for st in symbol_tags:
    tag = [''] * (len(tag_map) + 2)
    tag[0] = st[0]
    tag[1] = st[1]
    for t in st[2]:
        index = tag_map[t]
        tag[index + 2] = 1
    all_symbol_tags.append(tag)
        

In [246]:
all_symbol_tags

[['BTC',
  'Bitcoin',
  1,
  1,
  '',
  '',
  '',
  '',
  1,
  '',
  '',
  '',
  1,
  '',
  '',
  '',
  '',
  '',
  '',
  1,
  '',
  '',
  '',
  '',
  '',
  '',
  '',
  1,
  1,
  '',
  1,
  1,
  '',
  '',
  '',
  '',
  '',
  '',
  '',
  '',
  '',
  '',
  '',
  '',
  '',
  '',
  '',
  '',
  '',
  '',
  '',
  '',
  1,
  '',
  '',
  '',
  '',
  '',
  '',
  '',
  '',
  '',
  1,
  '',
  '',
  1,
  '',
  '',
  '',
  '',
  '',
  '',
  '',
  '',
  '',
  '',
  1,
  '',
  '',
  '',
  '',
  '',
  1,
  1,
  '',
  '',
  '',
  '',
  '',
  '',
  '',
  '',
  '',
  '',
  1,
  '',
  '',
  '',
  '',
  '',
  '',
  '',
  '',
  '',
  '',
  '',
  '',
  '',
  '',
  '',
  '',
  '',
  '',
  '',
  '',
  '',
  '',
  '',
  '',
  '',
  '',
  '',
  '',
  '',
  '',
  '',
  '',
  1,
  '',
  1,
  '',
  '',
  '',
  '',
  '',
  '',
  '',
  1,
  1,
  '',
  '',
  '',
  1,
  '',
  '',
  '',
  '',
  '',
  '',
  1,
  '',
  '',
  '',
  '',
  '',
  1,
  '',
  '',
  '',
  '',
  '',
  '',
  '',
  '',
  '',
  '',
  '',
  '',
  '',

In [14]:
columns = ['symbol','name']
columns.extend(all_tags)
columns

['symbol',
 'name',
 '1confirmation-portfolio',
 'a16z-portfolio',
 'aave-tokens',
 'adult',
 'agriculture',
 'ai-big-data',
 'alameda-research-portfolio',
 'amm',
 'analytics',
 'argon2',
 'arrington-xrp-capital',
 'art',
 'asset-backed-coin',
 'asset-management',
 'atomic-swaps',
 'avalanche-ecosystem',
 'binance-chain',
 'binance-labs-portfolio',
 'binance-launchpad',
 'binance-launchpool',
 'binance-smart-chain',
 'blake',
 'blake256',
 'blake2b',
 'blake2s',
 'blockchain-capital-portfolio',
 'boostvc-portfolio',
 'centralized-exchange',
 'cms-holdings-portfolio',
 'coinbase-ventures-portfolio',
 'coinfund-portfolio',
 'collectibles-nfts',
 'commodities',
 'communications-social-media',
 'content-creation',
 'cosmos',
 'cosmos-ecosystem',
 'crowdfunding',
 'crowdsourcing',
 'cryptonight',
 'cryptonight-lite',
 'cuckoo-cycle',
 'cybersecurity',
 'dag',
 'dagger-hashimoto',
 'dao',
 'dao-maker',
 'dapp',
 'data-availability-proof',
 'data-provenance',
 'dcg-portfolio',
 'decentralize

In [15]:
len(columns)

220

In [16]:
df = pd.DataFrame(all_symbol_tags, columns=columns)

In [17]:
df

symbol                              name 1confirmation-portfolio  \
0        BTC                           Bitcoin                       1   
1        ETH                          Ethereum                       1   
2        BNB                      Binance Coin                           
3       USDT                            Tether                           
4        ADA                           Cardano                           
...      ...                               ...                     ...   
4565   MAYFI   Matic Aave Interest Bearing YFI                           
4566  MALINK  Matic Aave Interest Bearing LINK                           
4567  WMATIC                     Wrapped Matic                           
4568   DELTA                             Delta                           
4569   wxDai                      Wrapped XDAI                           

     a16z-portfolio aave-tokens adult agriculture ai-big-data  \
0                 1                                             
1                 1                                             
2                                                               
3                                                               
4                                                               
...             ...         ...   ...         ...         ...   
4565                                                            
4566                                                            
4567                                                            
4568                                                            
4569                                                            

     alameda-research-portfolio amm  ... x11gost x13 x14 x15 xevan  \
0                             1      ...                             
1                             1      ...                             
2                             1      ...                             
3                                    ...                             
4                                    ...                             
...                         ...  ..  ...     ...  ..  ..  ..   ...   
4565                                 ...                             
4566                                 ...                             
4567                                 ...                             
4568                                 ...                             
4569                                 ...                             

     yearn-partnerships yescript yield-aggregator yield-farming  \
0                                                                 
1                                                                 
2                                                                 
3                                                                 
4                                                                 
...                 ...      ...              ...           ...   
4565                                                              
4566                                                              
4567                                                              
4568                                                              
4569                                                              

     zero-knowledge-proofs  
0                           
1                           
2                           
3                           
4                           
...                    ...  
4565                        
4566                        
4567                        
4568                        
4569                        

[4570 rows x 220 columns]

In [18]:
len(df.name.unique())

4564

In [19]:
df.shape

(4570, 220)

In [20]:
df.sort_values(['symbol'])

symbol                    name 1confirmation-portfolio  \
777                     $ANRX                AnRKey X                           
3433                   $BASED             Based Money                           
2977                    $COIN                    COIN                           
2587                    $KING               King Swap                           
2248                    $NOOB            noob.finance                           
...                       ...                     ...                     ...   
4430                    xMOON  r/CryptoCurrency Moons                           
4440                     yBAN               BananoDOS                           
3717                   yPANDA      YieldPanda Finance                           
2119                    yTSLA           yTSLA Finance                           
3675  yVault LP-yCurve(YYCRV)        yVault LP-yCurve                           

     a16z-portfolio aave-tokens adult agriculture ai-big-data  \
777                                                             
3433                                                            
2977                                                            
2587                                                            
2248                                                            
...             ...         ...   ...         ...         ...   
4430                                                            
4440                                                            
3717                                                            
2119                                                            
3675                                                            

     alameda-research-portfolio amm  ... x11gost x13 x14 x15 xevan  \
777                                  ...                             
3433                                 ...                             
2977                                 ...                             
2587                                 ...                             
2248                                 ...                             
...                         ...  ..  ...     ...  ..  ..  ..   ...   
4430                                 ...                             
4440                                 ...                             
3717                                 ...                             
2119                                 ...                             
3675                                 ...                             

     yearn-partnerships yescript yield-aggregator yield-farming  \
777                                                               
3433                                                          1   
2977                                                              
2587                                                              
2248                                                              
...                 ...      ...              ...           ...   
4430                                                              
4440                                                              
3717                                                              
2119                                                              
3675                                                          1   

     zero-knowledge-proofs  
777                         
3433                        
2977                        
2587                        
2248                        
...                    ...  
4430                        
4440                        
3717                        
2119                        
3675                        

[4570 rows x 220 columns]

In [21]:
df = df.drop_duplicates(subset=['symbol','name'])

In [22]:
df.to_csv('cmc_symbols_tags.csv')

In [24]:
def __connect__():
    db_user = 'coin'
    db_password = 'dragonstone#123'
    db_name = 'master_data'
    db_host = 'localhost'
    return pymysql.connect(
        unix_socket=None,
        host=db_host,
        user=db_user,
        password=db_password,
        db=db_name,
        charset='latin1',
        cursorclass=pymysql.cursors.DictCursor)


def get_cursor(connection):
    if connection is None:
        connection = __connect__()
    connection.ping(reconnect=True)
    return connection.cursor()



In [30]:
sql = 'select * from cmc_symbols_names'


In [31]:
df = pd.read_sql_query(sql, __connect__())

In [33]:
df = df[df['count'] > 1]

In [146]:
df = df.reset_index()
del df['index']

In [147]:
df

symbol                        names  count
0     ACM  AC Milan Fan Token,Actinium      2
1    AUTO                    Auto,Cube      2
2     BDP   BidiPass,Big Data Protocol      2
3     BFC    Bifrost,Bitcoin Free Cash      2
4    BIFI   Beefy.Finance,Bitcoin File      2
..    ...                          ...    ...
58    TOP                TokenSwap,TOP      2
59    ULT           Shardus,Ultiledger      2
60   WING                Wing,WingShop      2
61    XIN     Infinity Economics,Mixin      2
62    XOR               Oracolxor,Sora      2

[63 rows x 3 columns]

In [35]:
api_key = "a86e3326-8c8d-434e-897a-5d6becbf1f35"

In [120]:
def fetch_top_n_market_cap_symbols_(url, aux, symbol=None, slug=None):
    payload = {
        'aux':aux,
        'symbol':symbol,
        'slug': slug
    }
    headers = {
      'Accepts': 'application/json',
      'X-CMC_PRO_API_KEY': api_key
    }
    
    response = requests.get(url, params=payload, headers=headers).json()
    return response

In [207]:
aux = 'urls,logo,description,tags,platform,date_added,notice,status'
url = 'https://pro-api.coinmarketcap.com/v1/cryptocurrency/info'

In [208]:
def get_current_name(symbol):
    json = fetch_top_n_market_cap_symbols_(url, aux, symbol=symbol)
    current_name = json['data'][symbol]['name']
    return current_name
    

In [209]:
def get_slug_category(slug):
    json = fetch_top_n_market_cap_symbols_(url, aux, slug=slug)
    for key in json['data']:
        return [json['data'][key]['category'], json['data'][key]['urls']['website'][0]]

In [239]:
get_slug_category('namecoin')

['coin', 'https://www.namecoin.org/']

In [241]:
fetch_top_n_market_cap_symbols_(url, aux, slug = 'terracoin')

{'status': {'timestamp': '2021-04-03T08:20:47.101Z',
  'error_code': 0,
  'error_message': None,
  'elapsed': 12,
  'credit_count': 1,
  'notice': None},
 'data': {'4': {'id': 4,
   'name': 'Terracoin',
   'symbol': 'TRC',
   'category': 'coin',
   'description': 'Terracoin (TRC) is a cryptocurrency . Users are able to generate TRC through the process of mining. Terracoin has a current supply of 22,935,396.430361. The last known price of Terracoin is 0.01595721 USD and is down -6.34 over the last 24 hours. It is currently trading on 2 active market(s) with $39.27 traded over the last 24 hours. More information can be found at http://www.terracoin.io/.',
   'slug': 'terracoin',
   'logo': 'https://s2.coinmarketcap.com/static/img/coins/64x64/4.png',
   'subreddit': 'terracoin',
   'notice': '',
   'tags': ['mineable', 'pow', 'sha-256', 'masternodes'],
   'tag-names': ['Mineable', 'PoW', 'SHA-256', 'Masternodes'],
   'tag-groups': ['OTHER',
    'CONSENSUS_ALGORITHM',
    'CONSENSUS_ALGORI

In [217]:
import urllib.parse

def get_host_url(url):
    parsed_url = urllib.parse.urlparse(url)
    host_breakup = parsed_url.netloc.split('.')
    url = f'{parsed_url.scheme}://{host_breakup[-2]}.{host_breakup[-1]}'
    print(url)
    return url
    

In [219]:
slug_map = {}
slug_map['BitZ Token'] = 'bit-z-token'
slug_map['Etherisc DIP Token'] = 'etherisc'
slug_map['EduMetrix Coin'] = 'edumetrix'
slug_map['nHBTC(N0001)'] = 'nhbtc'
slug_map['Netflix tokenized stock Mirror'] = 'mirrored-netflix'
slug_map['Tesla tokenized stock Mirror'] = 'mirrored-tesla'
slug_map['TON Token'] = 'tontoken'
slug_map['IQ.cash'] = 'iqcash'
slug_map[''] = ''
slug_map[''] = ''
slug_map[''] = ''

symbols_excluded = ['LOKI']


coins_info = []
for index, row in df.iterrows():
    if index < 0:
        continue
    time.sleep(2)
    symbol = row['symbol']
    names = row['names'].split(',')
    if symbol in symbols_excluded:
        continue
    current_name = get_current_name(symbol)
    for name in names:
        slug = slug_map[name] if name in slug_map else name.lower().replace(' ', '-').replace('(', '').replace(')', '').replace('.', '-')
        category = get_slug_category(slug)
        coins_info.append([symbol, category[0], get_host_url(category[1]), name, slug, current_name])
        

https://socios.com
https://actinium.org
https://autofarm.network
https://cubeint.io
https://bidipass.org
https://bigdataprotocol.com
https://thebifrost.io
https://bitfree.vip
https://beefy.finance
https://bitcoinfile.org
https://bounce.finance
https://bounce.finance
https://batdollar.fi
https://bitshares.org
https://ftx.com
http://buysellcoin.org
https://getbux.com
https://buxcoins.com
https://bitz.top
https://bitz.top
https://carryprotocol.io
https://cybereits.com
https://creditcoin.org
http://ctchain.cc
https://deipool.io
https://etherisc.com
https://encrypgen.com
https://mvsdna.com
https://doschain.org
https://dos.network
https://edgeless.io
https://edgewa.re
https://goosedefi.com
https://nesteggcoin.com
https://nestree.io
https://edumetrix.io
http://emercoin.com
https://factomprotocol.org
https://firmachain.org
http://geocoin.cash
https://geodb.com
https://get-protocol.io
https://themis.network
https://globalrentaltoken.com
https://goldenratiotoken.site
https://thegraph.com
https:/

In [220]:
coins_info_df = pd.DataFrame(coins_info, columns=['symbol', 'category', 'url', 'name', 'slug', 'symbol_search_name'])

In [221]:
coins_info_df

symbol category                            url                name  \
0      ACM    token             https://socios.com  AC Milan Fan Token   
1      ACM     coin           https://actinium.org            Actinium   
2     AUTO    token       https://autofarm.network                Auto   
3     AUTO    token             https://cubeint.io                Cube   
4      BDP    token           https://bidipass.org            BidiPass   
..     ...      ...                            ...                 ...   
123   WING    token            https://wingshop.io            WingShop   
124    XIN     coin  http://infinity-economics.org  Infinity Economics   
125    XIN    token              https://mixin.one               Mixin   
126    XOR     coin              http://oracol.org           Oracolxor   
127    XOR    token               https://sora.org                Sora   

                   slug  symbol_search_name  
0    ac-milan-fan-token  AC Milan Fan Token  
1              actinium  AC Milan Fan Token  
2                  auto                Auto  
3                  cube                Auto  
4              bidipass   Big Data Protocol  
..                  ...                 ...  
123            wingshop                Wing  
124  infinity-economics               Mixin  
125               mixin               Mixin  
126           oracolxor                Sora  
127                sora                Sora  

[128 rows x 6 columns]

In [231]:
group_df = coins_info_df.groupby(['url', 'symbol'])

In [232]:
df2 = group_df.count()

In [233]:
df2[df2['slug'] > 1]

category  name  slug  symbol_search_name
url                    symbol                                          
http://syntropynet.com NOIA           2     2     2                   2
https://bitz.top       BZ             2     2     2                   2
https://bounce.finance BOT            2     2     2                   2
https://hifi.finance   MFT            2     2     2                   2
https://matic.network  MATIC          2     2     2                   2
https://mirror.finance mNFLX          2     2     2                   2
                       mTSLA          2     2     2                   2
https://stacks.co      STX            2     2     2                   2
https://ternio.io      TERN           2     2     2                   2

In [237]:
coins_info_df[coins_info_df['url'] == 'https://ternio.io']

symbol category                url            name          slug  \
112   TERN    token  https://ternio.io          Ternio        ternio   
113   TERN    token  https://ternio.io  Ternio (ERC20)  ternio-erc20   

    symbol_search_name  
112       Ternio-ERC20  
113       Ternio-ERC20

In [245]:
coins_info_df[coins_info_df['name'] == 'Rio DeFi']

Empty DataFrame
Columns: [symbol, category, url, name, slug, symbol_search_name]
Index: []

### Trello Card: https://trello.com/c/L7sTXLQQ/27-add-columns-at-the-end-of-masterdataratiosandpercentages20210331-report-for-tags

In [247]:
required_tags = ['binance-smart-chain','polkadot-ecosystem','ethereum','cosmos-ecosystem','polkadot','solana-ecosystem','binance-chain','avalanche-ecosystem','heco','layer-2','eos','sidechain','cosmos','tron','defi','yield-farming','decentralized-exchange','governance','dao','gaming','stablecoin','asset-management','centralized-exchange','staking','yield-aggregator','oracles','lending-borowing','dex','options','launchpad','stablecoin-algorithmically-stabilized']


In [248]:
required_tags.sort()
required_tags

['asset-management',
 'avalanche-ecosystem',
 'binance-chain',
 'binance-smart-chain',
 'centralized-exchange',
 'cosmos',
 'cosmos-ecosystem',
 'dao',
 'decentralized-exchange',
 'defi',
 'dex',
 'eos',
 'ethereum',
 'gaming',
 'governance',
 'heco',
 'launchpad',
 'layer-2',
 'lending-borowing',
 'options',
 'oracles',
 'polkadot',
 'polkadot-ecosystem',
 'sidechain',
 'solana-ecosystem',
 'stablecoin',
 'stablecoin-algorithmically-stabilized',
 'staking',
 'tron',
 'yield-aggregator',
 'yield-farming']

In [250]:
def __connect__():
    db_user = 'coin'
    db_password = 'dragonstone#123'
    db_name = 'master_data'
    db_host = 'localhost'
    return pymysql.connect(
        unix_socket=None,
        host=db_host,
        user=db_user,
        password=db_password,
        db=db_name,
        charset='latin1',
        cursorclass=pymysql.cursors.DictCursor)


def get_cursor(connection):
    if connection is None:
        connection = __connect__()
    connection.ping(reconnect=True)
    return connection.cursor()

sql = 'select * from master_data_view6_master'
data_df = pd.read_sql_query(sql, __connect__())

In [253]:
data_df

date              Name Symbol        Price  Marketcap CMC  \
0     2020-12-21         ABBC Coin   ABBC     0.227925   1.912421e+08   
1     2020-12-21          Actinium    ACM     0.007630   2.060344e+05   
2     2020-12-21           Cardano    ADA     0.152656   4.749512e+09   
3     2020-12-21      Aidos Kuneen    ADK     0.238089   5.952225e+06   
4     2020-12-21      AdEx Network    ADX     0.291127   3.137552e+07   
...          ...               ...    ...          ...            ...   
68247 2021-04-03        OptionRoom   ROOM     2.229825   2.719901e+07   
68248 2021-04-03  Umbrella Network    UMB     1.264613   2.312031e+07   
68249 2021-04-03         Venus BTC   vBTC  1152.472084   2.372202e+08   
68250 2021-04-03         YIELD App    YLD     0.756647   6.997665e+07   
68251 2021-04-03           yOUcash   YOUC     0.049545   8.551666e+07   

         Volume CMC  Circulating Supply CMC  Total Supply CMC  MAX Supply CMC  \
0      4.320631e+07            8.390575e+08      1.500000e+09    1.500000e+09   
1      2.618798e+05            2.700165e+07      2.700165e+07    8.400000e+07   
2      1.139902e+09            3.111248e+10      4.500000e+10    4.500000e+10   
3      1.737466e+06            2.500000e+07      2.500000e+07             NaN   
4      6.120680e+06            1.077725e+08      1.149150e+08    1.500000e+08   
...             ...                     ...               ...             ...   
68247  1.921732e+06            1.219782e+07      0.000000e+00    1.000000e+08   
68248  1.934452e+06            1.828251e+07      5.640509e+07    4.640509e+07   
68249  0.000000e+00            2.058360e+05      2.058360e+05             NaN   
68250  1.765022e+06            9.248250e+07      1.068717e+08    3.000000e+08   
68251  3.170457e+04            1.726054e+09      1.100000e+10    1.100000e+10   

         TVL Debank  ...    Price/Sale  Transaction GMV  Interest GMV  \
0               NaN  ...           NaN              NaN           NaN   
1               NaN  ...           NaN              NaN           NaN   
2               NaN  ...  49868.018928     3.639961e+08           NaN   
3               NaN  ...           NaN              NaN           NaN   
4               NaN  ...           NaN              NaN           NaN   
...             ...  ...           ...              ...           ...   
68247           NaN  ...           NaN              NaN           NaN   
68248           NaN  ...           NaN              NaN           NaN   
68249           NaN  ...           NaN              NaN           NaN   
68250  5.123732e+06  ...           NaN              NaN           NaN   
68251           NaN  ...           NaN              NaN           NaN   

       Users 24hr Debank  Transactions Count Debank  Trading Volume Debank  \
0                    NaN                        NaN                    NaN   
1                    NaN                        NaN                    NaN   
2                    NaN                        NaN                    NaN   
3                    NaN                        NaN                    NaN   
4                    NaN                        NaN                    NaN   
...                  ...                        ...                    ...   
68247                NaN                        NaN                    NaN   
68248                NaN                        NaN                    NaN   
68249                NaN                        NaN                    NaN   
68250                NaN                        NaN                    NaN   
68251                NaN                        NaN                    NaN   

       Borrowing Volume Debank  Users life-to-date duneanlytics  \
0                          NaN                              NaN   
1                          NaN                              NaN   
2                          NaN                              NaN   
3                          NaN                              NaN   
4            

In [259]:
df = pd.DataFrame(data_df['Tags'].copy())

In [260]:
df

Tags
0                        mineable,dpos,platform,payments
1                                               mineable
2      mineable,dpos,pos,platform,research,smart-cont...
3                                                       
4      marketing,smart-contracts,substrate,polkadot,p...
...                                                  ...
68247  oracles,prediction-markets,polkadot-ecosystem,...
68248                          defi,oracles,polkastarter
68249                                                   
68250                                                   
68251                                                   

[68252 rows x 1 columns]

In [261]:
required_tags_map = {}
i = 0
for tag in required_tags:
    required_tags_map[tag] = i
    i = i + 1

In [262]:
required_tags_map

{'asset-management': 0,
 'avalanche-ecosystem': 1,
 'binance-chain': 2,
 'binance-smart-chain': 3,
 'centralized-exchange': 4,
 'cosmos': 5,
 'cosmos-ecosystem': 6,
 'dao': 7,
 'decentralized-exchange': 8,
 'defi': 9,
 'dex': 10,
 'eos': 11,
 'ethereum': 12,
 'gaming': 13,
 'governance': 14,
 'heco': 15,
 'launchpad': 16,
 'layer-2': 17,
 'lending-borowing': 18,
 'options': 19,
 'oracles': 20,
 'polkadot': 21,
 'polkadot-ecosystem': 22,
 'sidechain': 23,
 'solana-ecosystem': 24,
 'stablecoin': 25,
 'stablecoin-algorithmically-stabilized': 26,
 'staking': 27,
 'tron': 28,
 'yield-aggregator': 29,
 'yield-farming': 30}

In [278]:
all_symbol_tags = []
for index, row in df.iterrows():
    tag = [''] * (len(required_tags))
    tags = row['Tags']
    tags = tags.split(',')
    for t in tags:
        index = required_tags_map[t] if t in required_tags_map else -1
        if index > -1:
            tag[index] = 1
    all_symbol_tags.append(tag)
        

In [279]:
all_symbol_tags

[['',
  '',
  '',
  '',
  '',
  '',
  '',
  '',
  '',
  '',
  '',
  '',
  '',
  '',
  '',
  '',
  '',
  '',
  '',
  '',
  '',
  '',
  '',
  '',
  '',
  '',
  '',
  '',
  '',
  '',
  ''],
 ['',
  '',
  '',
  '',
  '',
  '',
  '',
  '',
  '',
  '',
  '',
  '',
  '',
  '',
  '',
  '',
  '',
  '',
  '',
  '',
  '',
  '',
  '',
  '',
  '',
  '',
  '',
  '',
  '',
  '',
  ''],
 ['',
  '',
  1,
  '',
  '',
  '',
  '',
  '',
  '',
  '',
  '',
  '',
  '',
  '',
  '',
  '',
  '',
  '',
  '',
  '',
  '',
  '',
  '',
  '',
  '',
  '',
  '',
  1,
  '',
  '',
  ''],
 ['',
  '',
  '',
  '',
  '',
  '',
  '',
  '',
  '',
  '',
  '',
  '',
  '',
  '',
  '',
  '',
  '',
  '',
  '',
  '',
  '',
  '',
  '',
  '',
  '',
  '',
  '',
  '',
  '',
  '',
  ''],
 ['',
  '',
  '',
  '',
  '',
  '',
  '',
  '',
  '',
  '',
  '',
  '',
  '',
  '',
  '',
  '',
  '',
  '',
  '',
  '',
  '',
  1,
  1,
  '',
  '',
  '',
  '',
  '',
  '',
  '',
  ''],
 ['',
  '',
  '',
  '',
  '',
  '',
  '',
  '',
  '',
  '',
  '',
  '

In [280]:
columns = []
columns.extend(required_tags)
columns

['asset-management',
 'avalanche-ecosystem',
 'binance-chain',
 'binance-smart-chain',
 'centralized-exchange',
 'cosmos',
 'cosmos-ecosystem',
 'dao',
 'decentralized-exchange',
 'defi',
 'dex',
 'eos',
 'ethereum',
 'gaming',
 'governance',
 'heco',
 'launchpad',
 'layer-2',
 'lending-borowing',
 'options',
 'oracles',
 'polkadot',
 'polkadot-ecosystem',
 'sidechain',
 'solana-ecosystem',
 'stablecoin',
 'stablecoin-algorithmically-stabilized',
 'staking',
 'tron',
 'yield-aggregator',
 'yield-farming']

In [281]:
df2 = pd.DataFrame(all_symbol_tags, columns = columns)

In [282]:
df2

asset-management avalanche-ecosystem binance-chain binance-smart-chain  \
0                                                                              
1                                                                              
2                                                      1                       
3                                                                              
4                                                                              
...                ...                 ...           ...                 ...   
68247                                                                          
68248                                                                          
68249                                                                          
68250                                                                          
68251                                                                          

      centralized-exchange cosmos cosmos-ecosystem dao decentralized-exchange  \
0                                                                               
1                                                                               
2                                                                               
3                                                                               
4                                                                               
...                    ...    ...              ...  ..                    ...   
68247                                                                           
68248                                                                           
68249                                                                           
68250                                                                           
68251                                                                           

      defi  ... polkadot polkadot-ecosystem sidechain solana-ecosystem  \
0           ...                                                          
1           ...                                                          
2           ...                                                          
3           ...                                                          
4           ...        1                  1                              
...    ...  ...      ...                ...       ...              ...   
68247       ...                           1                              
68248    1  ...                                                          
68249       ...                                                          
68250       ...                                                          
68251       ...                                                          

      stablecoin stablecoin-algorithmically-stabilized staking tron  \
0                                                                     
1                                                                     
2                                                            1        
3                                                                     
4                                                                     
...          ...                                   ...     ...  ...   
68247                                                                 
68248                                                                 
68249                                                                 
68250                                                                 
68251                                                                 

      yield-aggregator yield-farming  
0                                     
1                                     
2                                     
3                                     
4                                     
...                ...           ...  
68247                                 
68248             

In [286]:
data_df = data_df.join(df2)

In [288]:
del data_df['Tags']

KeyError: 'Tags'

In [287]:
data_df.columns

Index(['date', 'Name', 'Symbol', 'Price', 'Marketcap CMC', 'Volume CMC',
       'Circulating Supply CMC', 'Total Supply CMC', 'MAX Supply CMC',
       'TVL Debank', 'TVL Defipulse', 'Transaction Revenue',
       'Interest Revenue', 'Transaction Revenue Supply Side',
       'Interest Revenue Supply Side', 'Transaction Revenue Protocol',
       'Interest Revenue Protocol', 'Price/Sale', 'Transaction GMV',
       'Interest GMV', 'Users 24hr Debank', 'Transactions Count Debank',
       'Trading Volume Debank', 'Borrowing Volume Debank',
       'Users life-to-date duneanlytics', 'CoinUrl', 'asset-management',
       'avalanche-ecosystem', 'binance-chain', 'binance-smart-chain',
       'centralized-exchange', 'cosmos', 'cosmos-ecosystem', 'dao',
       'decentralized-exchange', 'defi', 'dex', 'eos', 'ethereum', 'gaming',
       'governance', 'heco', 'launchpad', 'layer-2', 'lending-borowing',
       'options', 'oracles', 'polkadot', 'polkadot-ecosystem', 'sidechain',
       'solana-ecosystem

## Trello Card: https://trello.com/c/pxrM2n2C/25-name-change-db-master-name

In [313]:
df = pd.read_csv('cmc_coin_name_change_sheet.csv')

In [314]:
df = df[df['name'] != df['current_name']]

In [316]:
df

name symbol               current_name  is_dead  \
1                BetProtocol  BEPRO              BEPRO Network      NaN   
2          Bitcoin Free Cash    BFC              Bifrost (BFC)      NaN   
3                    Bifrost    BFC              Bifrost (BFC)      NaN   
5               BitMax Token   BTMX                       BTMX      NaN   
6    AscendEX (BitMax) Token   BTMX                       BTMX      NaN   
8                Bit-Z Token     BZ                 BitZ Token      NaN   
10       COVER Protocol[old]  COVER             COVER Protocol      NaN   
13                 DerivaDEX    DDX                  DerivaDAO      NaN   
14        Unit Protocol Duck   DUCK  Duck DAO (DLP Duck Token)      NaN   
15  Duck DAO (DLP Duck Token   DUCK  Duck DAO (DLP Duck Token)      NaN   
17                  Duck DAO   DUCK  Duck DAO (DLP Duck Token)      NaN   
19        Flow (Dapper labs)   FLOW                       Flow      NaN   
20              nHBTC(N0001)   HBTC                  Huobi BTC      NaN   
22                 ichi.farm   ICHI                       ICHI      NaN   
24                     Joule    JUL              JustLiquidity      NaN   
26             KuCoin Shares    KCS               KuCoin Token      NaN   
28             Matic Network  MATIC                    Polygon      NaN   
30                 Mainframe    MFT               Hifi Finance      NaN   
33                     Melon    MLN                     Enzyme      NaN   
35                  Mooncoin   MOON                   MoonSwap      NaN   
36             Nash Exchange    NEX                       Nash      NaN   
38                   Pundi X   NPXS               Pundi X[new]      NaN   
39                PAC Global    PAC               PAC Protocol      NaN   
41                     Paint  PAINT                     MurAll      NaN   
43             Phala.Network    PHA              Phala Network      NaN   
46                    PCHAIN     PI                      Plian      NaN   
48            Roti Bank Coin    RBC                      Rubic      NaN   
49                  Rio DeFi  RFUEL                    RioDeFi      NaN   
51      Social Lending Token    SLT         Smartlands Network      NaN   
53   StakeHound Staked Ether  STETH               stETH (Lido)      NaN   
55                     stETH  STETH               stETH (Lido)      NaN   
56                      Stox    STX                     Stacks      NaN   
57                Blockstack    STX                     Stacks      NaN   
59                    inSure   SURE                inSure DeFi      NaN   
61                TrustToken    TRU                     TrueFi      NaN   
63       Terra Virtua Kolekt    TVK        Terra Virtua Kolect      NaN   
65                Tixl [NEW]    TXL                       Tixl      NaN   

   new_symbol  
1         NaN  
2         NaN  
3         NaN  
5         NaN  
6         NaN  
8         NaN  
10        NaN  
13        NaN  
14        NaN  
15        NaN  
17        NaN  
19        NaN  
20        NaN  
22        NaN  
24        NaN  
26        NaN  
28        NaN  
30        NaN  
33        NaN  
35        NaN  
36        NaN  
38     PUNDIX  
39        NaN  
41        NaN  
43        NaN  
46        NaN  
48        NaN  
49        NaN  
51        NaN  
53        NaN  
55        NaN  
56        NaN  
57        NaN  
59        NaN  
61        NaN  
63        NaN  
65        NaN

In [301]:
symbols = list(df['symbol'].unique())

In [305]:
symbols_str = ",".join([f"'{s}'" for s in symbols])

In [309]:
sql = f'select * from cmc_coin_metainfo where symbol in ({symbols_str})'

In [310]:
sql

"select * from cmc_coin_metainfo where symbol in ('BEPRO','BFC','BTMX','BZ','COVER','DDX','DUCK','FLOW','HBTC','ICHI','JUL','KCS','MATIC','MFT','MLN','MOON','NEX','NPXS','PAC','PAINT','PHA','PI','RBC','RFUEL','SLT','STETH','STX','SURE','TRU','TVK','TXL')"

In [317]:
df2 = pd.read_sql_query(sql, __connect__())

In [318]:
df2

cmc_id                       name               current_name symbol  \
0     1107               PAC Protocol               PAC Protocol    PAC   
1     1552                     Enzyme                     Enzyme    MLN   
2     1861                       Stox                       Stox    STX   
3     2087               KuCoin Token               KuCoin Token    KCS   
4     2471         Smartlands Network         Smartlands Network    SLT   
5     2603               Pundi X[old]               Pundi X[old]   NPXS   
6     2838                      Plian                      Plian     PI   
7     2896               Hifi Finance               Hifi Finance    MFT   
8     2918                 BitZ Token                 BitZ Token     BZ   
9     3673                       BTMX                       BTMX   BTMX   
10    3829                       Nash                       Nash    NEX   
11    3890                    Polygon                    Polygon  MATIC   
12    4558                       Flow                       Flow   FLOW   
13    4847                     Stacks                     Stacks    STX   
14    5051          Bitcoin Free Cash          Bitcoin Free Cash    BFC   
15    5062              BEPRO Network              BEPRO Network  BEPRO   
16    5113                inSure DeFi                inSure DeFi   SURE   
17    6537                    RioDeFi                    RioDeFi  RFUEL   
18    6841              Phala Network              Phala Network    PHA   
19    6937              JustLiquidity              JustLiquidity    JUL   
20    6941                  Huobi BTC                  Huobi BTC   HBTC   
21    7017                   MoonSwap                   MoonSwap   MOON   
22    7024                       Tixl                       Tixl    TXL   
23    7219                      Rubic                      Rubic    RBC   
24    7228                  DerivaDAO                  DerivaDAO    DDX   
25    7432              Bit Financial              Bit Financial    BFC   
26    7725                     TrueFi                     TrueFi    TRU   
27    7726                       ICHI                       ICHI   ICHI   
28    7817              Bifrost (BFC)              Bifrost (BFC)    BFC   
29    7977         Unit Protocol Duck         Unit Protocol Duck   DUCK   
30    8037        Terra Virtua Kolect        Terra Virtua Kolect    TVK   
31    8063  Duck DAO (DLP Duck Token)  Duck DAO (DLP Duck Token)   DUCK   
32    8085               stETH (Lido)               stETH (Lido)  STETH   
33    8175             COVER Protocol             COVER Protocol  COVER   
34    8311    StakeHound Staked Ether    StakeHound Staked Ether  STETH   
35    8647                     MurAll                     MurAll  PAINT   

                       slug is_active category                         url  \
0              pac-protocol   b'\x01'     coin        https://pacglobal.io   
1                    enzyme   b'\x01'    token      https://enzyme.finance   
2                      stox   b'\x01'    token            https://stox.com   
3              kucoin-token   b'\x01'    token          https://kucoin.com   
4        smartlands-network   b'\x01'    token   http://smartlands.network   
5                   pundi-x   b'\x01'    token          https://pundix.com   
6                    pchain   b'\x01'     coin           https://plian.org   
7                 mainframe   b'\x01'    token        https://hifi.finance   
8               bit-z-token   b'\x01'    token            https://bitz.top   
9              bitmax-token   b'\x01'    token         https://ascendex.io   
10            nash-exchange   b'\x01'    token             https://nash.io   
11                  polygon   b'\x01'    token       https://matic.network   
12                     flow   b'\x01'     coin          https://onflow.org   
13                   stacks   b'\x01'     coin           https://stacks.co   
14        bitcoin-free-cash   b'\x01'     coin         htt

In [356]:
def get_coin_metainfo(df, symbol):
    cmc_id = df[df['symbol'] == symbol]['cmc_id'].max()
    print(cmc_id)
    df = df[df['cmc_id'] == int(cmc_id)]
    return df.values.tolist()[0]

In [359]:
metainfos = []
for index, row in df.iterrows():
    name = row['name']
    symbol = row['symbol']
    new_meta_info = get_coin_metainfo(df2, symbol)
    new_meta_info[1] = name
    metainfos.append(new_meta_info)

5062
7817
7817
3673
3673
2918
8175
7228
8063
8063
8063
4558
6941
7726
6937
2087
3890
2896
1552
7017
3829
2603
1107
8647
6841
2838
7219
6537
2471
8311
8311
4847
4847
5113
7725
8037
7024


In [360]:
metainfos

[[5062,
  'BetProtocol',
  'BEPRO Network',
  'BEPRO',
  'bepro-network',
  b'\x01',
  'token',
  'https://bepro.network',
  'gambling,defi,polkadot-ecosystem'],
 [7817,
  'Bitcoin Free Cash',
  'Bifrost (BFC)',
  'BFC',
  'bifrost',
  b'\x01',
  'token',
  'https://thebifrost.io',
  'platform,interoperability'],
 [7817,
  'Bifrost',
  'Bifrost (BFC)',
  'BFC',
  'bifrost',
  b'\x01',
  'token',
  'https://thebifrost.io',
  'platform,interoperability'],
 [3673,
  'BitMax Token',
  'BTMX',
  'BTMX',
  'bitmax-token',
  b'\x01',
  'token',
  'https://ascendex.io',
  'centralized-exchange'],
 [3673,
  'AscendEX (BitMax) Token',
  'BTMX',
  'BTMX',
  'bitmax-token',
  b'\x01',
  'token',
  'https://ascendex.io',
  'centralized-exchange'],
 [2918,
  'Bit-Z Token',
  'BitZ Token',
  'BZ',
  'bit-z-token',
  b'\x01',
  'token',
  'https://bitz.top',
  'marketplace,discount-token,payments'],
 [8175,
  'COVER Protocol[old]',
  'COVER Protocol',
  'COVER',
  'cover-protocol-new',
  b'\x01',
  't

In [362]:
df3 = pd.DataFrame(metainfos, columns = df2.columns)

In [363]:
df3

cmc_id                      name               current_name symbol  \
0     5062               BetProtocol              BEPRO Network  BEPRO   
1     7817         Bitcoin Free Cash              Bifrost (BFC)    BFC   
2     7817                   Bifrost              Bifrost (BFC)    BFC   
3     3673              BitMax Token                       BTMX   BTMX   
4     3673   AscendEX (BitMax) Token                       BTMX   BTMX   
5     2918               Bit-Z Token                 BitZ Token     BZ   
6     8175       COVER Protocol[old]             COVER Protocol  COVER   
7     7228                 DerivaDEX                  DerivaDAO    DDX   
8     8063        Unit Protocol Duck  Duck DAO (DLP Duck Token)   DUCK   
9     8063  Duck DAO (DLP Duck Token  Duck DAO (DLP Duck Token)   DUCK   
10    8063                  Duck DAO  Duck DAO (DLP Duck Token)   DUCK   
11    4558        Flow (Dapper labs)                       Flow   FLOW   
12    6941              nHBTC(N0001)                  Huobi BTC   HBTC   
13    7726                 ichi.farm                       ICHI   ICHI   
14    6937                     Joule              JustLiquidity    JUL   
15    2087             KuCoin Shares               KuCoin Token    KCS   
16    3890             Matic Network                    Polygon  MATIC   
17    2896                 Mainframe               Hifi Finance    MFT   
18    1552                     Melon                     Enzyme    MLN   
19    7017                  Mooncoin                   MoonSwap   MOON   
20    3829             Nash Exchange                       Nash    NEX   
21    2603                   Pundi X               Pundi X[old]   NPXS   
22    1107                PAC Global               PAC Protocol    PAC   
23    8647                     Paint                     MurAll  PAINT   
24    6841             Phala.Network              Phala Network    PHA   
25    2838                    PCHAIN                      Plian     PI   
26    7219            Roti Bank Coin                      Rubic    RBC   
27    6537                  Rio DeFi                    RioDeFi  RFUEL   
28    2471      Social Lending Token         Smartlands Network    SLT   
29    8311   StakeHound Staked Ether    StakeHound Staked Ether  STETH   
30    8311                     stETH    StakeHound Staked Ether  STETH   
31    4847                      Stox                     Stacks    STX   
32    4847                Blockstack                     Stacks    STX   
33    5113                    inSure                inSure DeFi   SURE   
34    7725                TrustToken                     TrueFi    TRU   
35    8037       Terra Virtua Kolekt        Terra Virtua Kolect    TVK   
36    7024                Tixl [NEW]                       Tixl    TXL   

                       slug is_active category                        url  \
0             bepro-network   b'\x01'    token      https://bepro.network   
1                   bifrost   b'\x01'    token      https://thebifrost.io   
2                   bifrost   b'\x01'    token      https://thebifrost.io   
3              bitmax-token   b'\x01'    token        https://ascendex.io   
4              bitmax-token   b'\x01'    token        https://ascendex.io   
5               bit-z-token   b'\x01'    token           https://bitz.top   
6        cover-protocol-new   b'\x01'    token  https://coverprotocol.com   
7                 derivadao   b'\x01'    token      https://derivadex.com   
8                  duck-dao   b'\x01'    token         https://duckdao.io   
9                  duck-dao   b'\x01'    token         https://duckdao.io   
10                 duck-dao   b'\x01'    token         https://duckdao.io   
11                     flow   b'\x01'     coin         https://onflow.org   
12                huobi-btc   b'\x01'    token       https://hbtc.finance   
13                     ichi   b'\x01'    token          https://ichi.farm   
14            justliquidity   b'\x01

In [366]:
def __connect__():
    db_user = 'coin'
    db_password = 'dragonstone#123'
    db_name = 'master_data'
    db_host = 'localhost'
    return pymysql.connect(
        unix_socket=None,
        host=db_host,
        user=db_user,
        password=db_password,
        db=db_name,
        charset='latin1',
        cursorclass=pymysql.cursors.DictCursor)


def get_cursor(connection):
    if connection is None:
        connection = __connect__()
    connection.ping(reconnect=True)
    return connection.cursor()

def insert_symbols_meta_info(df):
    connection = __connect__()
    cursor = get_cursor(connection)
    for i, row in df.iterrows():
        try:
            print(row["cmc_id"], row["name"], row["current_name"], row["symbol"], row["slug"], row["is_active"], row["category"], row["url"], row["tags"])
            sql = "INSERT INTO `cmc_coin_metainfo` (`cmc_id`, `name`, `current_name`, `symbol`, `slug`, `is_active`, `category`, `url`, `tags`) VALUES (%s, %s, %s, %s, %s, %s, %s, %s, %s)"
            cursor.execute(sql, (row["cmc_id"], row["name"], row["current_name"], row["symbol"], row["slug"], row["is_active"], row["category"], row["url"], row["tags"]))
        except Exception:
            print(traceback2.format_exc())
    connection.commit()
    cursor.close()
    connection.close()

In [367]:
insert_symbols_meta_info(df3)

5062 BetProtocol BEPRO Network BEPRO bepro-network b'\x01' token https://bepro.network gambling,defi,polkadot-ecosystem
7817 Bitcoin Free Cash Bifrost (BFC) BFC bifrost b'\x01' token https://thebifrost.io platform,interoperability
7817 Bifrost Bifrost (BFC) BFC bifrost b'\x01' token https://thebifrost.io platform,interoperability
3673 BitMax Token BTMX BTMX bitmax-token b'\x01' token https://ascendex.io centralized-exchange
3673 AscendEX (BitMax) Token BTMX BTMX bitmax-token b'\x01' token https://ascendex.io centralized-exchange
2918 Bit-Z Token BitZ Token BZ bit-z-token b'\x01' token https://bitz.top marketplace,discount-token,payments
8175 COVER Protocol[old] COVER Protocol COVER cover-protocol-new b'\x01' token https://coverprotocol.com insurance,yearn-partnerships
7228 DerivaDEX DerivaDAO DDX derivadao b'\x01' token https://derivadex.com decentralized-exchange,defi,derivatives
8063 Unit Protocol Duck Duck DAO (DLP Duck Token) DUCK duck-dao b'\x01' token https://duckdao.io 
8063 Duc

In [368]:
sql = "select * from  master_data_view6A_master"

In [369]:
test_df = pd.read_sql_query(sql, __connect__())

In [370]:
test_df[test_df['Symbol'] == 'SURE']

date         Name Symbol     Price  Marketcap CMC  Volume CMC  \
493   2020-12-21  inSure DeFi   SURE  0.001968   7.003992e+06    12222.56   
1062  2020-12-22  inSure DeFi   SURE  0.003175   1.130382e+07    17965.42   
1757  2020-12-23  inSure DeFi   SURE  0.002120   7.546090e+06    11315.17   
2275  2020-12-24  inSure DeFi   SURE  0.002037   7.253591e+06    15563.68   
2975  2020-12-25  inSure DeFi   SURE  0.000987   3.514016e+06     1983.98   
3550  2020-12-26  inSure DeFi   SURE  0.003437   1.223835e+07    16353.07   
4254  2020-12-27  inSure DeFi   SURE  0.002510   8.940703e+06    17799.67   
4773  2020-12-28  inSure DeFi   SURE  0.001084   3.860320e+06     1914.23   
5484  2020-12-29  inSure DeFi   SURE  0.008731   3.111208e+07    54181.09   
6063  2020-12-30  inSure DeFi   SURE  0.019341   6.892180e+07    35954.83   
6778  2020-12-31  inSure DeFi   SURE  0.006443   2.296748e+07    37509.56   
7301  2021-01-01  inSure DeFi   SURE  0.007385   2.632655e+07    26672.88   
8021  2021-01-02  inSure DeFi   SURE  0.009146   3.260352e+07    37451.21   
8601  2021-01-03  inSure DeFi   SURE  0.011020   3.929432e+07    58495.59   
9272  2021-01-04  inSure DeFi   SURE  0.013607   4.851576e+07    73726.24   
9968  2021-01-05  inSure DeFi   SURE  0.002114   7.576083e+06     6858.33   
10495 2021-01-06  inSure DeFi   SURE  0.040537   1.452412e+08    77399.36   
11192 2021-01-07  inSure DeFi   SURE  0.001890   6.771502e+06     6633.35   
11847 2021-01-08  inSure DeFi   SURE  0.002117   7.597524e+06    44783.46   
12546 2021-01-09  inSure DeFi   SURE  0.005890   2.113874e+07    60263.46   
13074 2021-01-10  inSure DeFi   SURE  0.005209   1.869489e+07    66158.57   
13773 2021-01-11  inSure DeFi   SURE  0.005232   1.877628e+07    67982.90   
14427 2021-01-12  inSure DeFi   SURE  0.003711   1.332455e+07    28198.62   
15131 2021-01-13  inSure DeFi   SURE  0.002183   7.840535e+06    37975.78   
15660 2021-01-14  inSure DeFi   SURE  0.004388   1.577329e+07    97506.63   
16364 2021-01-15  inSure DeFi   SURE  0.004536   1.624751e+07    27491.96   
17023 2021-01-16  inSure DeFi   SURE  0.002792   9.999303e+06    17488.49   
17730 2021-01-17  inSure DeFi   SURE  0.006351   2.275452e+07    18288.80   
18260 2021-01-18  inSure DeFi   SURE  0.007232   2.589313e+07    82834.89   
18968 2021-01-19  inSure DeFi   SURE  0.005050   1.808150e+07   140603.29   
19631 2021-01-20  inSure DeFi   SURE  0.003537   1.267016e+07    46317.97   
20340 2021-01-21  inSure DeFi   SURE  0.004014   1.437803e+07   107881.30   
20870 2021-01-22  inSure DeFi   SURE  0.004007   1.435133e+07    92992.04   
21580 2021-01-23  inSure DeFi   SURE  0.007694   2.755935e+07   106478.48   
22248 2021-01-24  inSure DeFi   SURE  0.004201   1.504710e+07    35548.28   

       Circulating supply CMC  MAX Supply CMC  Total Supply CMC  TVL Debank  \
493              3.559703e+09    8.800000e+10      8.800000e+10         NaN   
1062             3.559703e+09    8.800000e+10      8.800000e+10         NaN   
1757             3.560249e+09    8.800000e+10      8.800000e+10         NaN   
2275             3.560249e+09    8.800000e+10      8.800000e+10         NaN   
2975             3.560249e+09    8.800000e+10      8.800000e+10         NaN   
3550             3.560249e+09    8.800000e+10      8.800000e+10         NaN   
4254             3.561369e+09    8.800000e+10      8.800000e+10         NaN   
4773             3.561359e+09    8.800000e+10      8.800000e+10         NaN   
5484             3.563571e+09    8.800000e+10      8.800000e+10         NaN   
6063             3.563571e+09    8.800000e+10      8.800000e+10         NaN   
6778             3.564717e+09    8.800000e+10      8.800000e+10         NaN   
7301             3.564717e+09    8.800000e+10      8.800000e+10         NaN   
8021             3.564661e+09    8.800000e+10      8.800000e+10         NaN   
8601             3.565625e+09    8.800000e+10      8.800000e+10         NaN   
9272             3.565625e+09    8.800000e+10      8.8

### https://trello.com/c/dUfs1Uf9/34-update-users-data-from-dune-thats-shared-on-slack

In [5]:
df = pd.read_csv('Total_Users_combined.csv')

In [6]:
df

date       0x     1inch     Aave  Augur  BadgerDAO  \
0     2017-12-18 00:00:00+00:00      NaN       NaN      NaN    NaN        NaN   
1     2017-12-19 00:00:00+00:00      NaN       NaN      NaN    NaN        NaN   
2     2017-12-20 00:00:00+00:00      NaN       NaN      NaN    NaN        NaN   
3     2017-12-21 00:00:00+00:00      NaN       NaN      NaN    NaN        NaN   
4     2017-12-22 00:00:00+00:00      NaN       NaN      NaN    NaN        NaN   
...                         ...      ...       ...      ...    ...        ...   
1208  2021-04-09 00:00:00+00:00  25776.0  175668.0  47520.0    NaN    10848.0   
1209  2021-04-10 00:00:00+00:00  25853.0  176321.0  47631.0    NaN    10865.0   
1210  2021-04-11 00:00:00+00:00  25907.0  176946.0  47772.0    NaN    10883.0   
1211  2021-04-12 00:00:00+00:00  25942.0  177492.0  47883.0    NaN    10888.0   
1212  2021-04-13 00:00:00+00:00  25962.0  177841.0  47936.0    NaN    10896.0   

      balancer   Bancor  compound   Cream  ...     Kyber  MakerDAO  \
0          NaN      NaN       NaN     NaN  ...       NaN      29.0   
1          NaN      NaN       NaN     NaN  ...       NaN      68.0   
2          NaN      NaN       NaN     NaN  ...       NaN      86.0   
3          NaN      NaN       NaN     NaN  ...       NaN     100.0   
4          NaN      NaN       NaN     NaN  ...       NaN     118.0   
...        ...      ...       ...     ...  ...       ...       ...   
1208  133223.0  19183.0  312716.0  8576.0  ...  120006.0   71028.0   
1209  133707.0  19225.0  312870.0  8589.0  ...  120042.0   71060.0   
1210  134062.0  19281.0  313053.0  8608.0  ...  120082.0   71103.0   
1211  134307.0  19337.0  313201.0  8617.0  ...  120113.0   71133.0   
1212  134493.0  19368.0  313285.0  8620.0  ...  120138.0       NaN   

      Nexus Mutual  PoolTogether     Ren  Set Protocol  SushiSwap  Synthetix  \
0              NaN           NaN     NaN           NaN        NaN        NaN   
1              NaN           NaN     NaN           NaN        NaN        NaN   
2              NaN           NaN     NaN           NaN        NaN        NaN   
3              NaN           NaN     NaN           NaN        NaN        NaN   
4              NaN           NaN     NaN           NaN        NaN        NaN   
...            ...           ...     ...           ...        ...        ...   
1208        4431.0       17987.0  9814.0           NaN   110668.0    16473.0   
1209        4438.0       18036.0  9833.0           NaN   111266.0    16483.0   
1210        4446.0       18097.0  9849.0           NaN   111947.0    16493.0   
1211        4453.0       18143.0  9863.0           NaN   112588.0    16502.0   
1212        4455.0       18174.0  9877.0           NaN   112950.0    16512.0   

        Uniswap  yearn_finance  
0           NaN            NaN  
1           NaN            NaN  
2           NaN            NaN  
3           NaN            NaN  
4           NaN            NaN  
...         ...            ...  
1208  1264993.0        29518.0  
1209  1270700.0        29577.0  
1210  1277156.0        29699.0  
1211  1283214.0        29761.0  
1212  1286579.0        29788.0  

[1213 rows x 27 columns]

In [7]:
df.columns

Index(['date', '0x', '1inch', 'Aave', 'Augur', 'BadgerDAO', 'balancer',
       'Bancor', 'compound', 'Cream', 'Curve', 'Defi', 'dYdX',
       'Harvest Finance', 'Hegic', 'InstaDApp', 'KeeperDAO', 'Kyber',
       'MakerDAO', 'Nexus Mutual', 'PoolTogether', 'Ren', 'Set Protocol',
       'SushiSwap', 'Synthetix', 'Uniswap', 'yearn_finance'],
      dtype='object')

In [10]:
columns = ['date', '0x', '1inch', 'Aave', 'Augur', 'BadgerDAO', 'Balancer',
       'Bancor', 'Compound', 'Cream', 'Curve', 'Defi', 'dYdX',
       'Harvest Finance', 'Hegic', 'InstaDApp', 'KeeperDAO', 'Kyber',
       'MakerDAO', 'Nexus Mutual', 'PoolTogether', 'Ren', 'Set Protocol',
       'SushiSwap', 'Synthetix', 'Uniswap', 'yearn_finance']

In [9]:
columns

['date',
 '0x',
 '1inch',
 'Aave',
 'Augur',
 'BadgerDAO',
 'balancer',
 'Bancor',
 'compound',
 'Cream',
 'Curve',
 'Defi',
 'dYdX',
 'Harvest Finance',
 'Hegic',
 'InstaDApp',
 'KeeperDAO',
 'Kyber',
 'MakerDAO',
 'Nexus Mutual',
 'PoolTogether',
 'Ren',
 'Set Protocol',
 'SushiSwap',
 'Synthetix',
 'Uniswap',
 'yearn_finance']

In [11]:
df.columns = columns

In [59]:
list(df.columns.values)

['date',
 '0x',
 '1inch',
 'Aave',
 'Augur',
 'BadgerDAO',
 'Balancer',
 'Bancor',
 'Compound',
 'Cream',
 'Curve',
 'Defi',
 'dYdX',
 'Harvest Finance',
 'Hegic',
 'InstaDApp',
 'KeeperDAO',
 'Kyber',
 'MakerDAO',
 'Nexus Mutual',
 'PoolTogether',
 'Ren',
 'Set Protocol',
 'SushiSwap',
 'Synthetix',
 'Uniswap',
 'yearn_finance']

In [60]:
columns = list(df.columns.values)

In [61]:
# from datetime import datetime
def insert_dune_total_users(df):
    connection = __connect__()
    cursor = get_cursor(connection)
    for i, row in df.iterrows():
        try:
            if row["total_users"] == None:
                continue
            dt = pd.to_datetime(row["date"]).timestamp()
            print(row["date"], row["symbol"], row["total_users"])
            sql = "INSERT INTO `dune_total_users_analysis2` (`timestamp_dt`, `symbol`, `total_users`) VALUES (FROM_UNIXTIME(%s), %s, %s)"
            cursor.execute(sql, (dt, row["symbol"], row["total_users"]))
        except Exception:
            print(traceback2.format_exc())
    connection.commit()
    cursor.close()
    connection.close()

In [62]:
all_df = pd.DataFrame
columns.remove('date')
for column in columns:
    tmp_df = df[['date', column]].copy()
    tmp_df['symbol'] = column
    tmp_df.columns = ['date', 'total_users', 'symbol']
    tmp_df = tmp_df.astype(object).where(pd.notnull(tmp_df), None)
    if all_df.empty:
        all_df = tmp_df
    else:
        all_df = all_df.append(tmp_df)

In [63]:
all_df

date total_users         symbol
0     2017-12-18 00:00:00+00:00        None             0x
1     2017-12-19 00:00:00+00:00        None             0x
2     2017-12-20 00:00:00+00:00        None             0x
3     2017-12-21 00:00:00+00:00        None             0x
4     2017-12-22 00:00:00+00:00        None             0x
...                         ...         ...            ...
1208  2021-04-09 00:00:00+00:00     29518.0  yearn_finance
1209  2021-04-10 00:00:00+00:00     29577.0  yearn_finance
1210  2021-04-11 00:00:00+00:00     29699.0  yearn_finance
1211  2021-04-12 00:00:00+00:00     29761.0  yearn_finance
1212  2021-04-13 00:00:00+00:00     29788.0  yearn_finance

[31538 rows x 3 columns]

In [66]:
insert_dune_total_users(all_df)

2019-07-13 00:00:00+00:00 0x 31.0
Traceback (most recent call last):
  File "<ipython-input-61-ad703788c1c9>", line 12, in insert_dune_total_users
  File "/Library/Frameworks/Python.framework/Versions/3.9/lib/python3.9/site-packages/pymysql/cursors.py", line 148, in execute
    result = self._query(query)
  File "/Library/Frameworks/Python.framework/Versions/3.9/lib/python3.9/site-packages/pymysql/cursors.py", line 310, in _query
    conn.query(q)
  File "/Library/Frameworks/Python.framework/Versions/3.9/lib/python3.9/site-packages/pymysql/connections.py", line 548, in query
    self._affected_rows = self._read_query_result(unbuffered=unbuffered)
  File "/Library/Frameworks/Python.framework/Versions/3.9/lib/python3.9/site-packages/pymysql/connections.py", line 775, in _read_query_result
    result.read()
  File "/Library/Frameworks/Python.framework/Versions/3.9/lib/python3.9/site-packages/pymysql/connections.py", line 1156, in read
    first_packet = self.connection._read_packet()
  Fi

Traceback (most recent call last):
  File "<ipython-input-61-ad703788c1c9>", line 12, in insert_dune_total_users
  File "/Library/Frameworks/Python.framework/Versions/3.9/lib/python3.9/site-packages/pymysql/cursors.py", line 148, in execute
    result = self._query(query)
  File "/Library/Frameworks/Python.framework/Versions/3.9/lib/python3.9/site-packages/pymysql/cursors.py", line 310, in _query
    conn.query(q)
  File "/Library/Frameworks/Python.framework/Versions/3.9/lib/python3.9/site-packages/pymysql/connections.py", line 548, in query
    self._affected_rows = self._read_query_result(unbuffered=unbuffered)
  File "/Library/Frameworks/Python.framework/Versions/3.9/lib/python3.9/site-packages/pymysql/connections.py", line 775, in _read_query_result
    result.read()
  File "/Library/Frameworks/Python.framework/Versions/3.9/lib/python3.9/site-packages/pymysql/connections.py", line 1156, in read
    first_packet = self.connection._read_packet()
  File "/Library/Frameworks/Python.fra

Traceback (most recent call last):
  File "<ipython-input-61-ad703788c1c9>", line 12, in insert_dune_total_users
  File "/Library/Frameworks/Python.framework/Versions/3.9/lib/python3.9/site-packages/pymysql/cursors.py", line 148, in execute
    result = self._query(query)
  File "/Library/Frameworks/Python.framework/Versions/3.9/lib/python3.9/site-packages/pymysql/cursors.py", line 310, in _query
    conn.query(q)
  File "/Library/Frameworks/Python.framework/Versions/3.9/lib/python3.9/site-packages/pymysql/connections.py", line 548, in query
    self._affected_rows = self._read_query_result(unbuffered=unbuffered)
  File "/Library/Frameworks/Python.framework/Versions/3.9/lib/python3.9/site-packages/pymysql/connections.py", line 775, in _read_query_result
    result.read()
  File "/Library/Frameworks/Python.framework/Versions/3.9/lib/python3.9/site-packages/pymysql/connections.py", line 1156, in read
    first_packet = self.connection._read_packet()
  File "/Library/Frameworks/Python.fra

Traceback (most recent call last):
  File "<ipython-input-61-ad703788c1c9>", line 12, in insert_dune_total_users
  File "/Library/Frameworks/Python.framework/Versions/3.9/lib/python3.9/site-packages/pymysql/cursors.py", line 148, in execute
    result = self._query(query)
  File "/Library/Frameworks/Python.framework/Versions/3.9/lib/python3.9/site-packages/pymysql/cursors.py", line 310, in _query
    conn.query(q)
  File "/Library/Frameworks/Python.framework/Versions/3.9/lib/python3.9/site-packages/pymysql/connections.py", line 548, in query
    self._affected_rows = self._read_query_result(unbuffered=unbuffered)
  File "/Library/Frameworks/Python.framework/Versions/3.9/lib/python3.9/site-packages/pymysql/connections.py", line 775, in _read_query_result
    result.read()
  File "/Library/Frameworks/Python.framework/Versions/3.9/lib/python3.9/site-packages/pymysql/connections.py", line 1156, in read
    first_packet = self.connection._read_packet()
  File "/Library/Frameworks/Python.fra

Traceback (most recent call last):
  File "<ipython-input-61-ad703788c1c9>", line 12, in insert_dune_total_users
  File "/Library/Frameworks/Python.framework/Versions/3.9/lib/python3.9/site-packages/pymysql/cursors.py", line 148, in execute
    result = self._query(query)
  File "/Library/Frameworks/Python.framework/Versions/3.9/lib/python3.9/site-packages/pymysql/cursors.py", line 310, in _query
    conn.query(q)
  File "/Library/Frameworks/Python.framework/Versions/3.9/lib/python3.9/site-packages/pymysql/connections.py", line 548, in query
    self._affected_rows = self._read_query_result(unbuffered=unbuffered)
  File "/Library/Frameworks/Python.framework/Versions/3.9/lib/python3.9/site-packages/pymysql/connections.py", line 775, in _read_query_result
    result.read()
  File "/Library/Frameworks/Python.framework/Versions/3.9/lib/python3.9/site-packages/pymysql/connections.py", line 1156, in read
    first_packet = self.connection._read_packet()
  File "/Library/Frameworks/Python.fra

...

2019-12-07 00:00:00+00:00 Uniswap 21858.0
2019-12-08 00:00:00+00:00 Uniswap 21964.0
2019-12-09 00:00:00+00:00 Uniswap 22076.0
2019-12-10 00:00:00+00:00 Uniswap 22181.0
2019-12-11 00:00:00+00:00 Uniswap 22264.0
2019-12-12 00:00:00+00:00 Uniswap 22377.0
2019-12-13 00:00:00+00:00 Uniswap 22475.0
2019-12-14 00:00:00+00:00 Uniswap 22571.0
2019-12-15 00:00:00+00:00 Uniswap 22642.0
2019-12-16 00:00:00+00:00 Uniswap 22764.0
2019-12-17 00:00:00+00:00 Uniswap 22907.0
2019-12-18 00:00:00+00:00 Uniswap 23030.0
2019-12-19 00:00:00+00:00 Uniswap 23142.0
2019-12-20 00:00:00+00:00 Uniswap 23228.0
2019-12-21 00:00:00+00:00 Uniswap 23296.0
2019-12-22 00:00:00+00:00 Uniswap 23371.0
2019-12-23 00:00:00+00:00 Uniswap 23456.0
2019-12-24 00:00:00+00:00 Uniswap 23542.0
2019-12-25 00:00:00+00:00 Uniswap 23610.0
2019-12-26 00:00:00+00:00 Uniswap 23671.0
2019-12-27 00:00:00+00:00 Uniswap 23735.0
2019-12-28 00:00:00+00:00 Uniswap 23800.0
2019-12-29 00:00:00+00:00 Uniswap 23879.0
2019-12-30 00:00:00+00:00 Uniswap 

2020-06-20 00:00:00+00:00 Uniswap 77940.0
2020-06-21 00:00:00+00:00 Uniswap 78839.0
2020-06-22 00:00:00+00:00 Uniswap 79770.0
2020-06-23 00:00:00+00:00 Uniswap 80672.0
2020-06-24 00:00:00+00:00 Uniswap 81792.0
2020-06-25 00:00:00+00:00 Uniswap 82633.0
2020-06-26 00:00:00+00:00 Uniswap 83437.0
2020-06-27 00:00:00+00:00 Uniswap 84267.0
2020-06-28 00:00:00+00:00 Uniswap 84975.0
2020-06-29 00:00:00+00:00 Uniswap 85722.0
2020-06-30 00:00:00+00:00 Uniswap 86437.0
2020-07-01 00:00:00+00:00 Uniswap 87595.0
2020-07-02 00:00:00+00:00 Uniswap 88589.0
2020-07-03 00:00:00+00:00 Uniswap 89746.0
2020-07-04 00:00:00+00:00 Uniswap 90708.0
2020-07-05 00:00:00+00:00 Uniswap 91578.0
2020-07-06 00:00:00+00:00 Uniswap 92482.0
2020-07-07 00:00:00+00:00 Uniswap 93418.0
2020-07-08 00:00:00+00:00 Uniswap 94361.0
2020-07-09 00:00:00+00:00 Uniswap 95360.0
2020-07-10 00:00:00+00:00 Uniswap 96300.0
2020-07-11 00:00:00+00:00 Uniswap 97101.0
2020-07-12 00:00:00+00:00 Uniswap 98126.0
2020-07-13 00:00:00+00:00 Uniswap 

2020-12-30 00:00:00+00:00 Uniswap 678977.0
2020-12-31 00:00:00+00:00 Uniswap 683822.0
2021-01-01 00:00:00+00:00 Uniswap 687712.0
2021-01-02 00:00:00+00:00 Uniswap 691500.0
2021-01-03 00:00:00+00:00 Uniswap 694739.0
2021-01-04 00:00:00+00:00 Uniswap 697542.0
2021-01-05 00:00:00+00:00 Uniswap 701125.0
2021-01-06 00:00:00+00:00 Uniswap 704589.0
2021-01-07 00:00:00+00:00 Uniswap 707763.0
2021-01-08 00:00:00+00:00 Uniswap 711358.0
2021-01-09 00:00:00+00:00 Uniswap 715762.0
2021-01-10 00:00:00+00:00 Uniswap 719677.0
2021-01-11 00:00:00+00:00 Uniswap 721985.0
2021-01-12 00:00:00+00:00 Uniswap 725364.0
2021-01-13 00:00:00+00:00 Uniswap 728728.0
2021-01-14 00:00:00+00:00 Uniswap 732302.0
2021-01-15 00:00:00+00:00 Uniswap 735833.0
2021-01-16 00:00:00+00:00 Uniswap 740112.0
2021-01-17 00:00:00+00:00 Uniswap 745030.0
2021-01-18 00:00:00+00:00 Uniswap 749871.0
2021-01-19 00:00:00+00:00 Uniswap 754191.0
2021-01-20 00:00:00+00:00 Uniswap 758807.0
2021-01-21 00:00:00+00:00 Uniswap 762696.0
2021-01-22 

2020-10-12 00:00:00+00:00 yearn_finance 21399.0
2020-10-13 00:00:00+00:00 yearn_finance 21659.0
2020-10-14 00:00:00+00:00 yearn_finance 21728.0
2020-10-15 00:00:00+00:00 yearn_finance 21785.0
2020-10-16 00:00:00+00:00 yearn_finance 21845.0
2020-10-17 00:00:00+00:00 yearn_finance 21914.0
2020-10-18 00:00:00+00:00 yearn_finance 21994.0
2020-10-19 00:00:00+00:00 yearn_finance 22039.0
2020-10-20 00:00:00+00:00 yearn_finance 22086.0
2020-10-21 00:00:00+00:00 yearn_finance 22136.0
2020-10-22 00:00:00+00:00 yearn_finance 22193.0
2020-10-23 00:00:00+00:00 yearn_finance 22242.0
2020-10-24 00:00:00+00:00 yearn_finance 22303.0
2020-10-25 00:00:00+00:00 yearn_finance 22392.0
2020-10-26 00:00:00+00:00 yearn_finance 22501.0
2020-10-27 00:00:00+00:00 yearn_finance 22584.0
2020-10-28 00:00:00+00:00 yearn_finance 22679.0
2020-10-29 00:00:00+00:00 yearn_finance 22764.0
2020-10-30 00:00:00+00:00 yearn_finance 22830.0
2020-10-31 00:00:00+00:00 yearn_finance 22888.0
2020-11-01 00:00:00+00:00 yearn_finance 

2021-04-03 00:00:00+00:00 yearn_finance 29208.0
2021-04-04 00:00:00+00:00 yearn_finance 29261.0
2021-04-05 00:00:00+00:00 yearn_finance 29303.0
2021-04-06 00:00:00+00:00 yearn_finance 29337.0
2021-04-07 00:00:00+00:00 yearn_finance 29393.0
2021-04-08 00:00:00+00:00 yearn_finance 29451.0
2021-04-09 00:00:00+00:00 yearn_finance 29518.0
2021-04-10 00:00:00+00:00 yearn_finance 29577.0
2021-04-11 00:00:00+00:00 yearn_finance 29699.0
2021-04-12 00:00:00+00:00 yearn_finance 29761.0
2021-04-13 00:00:00+00:00 yearn_finance 29788.0


In [44]:
tmp_df

date total_users symbol
0     2017-12-18 00:00:00+00:00        None     0x
1     2017-12-19 00:00:00+00:00        None     0x
2     2017-12-20 00:00:00+00:00        None     0x
3     2017-12-21 00:00:00+00:00        None     0x
4     2017-12-22 00:00:00+00:00        None     0x
...                         ...         ...    ...
1208  2021-04-09 00:00:00+00:00     25776.0     0x
1209  2021-04-10 00:00:00+00:00     25853.0     0x
1210  2021-04-11 00:00:00+00:00     25907.0     0x
1211  2021-04-12 00:00:00+00:00     25942.0     0x
1212  2021-04-13 00:00:00+00:00     25962.0     0x

[1213 rows x 3 columns]

### https://trello.com/c/jjvcvpLb/38-compound-and-uniswap-prices-and-max-supply-since-4-5-2021-appear-to-be-wrong

In [1]:
import requests
import pandas as pd
import pymysql
from datetime import datetime, timedelta
import traceback2
import time

api_key = "a86e3326-8c8d-434e-897a-5d6becbf1f35"

symbol_tags = []
defi_symbols = []

def get_other_fields_historical_parsed_data(response_data, date, symbols):
    data = []
    date = datetime(date.year, date.month, date.day)
    for row in response_data:
        symbol = row['symbol']
        print(row)
        break
        if True:
            mcap = row['quote']['USD']['market_cap']
            volume_24h = row['quote']['USD']['volume_24h']
            price = row['quote']['USD']['price']
            symbol_data = [date, symbol, row['name'], price, mcap, row['max_supply'], row['circulating_supply'], row['total_supply'], volume_24h]
            symbol_tags.append([symbol, row['name'], row['tags']])
            data.append(symbol_data)      
    return data


def get_other_fields_historical_data(date, symbols, count=5000):
    print('Fetching')
    url = "https://pro-api.coinmarketcap.com/v1/cryptocurrency/listings/historical"
    payload = {
        'convert': 'USD',
        'date': date,
        'limit': count,
        'cryptocurrency_type': 'all',
        'aux': 'tags,circulating_supply,total_supply,max_supply'
    }
    headers = {
        'Accepts': 'application/json',
        'X-CMC_PRO_API_KEY': api_key
    }
    try:
        response = requests.get(url, params=payload, headers=headers).json()
        data = response['data']
#         print(data)
        data = get_other_fields_historical_parsed_data(data, date, symbols)
        return data
    except Exception:
        print(traceback2.format_exc())
        if response:
            print(response)
        return []


def get_other_fields_historical_data_df(start_date, symbols):
    data = []
    now = datetime.now()
    print(start_date)
    print(now)
    print(start_date.timestamp() < now.timestamp())
    while start_date.timestamp() < now.timestamp():
        date = datetime(start_date.year, start_date.month, start_date.day)
        print(date)
        rows = get_other_fields_historical_data(date, symbols)
        time.sleep(.6)
        print(date, len(rows))
        if rows:
            data.extend(rows)
        start_date = start_date + timedelta(days=1)
    df = pd.DataFrame(data, columns=['date', 'symbol', 'name', 'price', 'mrk_cap', 'max_supply', 'circulating_supply', 'total_supply', 'volume'])
    df['date'] = pd.to_datetime(df['date'])
    return df

In [2]:
start_date = datetime(2021, 4, 5)

In [5]:
get_other_fields_historical_data_df(start_date, ['COMP'])

2021-04-05 00:00:00
2021-04-20 05:03:45.234152
True
2021-04-05 00:00:00
Fetching
{'id': 1, 'name': 'Bitcoin', 'symbol': 'BTC', 'slug': 'bitcoin', 'tags': ['mineable', 'pow', 'sha-256', 'store-of-value', 'state-channels', 'coinbase-ventures-portfolio', 'three-arrows-capital-portfolio', 'polychain-capital-portfolio', 'binance-labs-portfolio', 'arrington-xrp-capital', 'blockchain-capital-portfolio', 'boostvc-portfolio', 'cms-holdings-portfolio', 'dcg-portfolio', 'dragonfly-capital-portfolio', 'electric-capital-portfolio', 'fabric-ventures-portfolio', 'framework-ventures', 'galaxy-digital-portfolio', 'huobi-capital', 'alameda-research-portfolio', 'a16z-portfolio', '1confirmation-portfolio', 'winklevoss-capital', 'usv-portfolio', 'placeholder-ventures-portfolio', 'pantera-capital-portfolio', 'multicoin-capital-portfolio', 'paradigm-xzy-screener'], 'max_supply': 21000000, 'circulating_supply': 18674575, 'total_supply': 18674575, 'last_updated': '2021-04-05T23:00:00.000Z', 'quote': {'USD': {'

2021-04-11 00:00:00 0
2021-04-12 00:00:00
Fetching
{'id': 1, 'name': 'Bitcoin', 'symbol': 'BTC', 'slug': 'bitcoin', 'tags': ['mineable', 'pow', 'sha-256', 'store-of-value', 'state-channels', 'coinbase-ventures-portfolio', 'three-arrows-capital-portfolio', 'polychain-capital-portfolio', 'binance-labs-portfolio', 'arrington-xrp-capital', 'blockchain-capital-portfolio', 'boostvc-portfolio', 'cms-holdings-portfolio', 'dcg-portfolio', 'dragonfly-capital-portfolio', 'electric-capital-portfolio', 'fabric-ventures-portfolio', 'framework-ventures', 'galaxy-digital-portfolio', 'huobi-capital', 'alameda-research-portfolio', 'a16z-portfolio', '1confirmation-portfolio', 'winklevoss-capital', 'usv-portfolio', 'placeholder-ventures-portfolio', 'pantera-capital-portfolio', 'multicoin-capital-portfolio', 'paradigm-xzy-screener'], 'max_supply': 21000000, 'circulating_supply': 18681025, 'total_supply': 18681025, 'last_updated': '2021-04-12T23:00:00.000Z', 'quote': {'USD': {'price': 59893.45188868903, 'vo

2021-04-18 00:00:00 0
2021-04-19 00:00:00
Fetching
{'id': 1, 'name': 'Bitcoin', 'symbol': 'BTC', 'slug': 'bitcoin', 'tags': ['mineable', 'pow', 'sha-256', 'store-of-value', 'state-channels', 'coinbase-ventures-portfolio', 'three-arrows-capital-portfolio', 'polychain-capital-portfolio', 'binance-labs-portfolio', 'arrington-xrp-capital', 'blockchain-capital-portfolio', 'boostvc-portfolio', 'cms-holdings-portfolio', 'dcg-portfolio', 'dragonfly-capital-portfolio', 'electric-capital-portfolio', 'fabric-ventures-portfolio', 'framework-ventures', 'galaxy-digital-portfolio', 'huobi-capital', 'alameda-research-portfolio', 'a16z-portfolio', '1confirmation-portfolio', 'winklevoss-capital', 'usv-portfolio', 'placeholder-ventures-portfolio', 'pantera-capital-portfolio', 'multicoin-capital-portfolio', 'paradigm-xzy-screener'], 'max_supply': 21000000, 'circulating_supply': 18686431, 'total_supply': 18686431, 'last_updated': '2021-04-19T23:00:00.000Z', 'quote': {'USD': {'price': 55724.26709807391, 'vo

Empty DataFrame
Columns: [date, symbol, name, price, mrk_cap, max_supply, circulating_supply, total_supply, volume]
Index: []

### https://trello.com/c/bVxEH951/36-add-yield-farming-data-from-cmc-pool-pair-tvl-reward-type-impermanent-loss-apy

In [28]:
json = {"yieldFarmingList":[{"id":"5fcf5b00c5adb439ad44e3d3","name":"Venus","platform":"Binance Smart Chain","webSite":"https://venus.io/","totalValueLocked":9766742349.3,"poolList":[{"id":196,"name":"vBTC-BTCB Lending","link":"https://app.venus.io/dashboard","pair":"vBTC-BTCB","totalStake":1927687841.25,"totalStakeRatio":0.19737265,"rewards":[{"cryptoId":7288,"name":"Venus","symbol":"XVS","slug":"venus"}],"impermanentLoss":"None","dailyROI":0.00865753424658,"weeklyROI":0.06060273972606,"monthlyROI":0.26333333333333,"yearlyROI":3.16,"updateTime":"2021-04-20T11:31:27.000Z"},{"id":195,"name":"vBUSD-BUSD Lending","link":"https://app.venus.io/dashboard","pair":"vBUSD-BUSD","totalStake":1655735746.75,"totalStakeRatio":0.16952794,"rewards":[{"cryptoId":7288,"name":"Venus","symbol":"XVS","slug":"venus"}],"impermanentLoss":"None","dailyROI":0.00871232876712,"weeklyROI":0.06098630136984,"monthlyROI":0.265,"yearlyROI":3.18,"updateTime":"2021-04-20T11:31:26.000Z"},{"id":197,"name":"vBNB-BNB Lending","link":"https://app.venus.io/dashboard","pair":"vBNB-BNB","totalStake":1621405283.35,"totalStakeRatio":0.16601291,"rewards":[{"cryptoId":7288,"name":"Venus","symbol":"XVS","slug":"venus"}],"impermanentLoss":"None","dailyROI":0.01106849315068,"weeklyROI":0.07747945205476,"monthlyROI":0.33666666666667,"yearlyROI":4.04,"updateTime":"2021-04-20T11:31:27.000Z"},{"id":201,"name":"vUSDC-USDC Lending","link":"https://app.venus.io/dashboard","pair":"vUSDC-USDC","totalStake":1251335369.19,"totalStakeRatio":0.12812208,"rewards":[{"cryptoId":7288,"name":"Venus","symbol":"XVS","slug":"venus"}],"impermanentLoss":"None","dailyROI":0.00849315068493,"weeklyROI":0.05945205479451,"monthlyROI":0.25833333333333,"yearlyROI":3.1,"updateTime":"2021-04-20T11:31:28.000Z"},{"id":200,"name":"vUSDT-USDT Lending","link":"https://app.venus.io/dashboard","pair":"vUSDT-USDT","totalStake":1063997012.91,"totalStakeRatio":0.10894083,"rewards":[{"cryptoId":7288,"name":"Venus","symbol":"XVS","slug":"venus"}],"impermanentLoss":"None","dailyROI":0.01556164383562,"weeklyROI":0.10893150684934,"monthlyROI":0.47333333333333,"yearlyROI":5.68,"updateTime":"2021-04-20T11:31:28.000Z"},{"id":194,"name":"vETH-ETH Lending","link":"https://app.venus.io/dashboard","pair":"vETH-ETH","totalStake":917734767.89,"totalStakeRatio":0.09396529,"rewards":[{"cryptoId":7288,"name":"Venus","symbol":"XVS","slug":"venus"}],"impermanentLoss":"None","dailyROI":0.00978082191781,"weeklyROI":0.06846575342467,"monthlyROI":0.2975,"yearlyROI":3.57,"updateTime":"2021-04-20T11:31:26.000Z"},{"id":193,"name":"vXVS-XVS Lending","link":"https://app.venus.io/dashboard","pair":"vXVS-XVS","totalStake":399209896.65,"totalStakeRatio":0.04087442,"rewards":[{"cryptoId":7288,"name":"Venus","symbol":"XVS","slug":"venus"}],"impermanentLoss":"None","dailyROI":0.02638356164384,"weeklyROI":0.18468493150688,"monthlyROI":0.8025,"yearlyROI":9.63,"updateTime":"2021-04-20T11:31:26.000Z"},{"id":202,"name":"vSXP-SXP Lending","link":"https://app.venus.io/dashboard","pair":"vSXP-SXP","totalStake":268024106.26,"totalStakeRatio":0.02744253,"rewards":[{"cryptoId":7288,"name":"Venus","symbol":"XVS","slug":"venus"}],"impermanentLoss":"None","dailyROI":0.01819178082192,"weeklyROI":0.12734246575344,"monthlyROI":0.55333333333333,"yearlyROI":6.64,"updateTime":"2021-04-20T11:31:28.000Z"},{"id":206,"name":"VAI Mint","link":"https://app.venus.io/dashboard","pair":"VAI","totalStake":179770916.92,"totalStakeRatio":0.01840644,"rewards":[{"cryptoId":7288,"name":"Venus","symbol":"XVS","slug":"venus"}],"impermanentLoss":"None","dailyROI":0.25241095890411,"weeklyROI":1.76687671232877,"monthlyROI":7.6775,"yearlyROI":92.13,"updateTime":"2021-04-20T11:31:30.000Z"},{"id":204,"name":"vDOT-DOT Lending","link":"https://app.venus.io/dashboard","pair":"vDOT-DOT","totalStake":179096892.91,"totalStakeRatio":0.01833742,"rewards":[{"cryptoId":7288,"name":"Venus","symbol":"XVS","slug":"venus"},{"cryptoId":6636,"name":"Polkadot","symbol":"DOT","slug":"polkadot-new"}],"impermanentLoss":"None","dailyROI":0.00750684931507,"weeklyROI":0.05254794520549,"monthlyROI":0.22833333333333,"yearlyROI":2.74,"updateTime":"2021-04-20T11:31:29.000Z"},{"id":198,"name":"vXRP-XRP Lending","link":"https://app.venus.io/dashboard","pair":"vXRP-XRP","totalStake":144934387.11,"totalStakeRatio":0.01483958,"rewards":[{"cryptoId":7288,"name":"Venus","symbol":"XVS","slug":"venus"}],"impermanentLoss":"None","dailyROI":0.00271232876712,"weeklyROI":0.01898630136984,"monthlyROI":0.0825,"yearlyROI":0.99,"updateTime":"2021-04-20T11:31:27.000Z"},{"id":205,"name":"vLINK-LINK Lending","link":"https://app.venus.io/dashboard","pair":"vLINK-LINK","totalStake":83810578.65,"totalStakeRatio":0.00858122,"rewards":[{"cryptoId":7288,"name":"Venus","symbol":"XVS","slug":"venus"},{"cryptoId":1975,"name":"Chainlink","symbol":"LINK","slug":"chainlink"}],"impermanentLoss":"None","dailyROI":0.00783561643836,"weeklyROI":0.05484931506852,"monthlyROI":0.23833333333333,"yearlyROI":2.86,"updateTime":"2021-04-20T11:31:29.000Z"},{"id":199,"name":"vLTC-LTC Lending","link":"https://app.venus.io/dashboard","pair":"vLTC-LTC","totalStake":40506476.01,"totalStakeRatio":0.00414739,"rewards":[{"cryptoId":7288,"name":"Venus","symbol":"XVS","slug":"venus"}],"impermanentLoss":"None","dailyROI":0.00882191780822,"weeklyROI":0.06175342465754,"monthlyROI":0.26833333333333,"yearlyROI":3.22,"updateTime":"2021-04-20T11:31:28.000Z"},{"id":203,"name":"vBCH-BCH Lending","link":"https://app.venus.io/dashboard","pair":"vBCH-BCH","totalStake":33493073.45,"totalStakeRatio":0.0034293,"rewards":[{"cryptoId":7288,"name":"Venus","symbol":"XVS","slug":"venus"},{"cryptoId":1831,"name":"Bitcoin Cash","symbol":"BCH","slug":"bitcoin-cash"}],"impermanentLoss":"None","dailyROI":0.00197260273973,"weeklyROI":0.01380821917811,"monthlyROI":0.06,"yearlyROI":0.72,"updateTime":"2021-04-20T11:31:29.000Z"}],"auditList":[{"url":"https://certik.foundation/projects/swipe","auditFirm":"Certik"}],"hasNew":1},{"id":"5f86b154cc06881662044a5a","name":"PancakeSwap","platform":"Binance Smart Chain","webSite":"https://pancakeswap.finance/","totalValueLocked":8115393879.487392,"poolList":[{"id":126,"name":"CAKE","link":"https://pancakeswap.finance/staking","pair":"CAKE","totalStake":5277386182.68659,"totalStakeRatio":0.65029329,"rewards":[{"cryptoId":7186,"name":"PancakeSwap","symbol":"CAKE","slug":"pancakeswap"}],"impermanentLoss":"None","dailyROI":0.25593506849315,"weeklyROI":1.79154547945205,"monthlyROI":7.78469166666667,"yearlyROI":93.4163,"updateTime":"2021-04-20T11:31:11.000Z"},{"id":127,"name":"PancakeSWAP CAKE-BNB","link":"https://pancakeswap.finance/farms/CAKE-BNB%20FLIP","pair":"CAKE-WBNB","totalStake":1005454531.4687102,"totalStakeRatio":0.12389473,"rewards":[{"cryptoId":7186,"name":"PancakeSwap","symbol":"CAKE","slug":"pancakeswap"}],"impermanentLoss":"High","dailyROI":0.40773945205479,"weeklyROI":2.85417616438353,"monthlyROI":12.402075,"yearlyROI":148.8249,"updateTime":"2021-04-20T11:31:11.000Z"},{"id":128,"name":"PancakeSWAP BUSD-BNB","link":"https://pancakeswap.finance/farms/BUSD-BNB%20FLIP","pair":"BUSD-WBNB","totalStake":562438359.9598755,"totalStakeRatio":0.06930512,"rewards":[{"cryptoId":7186,"name":"PancakeSwap","symbol":"CAKE","slug":"pancakeswap"}],"impermanentLoss":"High","dailyROI":0.19437424657534,"weeklyROI":1.36061972602738,"monthlyROI":5.91221666666667,"yearlyROI":70.9466,"updateTime":"2021-04-20T11:31:11.000Z"},{"id":170,"name":"PancakeSWAP ETH-BNB","link":"https://pancakeswap.finance/farms/ETH-BNB%20FLP","pair":"ETH-BNB","totalStake":298987749.45881903,"totalStakeRatio":0.03684205,"rewards":[{"cryptoId":7186,"name":"PancakeSwap","symbol":"CAKE","slug":"pancakeswap"}],"impermanentLoss":"High","dailyROI":0.09144493150685,"weeklyROI":0.64011452054795,"monthlyROI":2.78145,"yearlyROI":33.3774,"updateTime":"2021-04-20T11:31:18.000Z"},{"id":171,"name":"PancakeSWAP BTC-BNB","link":"https://pancakeswap.finance/farms/BTCB-BNB%20FLP","pair":"BTC-BNB","totalStake":293888612.3485444,"totalStakeRatio":0.03621372,"rewards":[{"cryptoId":7186,"name":"PancakeSwap","symbol":"CAKE","slug":"pancakeswap"}],"impermanentLoss":"High","dailyROI":0.09303150684932,"weeklyROI":0.65122054794524,"monthlyROI":2.82970833333333,"yearlyROI":33.9565,"updateTime":"2021-04-20T11:31:19.000Z"},{"id":168,"name":"PancakeSWAP USDT-BUSD","link":"https://pancakeswap.finance/farms/USDT-BUSD%20FLIP","pair":"USDT-BUSD","totalStake":182728528.0371041,"totalStakeRatio":0.02251629,"rewards":[{"cryptoId":7186,"name":"PancakeSwap","symbol":"CAKE","slug":"pancakeswap"}],"impermanentLoss":"Low","dailyROI":0.07481287671233,"weeklyROI":0.52369013698631,"monthlyROI":2.27555833333333,"yearlyROI":27.3067,"updateTime":"2021-04-20T11:31:18.000Z"},{"id":173,"name":"PancakeSWAP USDT-BNB","link":"https://pancakeswap.finance/farms/USDT-BNB%20FLP","pair":"USDT-BNB","totalStake":149461031.20067152,"totalStakeRatio":0.01841698,"rewards":[{"cryptoId":7186,"name":"PancakeSwap","symbol":"CAKE","slug":"pancakeswap"}],"impermanentLoss":"High","dailyROI":0.1829298630137,"weeklyROI":1.2805090410959,"monthlyROI":5.56411666666667,"yearlyROI":66.7694,"updateTime":"2021-04-20T11:31:19.000Z"},{"id":131,"name":"PancakeSWAP DOT-BNB","link":"https://pancakeswap.finance/farms/DOT-BNB%20FLIP","pair":"DOT-WBNB","totalStake":90809256.30127065,"totalStakeRatio":0.01118975,"rewards":[{"cryptoId":7186,"name":"PancakeSwap","symbol":"CAKE","slug":"pancakeswap"}],"impermanentLoss":"High","dailyROI":0.3009704109589,"weeklyROI":2.1067928767123,"monthlyROI":9.15451666666667,"yearlyROI":109.8542,"updateTime":"2021-04-20T11:31:12.000Z"},{"id":133,"name":"PancakeSWAP LINK-BNB","link":"https://pancakeswap.finance/farms/LINK-BNB%20FLIP","pair":"LINK-WBNB","totalStake":56625572.76652139,"totalStakeRatio":0.00697755,"rewards":[{"cryptoId":7186,"name":"PancakeSwap","symbol":"CAKE","slug":"pancakeswap"}],"impermanentLoss":"High","dailyROI":0.48283616438356,"weeklyROI":3.37985315068492,"monthlyROI":14.68626666666667,"yearlyROI":176.2352,"updateTime":"2021-04-20T11:31:14.000Z"},{"id":174,"name":"PancakeSWAP XRP-BNB","link":"https://pancakeswap.finance/farms/XRP-BNB%20FLP","pair":"XRP-BNB","totalStake":48613888.07333609,"totalStakeRatio":0.00599033,"rewards":[{"cryptoId":7186,"name":"PancakeSwap","symbol":"CAKE","slug":"pancakeswap"}],"impermanentLoss":"High","dailyROI":0.28120438356164,"weeklyROI":1.96843068493148,"monthlyROI":8.5533,"yearlyROI":102.6396,"updateTime":"2021-04-20T11:31:19.000Z"},{"id":129,"name":"PancakeSWAP ADA-BNB","link":"https://pancakeswap.finance/farms/ADA-BNB%20FLIP","pair":"ADA-WBNB","totalStake":46430328.453746125,"totalStakeRatio":0.00572127,"rewards":[{"cryptoId":7186,"name":"PancakeSwap","symbol":"CAKE","slug":"pancakeswap"}],"impermanentLoss":"High","dailyROI":0.29432164383562,"weeklyROI":2.06025150684934,"monthlyROI":8.95228333333333,"yearlyROI":107.4274,"updateTime":"2021-04-20T11:31:11.000Z"},{"id":130,"name":"PancakeSWAP BAND-BNB","link":"https://pancakeswap.finance/farms/BAND-BNB%20FLIP","pair":"BAND-WBNB","totalStake":33376027.7536527,"totalStakeRatio":0.00411268,"rewards":[{"cryptoId":7186,"name":"PancakeSwap","symbol":"CAKE","slug":"pancakeswap"}],"impermanentLoss":"High","dailyROI":0.81887808219178,"weeklyROI":5.73214657534246,"monthlyROI":24.90754166666667,"yearlyROI":298.8905,"updateTime":"2021-04-20T11:31:11.000Z"},{"id":172,"name":"PancakeSWAP ALPHA-BNB","link":"https://pancakeswap.finance/farms/ALPHA-BNB%20FLP","pair":"ALPHA-BNB","totalStake":30817624.030098937,"totalStakeRatio":0.00379743,"rewards":[{"cryptoId":7186,"name":"PancakeSwap","symbol":"CAKE","slug":"pancakeswap"}],"impermanentLoss":"High","dailyROI":0.44359150684932,"weeklyROI":3.10514054794524,"monthlyROI":13.492575,"yearlyROI":161.9109,"updateTime":"2021-04-20T11:31:19.000Z"},{"id":169,"name":"PancakeSWAP TWT-BNB","link":"https://pancakeswap.finance/farms/TWT-BNB%20FLP","pair":"TWT-BNB","totalStake":18803965.596320003,"totalStakeRatio":0.00231707,"rewards":[{"cryptoId":7186,"name":"PancakeSwap","symbol":"CAKE","slug":"pancakeswap"}],"impermanentLoss":"High","dailyROI":1.45399534246575,"weeklyROI":10.17796739726025,"monthlyROI":44.22569166666667,"yearlyROI":530.7083,"updateTime":"2021-04-20T11:31:18.000Z"},{"id":175,"name":"PancakeSWAP ATOM-BNB","link":"https://pancakeswap.finance/farms/ATOM-BNB%20FLP","pair":"ATOM-BNB","totalStake":9911690.29667046,"totalStakeRatio":0.00122134,"rewards":[{"cryptoId":7186,"name":"PancakeSwap","symbol":"CAKE","slug":"pancakeswap"}],"impermanentLoss":"High","dailyROI":1.37922383561644,"weeklyROI":9.65456684931508,"monthlyROI":41.95139166666667,"yearlyROI":503.4167,"updateTime":"2021-04-20T11:31:20.000Z"},{"id":132,"name":"PancakeSWAP EOS-BNB","link":"https://pancakeswap.finance/farms/EOS-BNB%20FLIP","pair":"EOS-WBNB","totalStake":7709563.3947910145,"totalStakeRatio":0.00094999,"rewards":[{"cryptoId":7186,"name":"PancakeSwap","symbol":"CAKE","slug":"pancakeswap"}],"impermanentLoss":"High","dailyROI":1.77317945205479,"weeklyROI":12.41225616438353,"monthlyROI":53.93420833333333,"yearlyROI":647.2105,"updateTime":"2021-04-20T11:31:13.000Z"},{"id":179,"name":"PancakeSWAP BCH-BNB","link":"https://pancakeswap.finance/farms/BCH-BNB%20FLP","pair":"BCH-BNB","totalStake":1063861.0315633444,"totalStakeRatio":0.00013109,"rewards":[{"cryptoId":7186,"name":"PancakeSwap","symbol":"CAKE","slug":"pancakeswap"}],"impermanentLoss":"High","dailyROI":12.84983643835616,"weeklyROI":89.94885506849312,"monthlyROI":390.8491916666667,"yearlyROI":4690.1903,"updateTime":"2021-04-20T11:31:21.000Z"},{"id":178,"name":"PancakeSWAP XTZ-BNB","link":"https://pancakeswap.finance/farms/XTZ-BNB%20FLP","pair":"XTZ-BNB","totalStake":617922.8690560703,"totalStakeRatio":0.00007614,"rewards":[{"cryptoId":7186,"name":"PancakeSwap","symbol":"CAKE","slug":"pancakeswap"}],"impermanentLoss":"High","dailyROI":22.12321479452055,"weeklyROI":154.86250356164385,"monthlyROI":672.91445,"yearlyROI":8074.9734,"updateTime":"2021-04-20T11:31:21.000Z"},{"id":176,"name":"PancakeSWAP YFII-BNB","link":"https://pancakeswap.finance/farms/YFII-BNB%20FLP","pair":"YFII-BNB","totalStake":136849.07803390583,"totalStakeRatio":0.00001686,"rewards":[{"cryptoId":7186,"name":"PancakeSwap","symbol":"CAKE","slug":"pancakeswap"}],"impermanentLoss":"High","dailyROI":99.89428164383563,"weeklyROI":699.2599715068493,"monthlyROI":3038.4510666666665,"yearlyROI":36461.4128,"updateTime":"2021-04-20T11:31:20.000Z"},{"id":177,"name":"PancakeSWAP DAI-BNB","link":"https://pancakeswap.finance/farms/DAI-BNB%20FLP","pair":"DAI-BNB","totalStake":132334.6820171771,"totalStakeRatio":0.00001631,"rewards":[{"cryptoId":7186,"name":"PancakeSwap","symbol":"CAKE","slug":"pancakeswap"}],"impermanentLoss":"High","dailyROI":103.30202273972603,"weeklyROI":723.1141591780822,"monthlyROI":3142.1031916666666,"yearlyROI":37705.2383,"updateTime":"2021-04-20T11:31:20.000Z"}],"auditList":[{"url":"https://github.com/certikfoundation-shared/CertiK-Audits/blob/master/reports/REP-PancakeSwap-16_10_2020.pdf","auditFirm":"CertiK"}],"hasNew":0},{"id":"5f5b5b9cb761c05513d8356d","name":"Curve","platform":"Ethereum","webSite":"https://www.curve.fi/","totalValueLocked":1854776987.4432564,"poolList":[{"id":39,"name":"renBTC","link":"https://www.curve.fi/ren","pair":"renBTC-wBTC","totalStake":517522019.25426126,"totalStakeRatio":0.27902116,"rewards":[{"cryptoId":6538,"name":"Curve DAO Token","symbol":"CRV","slug":"curve-dao-token"}],"impermanentLoss":"Low","dailyROI":0.00483287671233,"weeklyROI":0.03383013698631,"monthlyROI":0.147,"yearlyROI":1.764,"updateTime":"2021-04-15T10:00:46.000Z"},{"id":41,"name":"hBTC","link":"https://www.curve.fi/hbtc","pair":"hBTC-wBTC","totalStake":480045188.0476562,"totalStakeRatio":0.25881558,"rewards":[{"cryptoId":6538,"name":"Curve DAO Token","symbol":"CRV","slug":"curve-dao-token"}],"impermanentLoss":"Low","dailyROI":0.01870383561644,"weeklyROI":0.13092684931508,"monthlyROI":0.56890833333333,"yearlyROI":6.8269,"updateTime":"2021-04-15T10:00:46.000Z"},{"id":40,"name":"sBTC","link":"https://www.curve.fi/sbtc","pair":"renBTC-wBTC-sBTC","totalStake":425205110.03057575,"totalStakeRatio":0.22924864,"rewards":[{"cryptoId":6538,"name":"Curve DAO Token","symbol":"CRV","slug":"curve-dao-token"}],"impermanentLoss":"Low","dailyROI":0.00577726027397,"weeklyROI":0.04044082191779,"monthlyROI":0.175725,"yearlyROI":2.1087,"updateTime":"2021-04-15T10:00:46.000Z"},{"id":38,"name":"sUSD","link":"https://www.curve.fi/susdv2","pair":"DAI-USDC-USDT-sUSD","totalStake":199434597.04514995,"totalStakeRatio":0.10752484,"rewards":[{"cryptoId":6538,"name":"Curve DAO Token","symbol":"CRV","slug":"curve-dao-token"}],"impermanentLoss":"Low","dailyROI":0.04020493150685,"weeklyROI":0.28143452054795,"monthlyROI":1.2229,"yearlyROI":14.6748,"updateTime":"2021-04-15T10:00:45.000Z"},{"id":34,"name":"Compound","link":"https://www.curve.fi/compound","pair":"DAI-USDC","totalStake":142911560.83606184,"totalStakeRatio":0.07705054,"rewards":[{"cryptoId":6538,"name":"Curve DAO Token","symbol":"CRV","slug":"curve-dao-token"}],"impermanentLoss":"Low","dailyROI":0.03104602739726,"weeklyROI":0.21732219178082,"monthlyROI":0.94431666666667,"yearlyROI":11.3318,"updateTime":"2021-04-15T10:00:44.000Z"},{"id":37,"name":"bUSD","link":"https://www.curve.fi/busd","pair":"DAI-USDC-USDT-BUSD","totalStake":89658512.22955135,"totalStakeRatio":0.04833924,"rewards":[{"cryptoId":6538,"name":"Curve DAO Token","symbol":"CRV","slug":"curve-dao-token"}],"impermanentLoss":"Low","dailyROI":0.01985287671233,"weeklyROI":0.13897013698631,"monthlyROI":0.60385833333333,"yearlyROI":7.2463,"updateTime":"2021-04-15T10:00:45.000Z"}],"auditList":[{"url":"https://www.curve.fi/curve_audits/00-ToB.pdf","auditFirm":"Trail of Bits"},{"url":"https://www.curve.fi/curve_audits/curve-dao-quantstamp.pdf","auditFirm":"Quantstamp"}],"hasNew":0},{"id":"5f5b5b9cb761c05513d8356f","name":"Sushi","platform":"Ethereum","webSite":"https://sushiswap.org/","totalValueLocked":1834629015.881132,"poolList":[{"id":52,"name":"Sushi Party!","link":"https://sushiswapclassic.org/farms/SUSHI-ETH%20SLP","pair":"SUSHI-ETH","totalStake":463172582.9797993,"totalStakeRatio":0.25246117,"rewards":[{"cryptoId":6758,"name":"SushiSwap","symbol":"SUSHI","slug":"sushiswap"}],"impermanentLoss":"High","dailyROI":0.11631315068493,"weeklyROI":0.81419205479451,"monthlyROI":3.53785833333333,"yearlyROI":42.4543,"updateTime":"2021-04-20T11:30:38.000Z"},{"id":58,"name":"Circle Snail","link":"https://sushiswapclassic.org/farms/USDC-ETH%20SLP","pair":"USDC-ETH","totalStake":370658425.058987,"totalStakeRatio":0.20203454,"rewards":[{"cryptoId":6758,"name":"SushiSwap","symbol":"SUSHI","slug":"sushiswap"}],"impermanentLoss":"High","dailyROI":0.08693424657534,"weeklyROI":0.60853972602738,"monthlyROI":2.64425,"yearlyROI":31.731,"updateTime":"2021-04-20T11:30:40.000Z"},{"id":57,"name":"Donald DAI","link":"https://sushiswapclassic.org/farms/DAI-ETH%20SLP","pair":"DAI-ETH","totalStake":286533359.5525954,"totalStakeRatio":0.15618054,"rewards":[{"cryptoId":6758,"name":"SushiSwap","symbol":"SUSHI","slug":"sushiswap"}],"impermanentLoss":"High","dailyROI":0.11805890410959,"weeklyROI":0.82641232876713,"monthlyROI":3.59095833333333,"yearlyROI":43.0915,"updateTime":"2021-04-20T11:30:40.000Z"},{"id":55,"name":"Tether Turtle","link":"https://sushiswapclassic.org/farms/USDT-ETH%20SLP","pair":"USDT-ETH","totalStake":245835421.13518074,"totalStakeRatio":0.13399735,"rewards":[{"cryptoId":6758,"name":"SushiSwap","symbol":"SUSHI","slug":"sushiswap"}],"impermanentLoss":"High","dailyROI":0.11527835616438,"weeklyROI":0.80694849315066,"monthlyROI":3.50638333333333,"yearlyROI":42.0766,"updateTime":"2021-04-20T11:30:39.000Z"},{"id":54,"name":"YFI Whale","link":"https://sushiswapclassic.org/farms/YFI-ETH%20SLP","pair":"YFI-ETH","totalStake":172670354.74848753,"totalStakeRatio":0.09411731,"rewards":[{"cryptoId":6758,"name":"SushiSwap","symbol":"SUSHI","slug":"sushiswap"}],"impermanentLoss":"High","dailyROI":0.1313,"weeklyROI":0.9191,"monthlyROI":3.99370833333333,"yearlyROI":47.9245,"updateTime":"2021-04-20T11:30:39.000Z"},{"id":59,"name":"Toadie Marine","link":"https://sushiswapclassic.org/farms/LINK-ETH%20SLP","pair":"LINK-ETH","totalStake":121388264.0122265,"totalStakeRatio":0.06616502,"rewards":[{"cryptoId":6758,"name":"SushiSwap","symbol":"SUSHI","slug":"sushiswap"}],"impermanentLoss":"High","dailyROI":0.08524821917808,"weeklyROI":0.59673753424656,"monthlyROI":2.59296666666667,"yearlyROI":31.1156,"updateTime":"2021-04-20T11:30:40.000Z"},{"id":51,"name":"Synthetic Snake","link":"https://sushiswapclassic.org/farms/SNX-ETH%20SLP","pair":"SNX-ETH","totalStake":59848137.625209205,"totalStakeRatio":0.03262138,"rewards":[{"cryptoId":6758,"name":"SushiSwap","symbol":"SUSHI","slug":"sushiswap"}],"impermanentLoss":"High","dailyROI":0.09901808219178,"weeklyROI":0.69312657534246,"monthlyROI":3.0118,"yearlyROI":36.1416,"updateTime":"2021-04-20T11:30:38.000Z"},{"id":60,"name":"Compound Truffle","link":"https://sushiswapclassic.org/farms/COMP-ETH%20SLP","pair":"COMP-ETH","totalStake":28482879.66249029,"totalStakeRatio":0.01552514,"rewards":[{"cryptoId":6758,"name":"SushiSwap","symbol":"SUSHI","slug":"sushiswap"}],"impermanentLoss":"High","dailyROI":0.05871287671233,"weeklyROI":0.41099013698631,"monthlyROI":1.78585,"yearlyROI":21.4302,"updateTime":"2021-04-20T11:30:41.000Z"},{"id":64,"name":"REN Rhino","link":"https://sushiswapclassic.org/farms/REN-ETH%20SLP","pair":"ren-ETH","totalStake":19903622.689017594,"totalStakeRatio":0.01084885,"rewards":[{"cryptoId":6758,"name":"SushiSwap","symbol":"SUSHI","slug":"sushiswap"}],"impermanentLoss":"High","dailyROI":0.0563895890411,"weeklyROI":0.3947271232877,"monthlyROI":1.71518333333333,"yearlyROI":20.5822,"updateTime":"2021-04-20T11:30:42.000Z"},{"id":61,"name":"Spartan Dollar","link":"https://sushiswapclassic.org/farms/SUSD-ETH%20SLP","pair":"SUSD-ETH","totalStake":19582315.906880725,"totalStakeRatio":0.01067372,"rewards":[{"cryptoId":6758,"name":"SushiSwap","symbol":"SUSHI","slug":"sushiswap"}],"impermanentLoss":"High","dailyROI":0.15646931506849,"weeklyROI":1.09528520547943,"monthlyROI":4.759275,"yearlyROI":57.1113,"updateTime":"2021-04-20T11:30:41.000Z"},{"id":65,"name":"CRV Crocodile","link":"https://sushiswapclassic.org/farms/CRV-ETH%20SLP","pair":"CRV-ETH","totalStake":15828499.447976978,"totalStakeRatio":0.00862763,"rewards":[{"cryptoId":6758,"name":"SushiSwap","symbol":"SUSHI","slug":"sushiswap"}],"impermanentLoss":"High","dailyROI":0.07090739726027,"weeklyROI":0.49635178082189,"monthlyROI":2.15676666666667,"yearlyROI":25.8812,"updateTime":"2021-04-20T11:30:42.000Z"},{"id":50,"name":"Band-osaurus","link":"https://sushiswapclassic.org/farms/BAND-ETH%20SLP","pair":"BAND-ETH","totalStake":15682191.840735458,"totalStakeRatio":0.00854788,"rewards":[{"cryptoId":6758,"name":"SushiSwap","symbol":"SUSHI","slug":"sushiswap"}],"impermanentLoss":"High","dailyROI":0.10162767123288,"weeklyROI":0.71139369863016,"monthlyROI":3.091175,"yearlyROI":37.0941,"updateTime":"2021-04-20T11:30:37.000Z"},{"id":49,"name":"Umami Squid","link":"https://sushiswapclassic.org/farms/UMA-ETH%20SLP","pair":"UMA-ETH","totalStake":15042961.221545286,"totalStakeRatio":0.00819946,"rewards":[{"cryptoId":6758,"name":"SushiSwap","symbol":"SUSHI","slug":"sushiswap"}],"impermanentLoss":"High","dailyROI":0.0746101369863,"weeklyROI":0.5222709589041,"monthlyROI":2.26939166666667,"yearlyROI":27.2327,"updateTime":"2021-04-20T11:30:37.000Z"}],"auditList":[{"url":"https://github.com/quantstamp/sushiswap-security-review","auditFirm":"Quantstamp"},{"url":"https://github.com/peckshield/publications/blob/master/audit_reports/PeckShield-Audit-Report-SushiSwap-v1.0.pdf","auditFirm":"Peckshield"}],"hasNew":0},{"id":"5f71c830edcba010f8a365b4","name":"Harvest","platform":"Ethereum","webSite":"https://harvest.finance/","totalValueLocked":270760747.9444821,"poolList":[{"id":142,"name":"CRVRENWBTC Vault","link":"https://harvest.finance/","pair":"CRV-RENBTC","totalStake":104608567.18765447,"totalStakeRatio":0.38635056,"rewards":[{"cryptoId":6859,"name":"Harvest Finance","symbol":"FARM","slug":"harvest-finance"},{"cryptoId":6538,"name":"Curve DAO Token","symbol":"CRV","slug":"curve-dao-token"}],"impermanentLoss":"Low","dailyROI":0.00602739726027,"weeklyROI":0.04219178082189,"monthlyROI":0.18333333333333,"yearlyROI":2.2,"updateTime":"2021-04-20T11:31:10.000Z"},{"id":147,"name":"FARM Profit Sharing","link":"https://harvest.finance/","pair":"FARM","totalStake":80995582.79860535,"totalStakeRatio":0.29914079,"rewards":[{"cryptoId":6859,"name":"Harvest Finance","symbol":"FARM","slug":"harvest-finance"}],"impermanentLoss":"None","dailyROI":0.08038356164384,"weeklyROI":0.56268493150688,"monthlyROI":2.445,"yearlyROI":29.34,"updateTime":"2021-04-20T11:31:11.000Z"},{"id":138,"name":"USDC Vault","link":"https://harvest.finance/","pair":"USDC","totalStake":49368387.681626,"totalStakeRatio":0.18233214,"rewards":[{"cryptoId":6859,"name":"Harvest Finance","symbol":"FARM","slug":"harvest-finance"},{"cryptoId":6538,"name":"Curve DAO Token","symbol":"CRV","slug":"curve-dao-token"}],"impermanentLoss":"Low","dailyROI":0.0401095890411,"weeklyROI":0.2807671232877,"monthlyROI":1.22,"yearlyROI":14.64,"updateTime":"2021-04-20T11:31:09.000Z"},{"id":136,"name":"WETH Vault","link":"https://harvest.finance/","pair":"WETH","totalStake":14317185.480822224,"totalStakeRatio":0.05287763,"rewards":[{"cryptoId":6859,"name":"Harvest Finance","symbol":"FARM","slug":"harvest-finance"},{"cryptoId":6193,"name":"Cream Finance","symbol":"CREAM","slug":"cream-finance"}],"impermanentLoss":"None","dailyROI":0.018,"weeklyROI":0.126,"monthlyROI":0.5475,"yearlyROI":6.57,"updateTime":"2021-04-20T11:31:08.000Z"},{"id":137,"name":"DAI Vault","link":"https://harvest.finance/","pair":"DAI","totalStake":13152912.37259854,"totalStakeRatio":0.04857762,"rewards":[{"cryptoId":6859,"name":"Harvest Finance","symbol":"FARM","slug":"harvest-finance"},{"cryptoId":6538,"name":"Curve DAO Token","symbol":"CRV","slug":"curve-dao-token"}],"impermanentLoss":"High","dailyROI":0.04397260273973,"weeklyROI":0.30780821917811,"monthlyROI":1.3375,"yearlyROI":16.05,"updateTime":"2021-04-20T11:31:08.000Z"},{"id":139,"name":"USDT Vault","link":"https://harvest.finance/","pair":"USDT","totalStake":6412426.405836,"totalStakeRatio":0.023683,"rewards":[{"cryptoId":6859,"name":"Harvest Finance","symbol":"FARM","slug":"harvest-finance"},{"cryptoId":6538,"name":"Curve DAO Token","symbol":"CRV","slug":"curve-dao-token"}],"impermanentLoss":"Low","dailyROI":0.03890410958904,"weeklyROI":0.27232876712328,"monthlyROI":1.18333333333333,"yearlyROI":14.2,"updateTime":"2021-04-20T11:31:09.000Z"},{"id":141,"name":"WBTC Vault","link":"https://harvest.finance/","pair":"WBTC","totalStake":1905686.0173395,"totalStakeRatio":0.00703827,"rewards":[{"cryptoId":6859,"name":"Harvest Finance","symbol":"FARM","slug":"harvest-finance"},{"cryptoId":6538,"name":"Curve DAO Token","symbol":"CRV","slug":"curve-dao-token"}],"impermanentLoss":"Low","dailyROI":0.00430136986301,"weeklyROI":0.03010958904107,"monthlyROI":0.13083333333333,"yearlyROI":1.57,"updateTime":"2021-04-20T11:31:10.000Z"}],"hasNew":0},{"id":"5f5b5b9cb761c05513d83568","name":"Synthetix","platform":"Ethereum","webSite":"https://mintr.synthetix.io/","totalValueLocked":192146030.16113365,"poolList":[{"id":18,"name":"Curve sUSD","link":"https://mintr.synthetix.io/","pair":"sUSD","totalStake":192146030.16113365,"totalStakeRatio":1,"rewards":[{"cryptoId":2586,"name":"Synthetix","symbol":"SNX","slug":"synthetix-network-token"},{"cryptoId":6538,"name":"Curve DAO Token","symbol":"CRV","slug":"curve-dao-token"}],"impermanentLoss":"None","dailyROI":0.01129369863014,"weeklyROI":0.07905589041098,"monthlyROI":0.34351666666667,"yearlyROI":4.1222,"updateTime":"2021-04-15T10:00:22.000Z"}],"auditList":[{"url":"https://docs.synthetix.io/contracts/audits/","auditFirm":"Iosiro"}],"hasNew":0},{"id":"5f787c8daba1f33645724c99","name":"SUN","platform":"Tron","webSite":"https://sun.io/","totalValueLocked":181926764,"poolList":[{"id":155,"name":"USDT/TRX LP Pool","link":"https://sun.io/#/sun","pair":"USDT-TRX","totalStake":53329235,"totalStakeRatio":0.29313573,"rewards":[{"cryptoId":6990,"name":"SUN","symbol":"SUN","slug":"sun"}],"impermanentLoss":"High","dailyROI":0.06135123287671,"weeklyROI":0.42945863013697,"monthlyROI":1.8661,"yearlyROI":22.3932,"updateTime":"2020-11-18T15:31:13.000Z"},{"id":150,"name":"HT Pool","link":"https://sun.io/#/sun","pair":"HT","totalStake":42604805,"totalStakeRatio":0.23418657,"rewards":[{"cryptoId":6990,"name":"SUN","symbol":"SUN","slug":"sun"}],"impermanentLoss":"None","dailyROI":0.04730684931507,"weeklyROI":0.33114794520549,"monthlyROI":1.43891666666667,"yearlyROI":17.267,"updateTime":"2020-10-08T06:01:12.000Z"},{"id":153,"name":"SUN/TRX LP Pool","link":"https://sun.io/#/sun","pair":"SUN-TRX","totalStake":28208478,"totalStakeRatio":0.15505403,"rewards":[{"cryptoId":6990,"name":"SUN","symbol":"SUN","slug":"sun"}],"impermanentLoss":"High","dailyROI":0.11598712328767,"weeklyROI":0.81190986301369,"monthlyROI":3.52794166666667,"yearlyROI":42.3353,"updateTime":"2020-11-18T15:31:12.000Z"},{"id":154,"name":"JST/TRX LP Pool","link":"https://sun.io/#/sun","pair":"JST-TRX","totalStake":19554433,"totalStakeRatio":0.10748519,"rewards":[{"cryptoId":6990,"name":"SUN","symbol":"SUN","slug":"sun"}],"impermanentLoss":"High","dailyROI":0.07436383561644,"weeklyROI":0.52054684931508,"monthlyROI":2.2619,"yearlyROI":27.1428,"updateTime":"2020-11-18T15:31:13.000Z"},{"id":156,"name":"SUN Pool","link":"https://sun.io/#/sun","pair":"SUN-TRX","totalStake":14941255,"totalStakeRatio":0.08212786,"rewards":[{"cryptoId":6990,"name":"SUN","symbol":"SUN","slug":"sun"}],"impermanentLoss":"High","dailyROI":0.07299287671233,"weeklyROI":0.51095013698631,"monthlyROI":2.2202,"yearlyROI":26.6424,"updateTime":"2020-11-18T15:31:13.000Z"},{"id":163,"name":"USDJ/TRX LP Pool","link":"https://sun.io/#/sun","pair":"USDJ-TRX","totalStake":10905012,"totalStakeRatio":0.05994177,"rewards":[{"cryptoId":6990,"name":"SUN","symbol":"SUN","slug":"sun"}],"impermanentLoss":"High","dailyROI":0.1000095890411,"weeklyROI":0.7000671232877,"monthlyROI":3.04195833333333,"yearlyROI":36.5035,"updateTime":"2020-11-18T15:31:15.000Z"},{"id":151,"name":"HT/TRX LP Pool","link":"https://sun.io/#/sun","pair":"HT-TRX","totalStake":9594999,"totalStakeRatio":0.052741,"rewards":[{"cryptoId":6990,"name":"SUN","symbol":"SUN","slug":"sun"}],"impermanentLoss":"High","dailyROI":0.09002465753425,"weeklyROI":0.63017260273975,"monthlyROI":2.73825,"yearlyROI":32.859,"updateTime":"2020-10-08T06:01:12.000Z"},{"id":161,"name":"WIN/TRX LP Pool","link":"https://sun.io/#/sun","pair":"WIN-TRX","totalStake":2788547,"totalStakeRatio":0.01532785,"rewards":[{"cryptoId":6990,"name":"SUN","symbol":"SUN","slug":"sun"}],"impermanentLoss":"High","dailyROI":0.13036739726027,"weeklyROI":0.91257178082189,"monthlyROI":3.96534166666667,"yearlyROI":47.5841,"updateTime":"2020-11-18T15:31:15.000Z"}],"hasNew":0},{"id":"5f685b38fcdfe7080cdd0fbb","name":"BakerySwap","platform":"Binance Smart Chain","webSite":"https://www.bakeryswap.org/","totalValueLocked":152765555.35,"poolList":[{"id":103,"name":"Bread","link":"https://www.bakeryswap.org/#/bakery/BAKE","pair":"BAKE","totalStake":63556465.93,"totalStakeRatio":0.41603924,"rewards":[{"cryptoId":7064,"name":"BakeryToken","symbol":"BAKE","slug":"bakerytoken"}],"impermanentLoss":"High","dailyROI":0.04180821917808,"weeklyROI":0.29265753424656,"monthlyROI":1.27166666666667,"yearlyROI":15.26,"updateTime":"2021-04-20T11:31:04.000Z"},{"id":109,"name":"Cake","link":"https://www.bakeryswap.org/#/bakery/BTC-BNB%20BLP","pair":"BTC-BNB","totalStake":49416586.55,"totalStakeRatio":0.3234799,"rewards":[{"cryptoId":7064,"name":"BakeryToken","symbol":"BAKE","slug":"bakerytoken"}],"impermanentLoss":"High","dailyROI":0.08961643835616,"weeklyROI":0.62731506849312,"monthlyROI":2.72583333333333,"yearlyROI":32.71,"updateTime":"2021-04-20T11:31:04.000Z"},{"id":104,"name":"Doughnut","link":"https://www.bakeryswap.org/#/bakery/BAKE-BNB%20BLP","pair":"BAKE-BNB","totalStake":33278627.98,"totalStakeRatio":0.21784117,"rewards":[{"cryptoId":7064,"name":"BakeryToken","symbol":"BAKE","slug":"bakerytoken"}],"impermanentLoss":"High","dailyROI":0.11408219178082,"weeklyROI":0.79857534246574,"monthlyROI":3.47,"yearlyROI":41.64,"updateTime":"2021-04-20T11:31:05.000Z"},{"id":105,"name":"Waffle","link":"https://www.bakeryswap.org/#/bakery/BAKE-BUSD%20BLP","pair":"BAKE-BUSD","totalStake":3809030.74,"totalStakeRatio":0.02493383,"rewards":[{"cryptoId":7064,"name":"BakeryToken","symbol":"BAKE","slug":"bakerytoken"}],"impermanentLoss":"High","dailyROI":0.26575342465753,"weeklyROI":1.86027397260271,"monthlyROI":8.08333333333333,"yearlyROI":97,"updateTime":"2021-04-20T11:31:04.000Z"},{"id":107,"name":"Croissant","link":"https://www.bakeryswap.org/#/bakery/BUSD-BNB%20BLP","pair":"BUSD-BNB","totalStake":1826515.64,"totalStakeRatio":0.01195633,"rewards":[{"cryptoId":7064,"name":"BakeryToken","symbol":"BAKE","slug":"bakerytoken"}],"impermanentLoss":"High","dailyROI":0.20783561643836,"weeklyROI":1.45484931506852,"monthlyROI":6.32166666666667,"yearlyROI":75.86,"updateTime":"2021-04-20T11:31:04.000Z"},{"id":108,"name":"Toast","link":"https://www.bakeryswap.org/#/bakery/ETH-BNB%20BLP","pair":"ETH-BNB","totalStake":878328.51,"totalStakeRatio":0.00574952,"rewards":[{"cryptoId":7064,"name":"BakeryToken","symbol":"BAKE","slug":"bakerytoken"}],"impermanentLoss":"High","dailyROI":0.14405479452055,"weeklyROI":1.00838356164385,"monthlyROI":4.38166666666667,"yearlyROI":52.58,"updateTime":"2021-04-20T11:31:05.000Z"}],"hasNew":0},{"id":"5f86b154cc06881662044a5c","name":"Flamincome","platform":"Ethereum","webSite":"https://flamincome.finance/","totalValueLocked":102436324.81345797,"poolList":[{"id":184,"name":"WBTC VAULT","link":"https://app.flamincome.finance/","pair":"WBTC","totalStake":47152065.97592938,"totalStakeRatio":0.46030611,"rewards":[{"cryptoId":3717,"name":"Wrapped Bitcoin","symbol":"WBTC","slug":"wrapped-bitcoin"}],"impermanentLoss":"None","dailyROI":0.01076712328767,"weeklyROI":0.07536986301369,"monthlyROI":0.3275,"yearlyROI":3.93,"updateTime":"2021-04-20T11:31:22.000Z"},{"id":183,"name":"USDT VAULT","link":"https://app.flamincome.finance/","pair":"USDT","totalStake":33057976.21681692,"totalStakeRatio":0.32271732,"rewards":[{"cryptoId":825,"name":"Tether","symbol":"USDT","slug":"tether"}],"impermanentLoss":"None","dailyROI":0.00950684931507,"weeklyROI":0.06654794520549,"monthlyROI":0.28916666666667,"yearlyROI":3.47,"updateTime":"2021-04-20T11:31:22.000Z"},{"id":185,"name":"WETH VAULT","link":"https://app.flamincome.finance/","pair":"WETH","totalStake":22226282.620711666,"totalStakeRatio":0.21697657,"rewards":[{"cryptoId":2396,"name":"WETH","symbol":"WETH","slug":"weth"}],"impermanentLoss":"None","dailyROI":0.00090410958904,"weeklyROI":0.00632876712328,"monthlyROI":0.0275,"yearlyROI":0.33,"updateTime":"2021-04-20T11:31:23.000Z"}],"hasNew":0},{"id":"5f5b5b9cb761c05513d8356a","name":"Yearn","platform":"Ethereum","webSite":"https://yearn.finance/vaults","totalValueLocked":95063339.64427319,"poolList":[{"id":26,"name":"yCRV Vault","link":"https://yearn.finance/vaults","pair":"yCRV","totalStake":43339857.72372348,"totalStakeRatio":0.45590506,"rewards":[{"cryptoId":6538,"name":"Curve DAO Token","symbol":"CRV","slug":"curve-dao-token"}],"impermanentLoss":"NONE","dailyROI":0.03170356164384,"weeklyROI":0.22192493150688,"monthlyROI":0.96431666666667,"yearlyROI":11.5718,"updateTime":"2021-04-20T11:30:27.000Z"},{"id":21,"name":"aLINK Vault","link":"https://yearn.finance/vaults","pair":"aLINK","totalStake":14518975.416509617,"totalStakeRatio":0.15272949,"rewards":[{"cryptoId":5751,"name":"Aave LINK","symbol":"ALINK","slug":"aave-link"}],"impermanentLoss":"NONE","dailyROI":0.00000849315068,"weeklyROI":0.00005945205476,"monthlyROI":0.00025833333333,"yearlyROI":0.0031,"updateTime":"2021-04-20T11:30:29.000Z"},{"id":22,"name":"DAI Vault","link":"https://yearn.finance/vaults","pair":"DAI","totalStake":13178954.544678444,"totalStakeRatio":0.13863341,"rewards":[{"cryptoId":4943,"name":"Dai","symbol":"DAI","slug":"multi-collateral-dai"}],"impermanentLoss":"NONE","dailyROI":0.08123945205479,"weeklyROI":0.56867616438353,"monthlyROI":2.47103333333333,"yearlyROI":29.6524,"updateTime":"2021-04-20T11:30:29.000Z"},{"id":24,"name":"USDC Vault","link":"https://yearn.finance/vaults","pair":"USDC","totalStake":11117162.444132,"totalStakeRatio":0.11694479,"rewards":[{"cryptoId":3408,"name":"USD Coin","symbol":"USDC","slug":"usd-coin"}],"impermanentLoss":"NONE","dailyROI":0.08383506849315,"weeklyROI":0.58684547945205,"monthlyROI":2.54998333333333,"yearlyROI":30.5998,"updateTime":"2021-04-20T11:30:28.000Z"},{"id":25,"name":"USDT Vault","link":"https://yearn.finance/vaults","pair":"USDT","totalStake":9617217.255204,"totalStakeRatio":0.10116641,"rewards":[{"cryptoId":825,"name":"Tether","symbol":"USDT","slug":"tether"}],"impermanentLoss":"NONE","dailyROI":0.07985452054795,"weeklyROI":0.55898164383565,"monthlyROI":2.42890833333333,"yearlyROI":29.1469,"updateTime":"2021-04-20T11:30:28.000Z"},{"id":23,"name":"TUSD Vault","link":"https://yearn.finance/vaults","pair":"TUSD","totalStake":3291172.260025648,"totalStakeRatio":0.03462084,"rewards":[{"cryptoId":2563,"name":"TrueUSD","symbol":"TUSD","slug":"trueusd"}],"impermanentLoss":"NONE","dailyROI":0.08531369863014,"weeklyROI":0.59719589041098,"monthlyROI":2.59495833333333,"yearlyROI":31.1395,"updateTime":"2021-04-20T11:30:28.000Z"}],"auditList":[{"url":"https://github.com/iearn-finance/audits/blob/master/Certik%20-%20itoken-finance-audit-report-1.1.0.pdf","auditFirm":"Certik"},{"url":"https://github.com/iearn-finance/audits/blob/master/CryptoManiacs%20%20-%20Audit%20of%20iearn.finance%20by%20CryptoManiacs%20-%20HackMD.pdf","auditFirm":"CryptoManiacs"},{"url":"https://github.com/iearn-finance/audits/blob/master/Quantstamp%20-%20Yearn.Finance%20Security%20Review.pdf","auditFirm":"Quantstamp"},{"url":"https://github.com/iearn-finance/audits/blob/master/StrategyCurveYCRV.sol%20-%20HackMD.pdf","auditFirm":"HackMD"}],"hasNew":0},{"id":"5f5b5b9cb761c05513d83566","name":"dForce","platform":"Ethereum","webSite":"https://staking.dforce.network/dapp","totalValueLocked":85987737.45764147,"poolList":[{"id":6,"name":"dUSDT/dUSDC/dDAI","link":"https://markets.dforce.network/","pair":"dUSDT-dUSDC-dDAI","totalStake":85374034.78,"totalStakeRatio":0.9928629,"rewards":[{"cryptoId":4758,"name":"dForce","symbol":"DF","slug":"dforce"}],"impermanentLoss":"None","dailyROI":0.00320767123288,"weeklyROI":0.02245369863016,"monthlyROI":0.09756666666667,"yearlyROI":1.1708,"updateTime":"2020-10-20T02:27:26.000Z"},{"id":5,"name":"Uniswap DF-USDx","link":"https://usr.dforce.network/","pair":"DF-USDx","totalStake":532663.9133717071,"totalStakeRatio":0.00619465,"rewards":[{"cryptoId":4758,"name":"dForce","symbol":"DF","slug":"dforce"}],"impermanentLoss":"None","dailyROI":0.04866876712329,"weeklyROI":0.34068136986303,"monthlyROI":1.48034166666667,"yearlyROI":17.7641,"updateTime":"2021-04-20T11:30:25.000Z"},{"id":7,"name":"Uniswap GOLDx-USDx","link":"https://goldx.dforce.network/","pair":"GOLDx-USDx","totalStake":81038.7642697576,"totalStakeRatio":0.00094245,"rewards":[{"cryptoId":4758,"name":"dForce","symbol":"DF","slug":"dforce"}],"impermanentLoss":"None","dailyROI":0.07057068493151,"weeklyROI":0.49399479452057,"monthlyROI":2.146525,"yearlyROI":25.7583,"updateTime":"2021-04-20T11:30:27.000Z"}],"auditList":[{"url":"https://github.com/peckshield/publications#dforce-network","auditFirm":"Peckshield"}],"hasNew":0},{"id":"5f5c6731037be201be4a7129","name":"Swerve","platform":"Ethereum","webSite":"https://swerve.fi/","totalValueLocked":25852843.680346794,"poolList":[{"id":67,"name":"swUSD","link":"http://ipfs2.swerve.fi/#/swusd","pair":"DAI-USDC-USDT-TUSD","totalStake":25852843.680346794,"totalStakeRatio":1,"rewards":[{"cryptoId":6901,"name":"Swerve","symbol":"SWRV","slug":"swerve"}],"impermanentLoss":"Low","dailyROI":0.17115890410959,"weeklyROI":1.19811232876713,"monthlyROI":5.20608333333333,"yearlyROI":62.473,"updateTime":"2021-04-15T10:00:47.000Z"}],"hasNew":0},{"id":"5f685b27fcdfe7080cdd0fba","name":"Fortube","platform":"Ethereum","webSite":"https://for.tube","totalValueLocked":22788623,"poolList":[{"id":78,"name":"USDT Vault","link":"https://for.tube/bank/home","pair":"USDT","totalStake":9588306,"totalStakeRatio":0.42074969,"rewards":[{"cryptoId":4118,"name":"ForTube","symbol":"FOR","slug":"the-force-protocol"}],"impermanentLoss":"None","dailyROI":0.00948191780822,"weeklyROI":0.06637342465754,"monthlyROI":0.28840833333333,"yearlyROI":3.4609,"updateTime":"2020-11-17T04:33:53.000Z"},{"id":82,"name":"FOR Vault","link":"https://for.tube/bank/home","pair":"FOR","totalStake":5097528,"totalStakeRatio":0.22368741,"rewards":[{"cryptoId":4118,"name":"ForTube","symbol":"FOR","slug":"the-force-protocol"}],"impermanentLoss":"None","dailyROI":0.01422273972603,"weeklyROI":0.09955917808221,"monthlyROI":0.43260833333333,"yearlyROI":5.1913,"updateTime":"2020-11-17T04:33:54.000Z"},{"id":83,"name":"ETH Vault","link":"https://for.tube/bank/home","pair":"ETH","totalStake":3176820,"totalStakeRatio":0.13940377,"rewards":[{"cryptoId":4118,"name":"ForTube","symbol":"FOR","slug":"the-force-protocol"}],"impermanentLoss":"None","dailyROI":0.00355561643836,"weeklyROI":0.02488931506852,"monthlyROI":0.10815,"yearlyROI":1.2978,"updateTime":"2020-11-17T04:33:54.000Z"},{"id":84,"name":"HBTC Vault","link":"https://for.tube/bank/home","pair":"HBTC","totalStake":1938891,"totalStakeRatio":0.08508153,"rewards":[{"cryptoId":4118,"name":"ForTube","symbol":"FOR","slug":"the-force-protocol"}],"impermanentLoss":"None","dailyROI":0.00355561643836,"weeklyROI":0.02488931506852,"monthlyROI":0.10815,"yearlyROI":1.2978,"updateTime":"2020-11-17T04:33:54.000Z"},{"id":79,"name":"USDC Vault","link":"https://for.tube/bank/home","pair":"USDC","totalStake":1367397,"totalStakeRatio":0.06000349,"rewards":[{"cryptoId":4118,"name":"ForTube","symbol":"FOR","slug":"the-force-protocol"}],"impermanentLoss":"None","dailyROI":0.00948191780822,"weeklyROI":0.06637342465754,"monthlyROI":0.28840833333333,"yearlyROI":3.4609,"updateTime":"2020-11-17T04:33:53.000Z"},{"id":80,"name":"BUSD Vault","link":"https://for.tube/bank/home","pair":"BUSD","totalStake":1100342,"totalStakeRatio":0.04828471,"rewards":[{"cryptoId":4118,"name":"ForTube","symbol":"FOR","slug":"the-force-protocol"}],"impermanentLoss":"None","dailyROI":0.00948191780822,"weeklyROI":0.06637342465754,"monthlyROI":0.28840833333333,"yearlyROI":3.4609,"updateTime":"2020-11-17T04:33:53.000Z"},{"id":77,"name":"WBTC Vault","link":"https://for.tube/bank/home","pair":"WBTC","totalStake":218726,"totalStakeRatio":0.00959803,"rewards":[{"cryptoId":4118,"name":"ForTube","symbol":"FOR","slug":"the-force-protocol"}],"impermanentLoss":"None","dailyROI":0.00355561643836,"weeklyROI":0.02488931506852,"monthlyROI":0.10815,"yearlyROI":1.2978,"updateTime":"2020-11-17T04:33:53.000Z"},{"id":81,"name":"DAI Vault","link":"https://for.tube/bank/home","pair":"DAI","totalStake":152322,"totalStakeRatio":0.00668412,"rewards":[{"cryptoId":4118,"name":"ForTube","symbol":"FOR","slug":"the-force-protocol"}],"impermanentLoss":"None","dailyROI":0.00948191780822,"weeklyROI":0.06637342465754,"monthlyROI":0.28840833333333,"yearlyROI":3.4609,"updateTime":"2020-11-17T04:33:53.000Z"},{"id":87,"name":"YFII Vault","link":"https://for.tube/bank/home","pair":"YFII","totalStake":99696,"totalStakeRatio":0.00437481,"rewards":[{"cryptoId":4118,"name":"ForTube","symbol":"FOR","slug":"the-force-protocol"}],"impermanentLoss":"None","dailyROI":0.00071123287671,"weeklyROI":0.00497863013697,"monthlyROI":0.02163333333333,"yearlyROI":0.2596,"updateTime":"2020-11-17T04:33:55.000Z"},{"id":85,"name":"YYDAI+YUSDC+YUSDT+YTUSD Vault","link":"https://for.tube/bank/home","pair":"yyDAI+yUSDC+yUSDT+yTUSD","totalStake":48595,"totalStakeRatio":0.00213242,"rewards":[{"cryptoId":4118,"name":"ForTube","symbol":"FOR","slug":"the-force-protocol"}],"impermanentLoss":"None","dailyROI":0.00948191780822,"weeklyROI":0.06637342465754,"monthlyROI":0.28840833333333,"yearlyROI":3.4609,"updateTime":"2020-11-17T04:33:55.000Z"}],"hasNew":0},{"id":"600004163c1b4b4fdf0bb038","name":"Saffron Finance","platform":"Ethereum","webSite":"https://saffron.finance","totalValueLocked":21830240.291052356,"poolList":[{"id":210,"name":"SFI Staking Pool","link":"https://saffron.finance","pair":"SFI","totalStake":12550338.600799998,"totalStakeRatio":0.57490611,"rewards":[{"cryptoId":7617,"name":"saffron.finance","symbol":"SFI","slug":"saffron-finance"}],"impermanentLoss":"None","dailyROI":0.0484501369863,"weeklyROI":0.3391509589041,"monthlyROI":1.47369166666667,"yearlyROI":17.6843,"updateTime":"2021-04-20T11:31:31.000Z"},{"id":209,"name":"SFI/ETH Uniswap LP Pool","link":"https://saffron.finance","pair":"SFI-ETH","totalStake":3489386.3873999994,"totalStakeRatio":0.15984187,"rewards":[{"cryptoId":7617,"name":"saffron.finance","symbol":"SFI","slug":"saffron-finance"}],"impermanentLoss":"High","dailyROI":0.16686767123288,"weeklyROI":1.16807369863016,"monthlyROI":5.07555833333333,"yearlyROI":60.9067,"updateTime":"2021-04-20T11:31:31.000Z"},{"id":212,"name":"rSFI Staking Pool","link":"https://saffron.finance","pair":"rSFI","totalStake":2947294.6965,"totalStakeRatio":0.13500972,"rewards":[{"cryptoId":7617,"name":"saffron.finance","symbol":"SFI","slug":"saffron-finance"}],"impermanentLoss":"None","dailyROI":0.16889506849315,"weeklyROI":1.18226547945205,"monthlyROI":5.137225,"yearlyROI":61.6467,"updateTime":"2021-01-24T14:52:31.000Z"},{"id":215,"name":"SFI/ETH SushiSwap Pool","link":"https://saffron.finance","pair":"SFI-ETH","totalStake":2565031.6054000002,"totalStakeRatio":0.11749901,"rewards":[{"cryptoId":7617,"name":"saffron.finance","symbol":"SFI","slug":"saffron-finance"}],"impermanentLoss":"High","dailyROI":0.17238904109589,"weeklyROI":1.20672328767123,"monthlyROI":5.2435,"yearlyROI":62.922,"updateTime":"2021-04-20T11:31:32.000Z"},{"id":214,"name":"SFI/ESD Uniswap Pool","link":"https://saffron.finance","pair":"SFI-ESD","totalStake":111864.36355236001,"totalStakeRatio":0.00512428,"rewards":[{"cryptoId":7617,"name":"saffron.finance","symbol":"SFI","slug":"saffron-finance"}],"impermanentLoss":"High","dailyROI":0.29946712328767,"weeklyROI":2.09626986301369,"monthlyROI":9.10879166666667,"yearlyROI":109.3055,"updateTime":"2021-04-20T11:31:32.000Z"},{"id":211,"name":"SFI/BTSE Pool","link":"https://saffron.finance","pair":"SFI-BTSE","totalStake":101941.8992,"totalStakeRatio":0.00466976,"rewards":[{"cryptoId":7617,"name":"saffron.finance","symbol":"SFI","slug":"saffron-finance"}],"impermanentLoss":"High","dailyROI":0.16043068493151,"weeklyROI":1.12301479452057,"monthlyROI":4.87976666666667,"yearlyROI":58.5572,"updateTime":"2021-04-20T11:31:31.000Z"},{"id":213,"name":"SFI/GEEQ Uniswap Pool","link":"https://saffron.finance","pair":"SFI-GEEQ","totalStake":64382.7382,"totalStakeRatio":0.00294925,"rewards":[{"cryptoId":7617,"name":"saffron.finance","symbol":"SFI","slug":"saffron-finance"}],"impermanentLoss":"High","dailyROI":0.29374383561644,"weeklyROI":2.05620684931508,"monthlyROI":8.93470833333333,"yearlyROI":107.2165,"updateTime":"2021-04-20T11:31:32.000Z"}],"hasNew":1},{"id":"5f5b5b9cb761c05513d83567","name":"mStable","platform":"Ethereum","webSite":"https://app.mstable.org/earn","totalValueLocked":5804746.0755305,"poolList":[{"id":8,"name":"Uniswap MTA/WETH 50/50","link":"https://app.mstable.org/earn/uniswap-mta-50-weth-50","pair":"MTA-wETH","totalStake":5804746.0755305,"totalStakeRatio":1,"rewards":[{"cryptoId":5748,"name":"mStable Governance Token: Meta (MTA)","symbol":"MTA","slug":"meta"},{"cryptoId":5728,"name":"Balancer","symbol":"BAL","slug":"balancer"}],"impermanentLoss":"High","dailyROI":0.1956397260274,"weeklyROI":1.3694780821918,"monthlyROI":5.95070833333333,"yearlyROI":71.4085,"updateTime":"2021-04-20T11:30:21.000Z"}],"auditList":[{"url":"https://diligence.consensys.net/audits/2020/07/mstable-1.1/","auditFirm":"Consensys Diligence"},{"url":"https://docs.mstable.org/protocol/security","auditFirm":"Bramah Systems"}],"hasNew":0},{"id":"5f86b154cc06881662044a5b","name":"Bella Protocol","platform":"Ethereum","webSite":"https://bella.fi/","totalValueLocked":3400729.358273354,"poolList":[{"id":181,"name":"BEL-ETH","link":"https://liquidity.bella.fi/","pair":"BEL-ETH","totalStake":1825248.2075416646,"totalStakeRatio":0.53672257,"rewards":[{"cryptoId":6928,"name":"Bella Protocol","symbol":"BEL","slug":"bella-protocol"}],"impermanentLoss":"High","dailyROI":0.36986301369863,"weeklyROI":2.58904109589041,"monthlyROI":11.25,"yearlyROI":135,"updateTime":"2021-04-20T11:31:27.000Z"},{"id":180,"name":"BEL-USDT","link":"https://liquidity.bella.fi/","pair":"BEL-USDT","totalStake":985042.9691239648,"totalStakeRatio":0.28965638,"rewards":[{"cryptoId":6928,"name":"Bella Protocol","symbol":"BEL","slug":"bella-protocol"}],"impermanentLoss":"High","dailyROI":1.36986301369863,"weeklyROI":9.58904109589041,"monthlyROI":41.66666666666667,"yearlyROI":500,"updateTime":"2021-04-20T11:31:27.000Z"},{"id":182,"name":"ARPA-USDT","link":"https://liquidity.bella.fi/","pair":"ARPA-USDT","totalStake":590438.1816077245,"totalStakeRatio":0.17362104,"rewards":[{"cryptoId":6928,"name":"Bella Protocol","symbol":"BEL","slug":"bella-protocol"}],"impermanentLoss":"High","dailyROI":1.14246575342466,"weeklyROI":7.99726027397262,"monthlyROI":34.75,"yearlyROI":417,"updateTime":"2021-04-20T11:31:27.000Z"}],"hasNew":0},{"id":"5f71c840edcba010f8a365b5","name":"HodlTree","platform":"Ethereum","webSite":"https://hodltree.io","totalValueLocked":1975942.171381185,"poolList":[{"id":149,"name":"HodlTree balancer","link":"https://pools.balancer.exchange/#/pool/0x02b77ad79e27ad80a0a0868cc7528520e8442c9b/","pair":"HTRE-USDC","totalStake":1947440.1082000001,"totalStakeRatio":0.98557546,"rewards":[{"cryptoId":7100,"name":"HodlTree","symbol":"HTRE","slug":"hodltree"}],"impermanentLoss":"High","dailyROI":0.28518904109589,"weeklyROI":1.99632328767123,"monthlyROI":8.6745,"yearlyROI":104.094,"updateTime":"2021-04-20T11:31:13.000Z"},{"id":148,"name":"HodlTree uniswap","link":"https://uniswap.info/pair/0x57e69e4385896fa4511f958e88d8775fd6a8c6c0","pair":"HTRE-USDC","totalStake":28502.063181185,"totalStakeRatio":0.01442454,"rewards":[{"cryptoId":7100,"name":"HodlTree","symbol":"HTRE","slug":"hodltree"}],"impermanentLoss":"High","dailyROI":0.28518904109589,"weeklyROI":1.99632328767123,"monthlyROI":8.6745,"yearlyROI":104.094,"updateTime":"2021-04-20T11:01:13.000Z"}],"hasNew":0},{"id":"5f6b21051a3d2007bc5ea1bb","name":"PerlinX","platform":"Ethereum","webSite":"https://perlinx.finance/","totalValueLocked":1017462.378677196,"poolList":[{"id":121,"name":"Balancer WETH-PERL 50/50","link":"https://app.perlinx.finance/pools/0x8C7769F9F1E5042C0809b8702e4b9947b1Bcb3f3","pair":"WETH-PERL","totalStake":653907.5691423632,"totalStakeRatio":0.64268476,"rewards":[{"cryptoId":4293,"name":"Perlin","symbol":"PERL","slug":"perlin"},{"cryptoId":5728,"name":"Balancer","symbol":"BAL","slug":"balancer"}],"impermanentLoss":"High","dailyROI":0.34463342465753,"weeklyROI":2.41243397260271,"monthlyROI":10.4826,"yearlyROI":125.7912,"updateTime":"2020-10-06T23:49:08.000Z"},{"id":122,"name":"Balancer TUSD-PERL 50/50","link":"https://app.perlinx.finance/pools/0x0BdF7EFEf728308B6F55b1dD8D0c714f0d5d233f","pair":"TUSD-PERL","totalStake":154035.40062250657,"totalStakeRatio":0.15139174,"rewards":[{"cryptoId":4293,"name":"Perlin","symbol":"PERL","slug":"perlin"},{"cryptoId":5728,"name":"Balancer","symbol":"BAL","slug":"balancer"}],"impermanentLoss":"High","dailyROI":0.29445835616438,"weeklyROI":2.06120849315066,"monthlyROI":8.95644166666667,"yearlyROI":107.4773,"updateTime":"2020-10-06T22:34:08.000Z"},{"id":123,"name":"Balancer BUSD-PERL 50/50","link":"https://app.perlinx.finance/pools/0x19F4611C61e2eE6D2FaDFccBde1e95cFcfd1E210","pair":"BUSD-PERL","totalStake":108925.26551513521,"totalStakeRatio":0.10705582,"rewards":[{"cryptoId":4293,"name":"Perlin","symbol":"PERL","slug":"perlin"},{"cryptoId":5728,"name":"Balancer","symbol":"BAL","slug":"balancer"}],"impermanentLoss":"High","dailyROI":0.44221917808219,"weeklyROI":3.09553424657533,"monthlyROI":13.45083333333333,"yearlyROI":161.41,"updateTime":"2020-10-06T23:52:09.000Z"},{"id":124,"name":"Balancer DAI-PERL 50/50\"","link":"https://app.perlinx.finance/pools/0x0B0Dea284a07d60d026691476b130f160e48BD0A","pair":"DAI-PERL","totalStake":87350.24405015854,"totalStakeRatio":0.08585108,"rewards":[{"cryptoId":4293,"name":"Perlin","symbol":"PERL","slug":"perlin"},{"cryptoId":5728,"name":"Balancer","symbol":"BAL","slug":"balancer"}],"impermanentLoss":"High","dailyROI":0.38915835616438,"weeklyROI":2.72410849315066,"monthlyROI":11.8369,"yearlyROI":142.0428,"updateTime":"2020-10-06T22:28:09.000Z"},{"id":125,"name":"Balancer BAL-PERL 50/50","link":"https://app.perlinx.finance/pools/0x2C1cB70Cccf250B35Ca2CB021E2F624aBa76e3e8","pair":"BAL-PERL","totalStake":13243.899347032466,"totalStakeRatio":0.0130166,"rewards":[{"cryptoId":4293,"name":"Perlin","symbol":"PERL","slug":"perlin"},{"cryptoId":5728,"name":"Balancer","symbol":"BAL","slug":"balancer"}],"impermanentLoss":"High","dailyROI":0.31130739726027,"weeklyROI":2.17915178082189,"monthlyROI":9.46893333333333,"yearlyROI":113.6272,"updateTime":"2020-10-06T22:37:09.000Z"}],"hasNew":0},{"id":"600004163c1b4b4fdf0bb037","name":"Mithril Cash","platform":"Ethereum","webSite":"https://mith.cash/","totalValueLocked":836937,"poolList":[{"id":208,"name":"MIC_USDT-SUSHI-LPV2","link":"https://mith.cash/","pair":"MIC-USDT","totalStake":718503,"totalStakeRatio":0.85849114,"rewards":[{"cryptoId":8141,"name":"Mithril Share","symbol":"MIS","slug":"mithril-share"}],"impermanentLoss":"High","dailyROI":0.00860821917808,"weeklyROI":0.06025753424656,"monthlyROI":0.26183333333333,"yearlyROI":3.142,"updateTime":"2021-04-20T11:31:31.000Z"},{"id":207,"name":"MIS_USDT-SUSHI-LPV2","link":"https://mith.cash/","pair":"MIS-USDT","totalStake":118434,"totalStakeRatio":0.14150886,"rewards":[{"cryptoId":8141,"name":"Mithril Share","symbol":"MIS","slug":"mithril-share"}],"impermanentLoss":"High","dailyROI":0.01376410958904,"weeklyROI":0.09634876712328,"monthlyROI":0.41865833333333,"yearlyROI":5.0239,"updateTime":"2021-04-20T11:31:31.000Z"}],"hasNew":1},{"id":"5f86b154cc06881662044a5d","name":"S.Finance","platform":"Ethereum","webSite":"https://s.finance","totalValueLocked":235955.9682400575,"poolList":[{"id":164,"name":"sUSD liquidity gauge","link":"https://s.finance/dao","pair":"DAI-USDT-USDC-sUSD","totalStake":117073.83291937767,"totalStakeRatio":0.49616814,"rewards":[{"cryptoId":7187,"name":"S.Finance","symbol":"SFG","slug":"s-finance"},{"cryptoId":6538,"name":"Curve DAO Token","symbol":"CRV","slug":"curve-dao-token"},{"cryptoId":2586,"name":"Synthetix","symbol":"SNX","slug":"synthetix-network-token"}],"impermanentLoss":"Low","dailyROI":0.18396849315068,"weeklyROI":1.28777945205476,"monthlyROI":5.59570833333333,"yearlyROI":67.1485,"updateTime":"2021-04-20T11:31:17.000Z"},{"id":167,"name":"dfi liquidity gauge","link":"https://s.finance/dao","pair":"DAI-USDC-USDT","totalStake":103886.31555852525,"totalStakeRatio":0.4402784,"rewards":[{"cryptoId":7187,"name":"S.Finance","symbol":"SFG","slug":"s-finance"}],"impermanentLoss":"Low","dailyROI":0.76820876712329,"weeklyROI":5.37746136986303,"monthlyROI":23.36635,"yearlyROI":280.3962,"updateTime":"2021-04-20T11:31:18.000Z"},{"id":165,"name":"SFG liquidity gauge","link":"https://s.finance/dao","pair":"SFG-DAI","totalStake":14995.81976215459,"totalStakeRatio":0.06355347,"rewards":[{"cryptoId":7187,"name":"S.Finance","symbol":"SFG","slug":"s-finance"}],"impermanentLoss":"High","dailyROI":1.43464794520548,"weeklyROI":10.04253561643836,"monthlyROI":43.63720833333333,"yearlyROI":523.6465,"updateTime":"2021-04-20T11:31:18.000Z"}],"hasNew":0}],"totalPoolLiquidity":22736372211.40627,"apyList":[{"id":"5f86b154cc06881662044a5a","name":"PancakeSwap","platform":"Binance Smart Chain","webSite":"https://pancakeswap.finance/","totalValueLocked":8115393879.487392,"auditList":[{"url":"https://github.com/certikfoundation-shared/CertiK-Audits/blob/master/reports/REP-PancakeSwap-16_10_2020.pdf","auditFirm":"CertiK"}],"hasNew":0,"poolId":177,"poolName":"PancakeSWAP DAI-BNB","link":"https://pancakeswap.finance/farms/DAI-BNB%20FLP","pair":"DAI-BNB","totalStake":132334.6820171771,"totalStakeRatio":0.00001631,"rewards":[{"cryptoId":7186,"name":"PancakeSwap","symbol":"CAKE","slug":"pancakeswap"}],"impermanentLoss":"High","dailyROI":103.30202273972603,"yearlyROI":37705.2383},{"id":"5f86b154cc06881662044a5a","name":"PancakeSwap","platform":"Binance Smart Chain","webSite":"https://pancakeswap.finance/","totalValueLocked":8115393879.487392,"auditList":[{"url":"https://github.com/certikfoundation-shared/CertiK-Audits/blob/master/reports/REP-PancakeSwap-16_10_2020.pdf","auditFirm":"CertiK"}],"hasNew":0,"poolId":176,"poolName":"PancakeSWAP YFII-BNB","link":"https://pancakeswap.finance/farms/YFII-BNB%20FLP","pair":"YFII-BNB","totalStake":136849.07803390583,"totalStakeRatio":0.00001686,"rewards":[{"cryptoId":7186,"name":"PancakeSwap","symbol":"CAKE","slug":"pancakeswap"}],"impermanentLoss":"High","dailyROI":99.89428164383563,"yearlyROI":36461.4128},{"id":"5f86b154cc06881662044a5a","name":"PancakeSwap","platform":"Binance Smart Chain","webSite":"https://pancakeswap.finance/","totalValueLocked":8115393879.487392,"auditList":[{"url":"https://github.com/certikfoundation-shared/CertiK-Audits/blob/master/reports/REP-PancakeSwap-16_10_2020.pdf","auditFirm":"CertiK"}],"hasNew":0,"poolId":178,"poolName":"PancakeSWAP XTZ-BNB","link":"https://pancakeswap.finance/farms/XTZ-BNB%20FLP","pair":"XTZ-BNB","totalStake":617922.8690560703,"totalStakeRatio":0.00007614,"rewards":[{"cryptoId":7186,"name":"PancakeSwap","symbol":"CAKE","slug":"pancakeswap"}],"impermanentLoss":"High","dailyROI":22.12321479452055,"yearlyROI":8074.9734},{"id":"5f86b154cc06881662044a5a","name":"PancakeSwap","platform":"Binance Smart Chain","webSite":"https://pancakeswap.finance/","totalValueLocked":8115393879.487392,"auditList":[{"url":"https://github.com/certikfoundation-shared/CertiK-Audits/blob/master/reports/REP-PancakeSwap-16_10_2020.pdf","auditFirm":"CertiK"}],"hasNew":0,"poolId":179,"poolName":"PancakeSWAP BCH-BNB","link":"https://pancakeswap.finance/farms/BCH-BNB%20FLP","pair":"BCH-BNB","totalStake":1063861.0315633444,"totalStakeRatio":0.00013109,"rewards":[{"cryptoId":7186,"name":"PancakeSwap","symbol":"CAKE","slug":"pancakeswap"}],"impermanentLoss":"High","dailyROI":12.84983643835616,"yearlyROI":4690.1903},{"id":"5f86b154cc06881662044a5a","name":"PancakeSwap","platform":"Binance Smart Chain","webSite":"https://pancakeswap.finance/","totalValueLocked":8115393879.487392,"auditList":[{"url":"https://github.com/certikfoundation-shared/CertiK-Audits/blob/master/reports/REP-PancakeSwap-16_10_2020.pdf","auditFirm":"CertiK"}],"hasNew":0,"poolId":132,"poolName":"PancakeSWAP EOS-BNB","link":"https://pancakeswap.finance/farms/EOS-BNB%20FLIP","pair":"EOS-WBNB","totalStake":7709563.3947910145,"totalStakeRatio":0.00094999,"rewards":[{"cryptoId":7186,"name":"PancakeSwap","symbol":"CAKE","slug":"pancakeswap"}],"impermanentLoss":"High","dailyROI":1.77317945205479,"yearlyROI":647.2105},{"id":"5f86b154cc06881662044a5a","name":"PancakeSwap","platform":"Binance Smart Chain","webSite":"https://pancakeswap.finance/","totalValueLocked":8115393879.487392,"auditList":[{"url":"https://github.com/certikfoundation-shared/CertiK-Audits/blob/master/reports/REP-PancakeSwap-16_10_2020.pdf","auditFirm":"CertiK"}],"hasNew":0,"poolId":169,"poolName":"PancakeSWAP TWT-BNB","link":"https://pancakeswap.finance/farms/TWT-BNB%20FLP","pair":"TWT-BNB","totalStake":18803965.596320003,"totalStakeRatio":0.00231707,"rewards":[{"cryptoId":7186,"name":"PancakeSwap","symbol":"CAKE","slug":"pancakeswap"}],"impermanentLoss":"High","dailyROI":1.45399534246575,"yearlyROI":530.7083},{"id":"5f86b154cc06881662044a5d","name":"S.Finance","platform":"Ethereum","webSite":"https://s.finance","totalValueLocked":235955.9682400575,"hasNew":0,"poolId":165,"poolName":"SFG liquidity gauge","link":"https://s.finance/dao","pair":"SFG-DAI","totalStake":14995.81976215459,"totalStakeRatio":0.06355347,"rewards":[{"cryptoId":7187,"name":"S.Finance","symbol":"SFG","slug":"s-finance"}],"impermanentLoss":"High","dailyROI":1.43464794520548,"yearlyROI":523.6465},{"id":"5f86b154cc06881662044a5a","name":"PancakeSwap","platform":"Binance Smart Chain","webSite":"https://pancakeswap.finance/","totalValueLocked":8115393879.487392,"auditList":[{"url":"https://github.com/certikfoundation-shared/CertiK-Audits/blob/master/reports/REP-PancakeSwap-16_10_2020.pdf","auditFirm":"CertiK"}],"hasNew":0,"poolId":175,"poolName":"PancakeSWAP ATOM-BNB","link":"https://pancakeswap.finance/farms/ATOM-BNB%20FLP","pair":"ATOM-BNB","totalStake":9911690.29667046,"totalStakeRatio":0.00122134,"rewards":[{"cryptoId":7186,"name":"PancakeSwap","symbol":"CAKE","slug":"pancakeswap"}],"impermanentLoss":"High","dailyROI":1.37922383561644,"yearlyROI":503.4167},{"id":"5f86b154cc06881662044a5b","name":"Bella Protocol","platform":"Ethereum","webSite":"https://bella.fi/","totalValueLocked":3400729.358273354,"hasNew":0,"poolId":180,"poolName":"BEL-USDT","link":"https://liquidity.bella.fi/","pair":"BEL-USDT","totalStake":985042.9691239648,"totalStakeRatio":0.28965638,"rewards":[{"cryptoId":6928,"name":"Bella Protocol","symbol":"BEL","slug":"bella-protocol"}],"impermanentLoss":"High","dailyROI":1.36986301369863,"yearlyROI":500},{"id":"5f86b154cc06881662044a5b","name":"Bella Protocol","platform":"Ethereum","webSite":"https://bella.fi/","totalValueLocked":3400729.358273354,"hasNew":0,"poolId":182,"poolName":"ARPA-USDT","link":"https://liquidity.bella.fi/","pair":"ARPA-USDT","totalStake":590438.1816077245,"totalStakeRatio":0.17362104,"rewards":[{"cryptoId":6928,"name":"Bella Protocol","symbol":"BEL","slug":"bella-protocol"}],"impermanentLoss":"High","dailyROI":1.14246575342466,"yearlyROI":417},{"id":"5f86b154cc06881662044a5a","name":"PancakeSwap","platform":"Binance Smart Chain","webSite":"https://pancakeswap.finance/","totalValueLocked":8115393879.487392,"auditList":[{"url":"https://github.com/certikfoundation-shared/CertiK-Audits/blob/master/reports/REP-PancakeSwap-16_10_2020.pdf","auditFirm":"CertiK"}],"hasNew":0,"poolId":130,"poolName":"PancakeSWAP BAND-BNB","link":"https://pancakeswap.finance/farms/BAND-BNB%20FLIP","pair":"BAND-WBNB","totalStake":33376027.7536527,"totalStakeRatio":0.00411268,"rewards":[{"cryptoId":7186,"name":"PancakeSwap","symbol":"CAKE","slug":"pancakeswap"}],"impermanentLoss":"High","dailyROI":0.81887808219178,"yearlyROI":298.8905},{"id":"5f86b154cc06881662044a5d","name":"S.Finance","platform":"Ethereum","webSite":"https://s.finance","totalValueLocked":235955.9682400575,"hasNew":0,"poolId":167,"poolName":"dfi liquidity gauge","link":"https://s.finance/dao","pair":"DAI-USDC-USDT","totalStake":103886.31555852525,"totalStakeRatio":0.4402784,"rewards":[{"cryptoId":7187,"name":"S.Finance","symbol":"SFG","slug":"s-finance"}],"impermanentLoss":"Low","dailyROI":0.76820876712329,"yearlyROI":280.3962},{"id":"5f86b154cc06881662044a5a","name":"PancakeSwap","platform":"Binance Smart Chain","webSite":"https://pancakeswap.finance/","totalValueLocked":8115393879.487392,"auditList":[{"url":"https://github.com/certikfoundation-shared/CertiK-Audits/blob/master/reports/REP-PancakeSwap-16_10_2020.pdf","auditFirm":"CertiK"}],"hasNew":0,"poolId":133,"poolName":"PancakeSWAP LINK-BNB","link":"https://pancakeswap.finance/farms/LINK-BNB%20FLIP","pair":"LINK-WBNB","totalStake":56625572.76652139,"totalStakeRatio":0.00697755,"rewards":[{"cryptoId":7186,"name":"PancakeSwap","symbol":"CAKE","slug":"pancakeswap"}],"impermanentLoss":"High","dailyROI":0.48283616438356,"yearlyROI":176.2352},{"id":"5f86b154cc06881662044a5a","name":"PancakeSwap","platform":"Binance Smart Chain","webSite":"https://pancakeswap.finance/","totalValueLocked":8115393879.487392,"auditList":[{"url":"https://github.com/certikfoundation-shared/CertiK-Audits/blob/master/reports/REP-PancakeSwap-16_10_2020.pdf","auditFirm":"CertiK"}],"hasNew":0,"poolId":172,"poolName":"PancakeSWAP ALPHA-BNB","link":"https://pancakeswap.finance/farms/ALPHA-BNB%20FLP","pair":"ALPHA-BNB","totalStake":30817624.030098937,"totalStakeRatio":0.00379743,"rewards":[{"cryptoId":7186,"name":"PancakeSwap","symbol":"CAKE","slug":"pancakeswap"}],"impermanentLoss":"High","dailyROI":0.44359150684932,"yearlyROI":161.9109},{"id":"5f6b21051a3d2007bc5ea1bb","name":"PerlinX","platform":"Ethereum","webSite":"https://perlinx.finance/","totalValueLocked":1017462.378677196,"hasNew":0,"poolId":123,"poolName":"Balancer BUSD-PERL 50/50","link":"https://app.perlinx.finance/pools/0x19F4611C61e2eE6D2FaDFccBde1e95cFcfd1E210","pair":"BUSD-PERL","totalStake":108925.26551513521,"totalStakeRatio":0.10705582,"rewards":[{"cryptoId":4293,"name":"Perlin","symbol":"PERL","slug":"perlin"},{"cryptoId":5728,"name":"Balancer","symbol":"BAL","slug":"balancer"}],"impermanentLoss":"High","dailyROI":0.44221917808219,"yearlyROI":161.41},{"id":"5f86b154cc06881662044a5a","name":"PancakeSwap","platform":"Binance Smart Chain","webSite":"https://pancakeswap.finance/","totalValueLocked":8115393879.487392,"auditList":[{"url":"https://github.com/certikfoundation-shared/CertiK-Audits/blob/master/reports/REP-PancakeSwap-16_10_2020.pdf","auditFirm":"CertiK"}],"hasNew":0,"poolId":127,"poolName":"PancakeSWAP CAKE-BNB","link":"https://pancakeswap.finance/farms/CAKE-BNB%20FLIP","pair":"CAKE-WBNB","totalStake":1005454531.4687102,"totalStakeRatio":0.12389473,"rewards":[{"cryptoId":7186,"name":"PancakeSwap","symbol":"CAKE","slug":"pancakeswap"}],"impermanentLoss":"High","dailyROI":0.40773945205479,"yearlyROI":148.8249},{"id":"5f6b21051a3d2007bc5ea1bb","name":"PerlinX","platform":"Ethereum","webSite":"https://perlinx.finance/","totalValueLocked":1017462.378677196,"hasNew":0,"poolId":124,"poolName":"Balancer DAI-PERL 50/50\"","link":"https://app.perlinx.finance/pools/0x0B0Dea284a07d60d026691476b130f160e48BD0A","pair":"DAI-PERL","totalStake":87350.24405015854,"totalStakeRatio":0.08585108,"rewards":[{"cryptoId":4293,"name":"Perlin","symbol":"PERL","slug":"perlin"},{"cryptoId":5728,"name":"Balancer","symbol":"BAL","slug":"balancer"}],"impermanentLoss":"High","dailyROI":0.38915835616438,"yearlyROI":142.0428},{"id":"5f86b154cc06881662044a5b","name":"Bella Protocol","platform":"Ethereum","webSite":"https://bella.fi/","totalValueLocked":3400729.358273354,"hasNew":0,"poolId":181,"poolName":"BEL-ETH","link":"https://liquidity.bella.fi/","pair":"BEL-ETH","totalStake":1825248.2075416646,"totalStakeRatio":0.53672257,"rewards":[{"cryptoId":6928,"name":"Bella Protocol","symbol":"BEL","slug":"bella-protocol"}],"impermanentLoss":"High","dailyROI":0.36986301369863,"yearlyROI":135},{"id":"5f6b21051a3d2007bc5ea1bb","name":"PerlinX","platform":"Ethereum","webSite":"https://perlinx.finance/","totalValueLocked":1017462.378677196,"hasNew":0,"poolId":121,"poolName":"Balancer WETH-PERL 50/50","link":"https://app.perlinx.finance/pools/0x8C7769F9F1E5042C0809b8702e4b9947b1Bcb3f3","pair":"WETH-PERL","totalStake":653907.5691423632,"totalStakeRatio":0.64268476,"rewards":[{"cryptoId":4293,"name":"Perlin","symbol":"PERL","slug":"perlin"},{"cryptoId":5728,"name":"Balancer","symbol":"BAL","slug":"balancer"}],"impermanentLoss":"High","dailyROI":0.34463342465753,"yearlyROI":125.7912},{"id":"5f6b21051a3d2007bc5ea1bb","name":"PerlinX","platform":"Ethereum","webSite":"https://perlinx.finance/","totalValueLocked":1017462.378677196,"hasNew":0,"poolId":125,"poolName":"Balancer BAL-PERL 50/50","link":"https://app.perlinx.finance/pools/0x2C1cB70Cccf250B35Ca2CB021E2F624aBa76e3e8","pair":"BAL-PERL","totalStake":13243.899347032466,"totalStakeRatio":0.0130166,"rewards":[{"cryptoId":4293,"name":"Perlin","symbol":"PERL","slug":"perlin"},{"cryptoId":5728,"name":"Balancer","symbol":"BAL","slug":"balancer"}],"impermanentLoss":"High","dailyROI":0.31130739726027,"yearlyROI":113.6272},{"id":"5f86b154cc06881662044a5a","name":"PancakeSwap","platform":"Binance Smart Chain","webSite":"https://pancakeswap.finance/","totalValueLocked":8115393879.487392,"auditList":[{"url":"https://github.com/certikfoundation-shared/CertiK-Audits/blob/master/reports/REP-PancakeSwap-16_10_2020.pdf","auditFirm":"CertiK"}],"hasNew":0,"poolId":131,"poolName":"PancakeSWAP DOT-BNB","link":"https://pancakeswap.finance/farms/DOT-BNB%20FLIP","pair":"DOT-WBNB","totalStake":90809256.30127065,"totalStakeRatio":0.01118975,"rewards":[{"cryptoId":7186,"name":"PancakeSwap","symbol":"CAKE","slug":"pancakeswap"}],"impermanentLoss":"High","dailyROI":0.3009704109589,"yearlyROI":109.8542},{"id":"600004163c1b4b4fdf0bb038","name":"Saffron Finance","platform":"Ethereum","webSite":"https://saffron.finance","totalValueLocked":21830240.291052356,"hasNew":1,"poolId":214,"poolName":"SFI/ESD Uniswap Pool","link":"https://saffron.finance","pair":"SFI-ESD","totalStake":111864.36355236001,"totalStakeRatio":0.00512428,"rewards":[{"cryptoId":7617,"name":"saffron.finance","symbol":"SFI","slug":"saffron-finance"}],"impermanentLoss":"High","dailyROI":0.29946712328767,"yearlyROI":109.3055},{"id":"5f6b21051a3d2007bc5ea1bb","name":"PerlinX","platform":"Ethereum","webSite":"https://perlinx.finance/","totalValueLocked":1017462.378677196,"hasNew":0,"poolId":122,"poolName":"Balancer TUSD-PERL 50/50","link":"https://app.perlinx.finance/pools/0x0BdF7EFEf728308B6F55b1dD8D0c714f0d5d233f","pair":"TUSD-PERL","totalStake":154035.40062250657,"totalStakeRatio":0.15139174,"rewards":[{"cryptoId":4293,"name":"Perlin","symbol":"PERL","slug":"perlin"},{"cryptoId":5728,"name":"Balancer","symbol":"BAL","slug":"balancer"}],"impermanentLoss":"High","dailyROI":0.29445835616438,"yearlyROI":107.4773},{"id":"5f86b154cc06881662044a5a","name":"PancakeSwap","platform":"Binance Smart Chain","webSite":"https://pancakeswap.finance/","totalValueLocked":8115393879.487392,"auditList":[{"url":"https://github.com/certikfoundation-shared/CertiK-Audits/blob/master/reports/REP-PancakeSwap-16_10_2020.pdf","auditFirm":"CertiK"}],"hasNew":0,"poolId":129,"poolName":"PancakeSWAP ADA-BNB","link":"https://pancakeswap.finance/farms/ADA-BNB%20FLIP","pair":"ADA-WBNB","totalStake":46430328.453746125,"totalStakeRatio":0.00572127,"rewards":[{"cryptoId":7186,"name":"PancakeSwap","symbol":"CAKE","slug":"pancakeswap"}],"impermanentLoss":"High","dailyROI":0.29432164383562,"yearlyROI":107.4274},{"id":"600004163c1b4b4fdf0bb038","name":"Saffron Finance","platform":"Ethereum","webSite":"https://saffron.finance","totalValueLocked":21830240.291052356,"hasNew":1,"poolId":213,"poolName":"SFI/GEEQ Uniswap Pool","link":"https://saffron.finance","pair":"SFI-GEEQ","totalStake":64382.7382,"totalStakeRatio":0.00294925,"rewards":[{"cryptoId":7617,"name":"saffron.finance","symbol":"SFI","slug":"saffron-finance"}],"impermanentLoss":"High","dailyROI":0.29374383561644,"yearlyROI":107.2165},{"id":"5f71c840edcba010f8a365b5","name":"HodlTree","platform":"Ethereum","webSite":"https://hodltree.io","totalValueLocked":1975942.171381185,"hasNew":0,"poolId":149,"poolName":"HodlTree balancer","link":"https://pools.balancer.exchange/#/pool/0x02b77ad79e27ad80a0a0868cc7528520e8442c9b/","pair":"HTRE-USDC","totalStake":1947440.1082000001,"totalStakeRatio":0.98557546,"rewards":[{"cryptoId":7100,"name":"HodlTree","symbol":"HTRE","slug":"hodltree"}],"impermanentLoss":"High","dailyROI":0.28518904109589,"yearlyROI":104.094},{"id":"5f71c840edcba010f8a365b5","name":"HodlTree","platform":"Ethereum","webSite":"https://hodltree.io","totalValueLocked":1975942.171381185,"hasNew":0,"poolId":148,"poolName":"HodlTree uniswap","link":"https://uniswap.info/pair/0x57e69e4385896fa4511f958e88d8775fd6a8c6c0","pair":"HTRE-USDC","totalStake":28502.063181185,"totalStakeRatio":0.01442454,"rewards":[{"cryptoId":7100,"name":"HodlTree","symbol":"HTRE","slug":"hodltree"}],"impermanentLoss":"High","dailyROI":0.28518904109589,"yearlyROI":104.094},{"id":"5f86b154cc06881662044a5a","name":"PancakeSwap","platform":"Binance Smart Chain","webSite":"https://pancakeswap.finance/","totalValueLocked":8115393879.487392,"auditList":[{"url":"https://github.com/certikfoundation-shared/CertiK-Audits/blob/master/reports/REP-PancakeSwap-16_10_2020.pdf","auditFirm":"CertiK"}],"hasNew":0,"poolId":174,"poolName":"PancakeSWAP XRP-BNB","link":"https://pancakeswap.finance/farms/XRP-BNB%20FLP","pair":"XRP-BNB","totalStake":48613888.07333609,"totalStakeRatio":0.00599033,"rewards":[{"cryptoId":7186,"name":"PancakeSwap","symbol":"CAKE","slug":"pancakeswap"}],"impermanentLoss":"High","dailyROI":0.28120438356164,"yearlyROI":102.6396},{"id":"5f685b38fcdfe7080cdd0fbb","name":"BakerySwap","platform":"Binance Smart Chain","webSite":"https://www.bakeryswap.org/","totalValueLocked":152765555.35,"hasNew":0,"poolId":105,"poolName":"Waffle","link":"https://www.bakeryswap.org/#/bakery/BAKE-BUSD%20BLP","pair":"BAKE-BUSD","totalStake":3809030.74,"totalStakeRatio":0.02493383,"rewards":[{"cryptoId":7064,"name":"BakeryToken","symbol":"BAKE","slug":"bakerytoken"}],"impermanentLoss":"High","dailyROI":0.26575342465753,"yearlyROI":97},{"id":"5f86b154cc06881662044a5a","name":"PancakeSwap","platform":"Binance Smart Chain","webSite":"https://pancakeswap.finance/","totalValueLocked":8115393879.487392,"auditList":[{"url":"https://github.com/certikfoundation-shared/CertiK-Audits/blob/master/reports/REP-PancakeSwap-16_10_2020.pdf","auditFirm":"CertiK"}],"hasNew":0,"poolId":126,"poolName":"CAKE","link":"https://pancakeswap.finance/staking","pair":"CAKE","totalStake":5277386182.68659,"totalStakeRatio":0.65029329,"rewards":[{"cryptoId":7186,"name":"PancakeSwap","symbol":"CAKE","slug":"pancakeswap"}],"impermanentLoss":"None","dailyROI":0.25593506849315,"yearlyROI":93.4163},{"id":"5fcf5b00c5adb439ad44e3d3","name":"Venus","platform":"Binance Smart Chain","webSite":"https://venus.io/","totalValueLocked":9766742349.3,"auditList":[{"url":"https://certik.foundation/projects/swipe","auditFirm":"Certik"}],"hasNew":1,"poolId":206,"poolName":"VAI Mint","link":"https://app.venus.io/dashboard","pair":"VAI","totalStake":179770916.92,"totalStakeRatio":0.01840644,"rewards":[{"cryptoId":7288,"name":"Venus","symbol":"XVS","slug":"venus"}],"impermanentLoss":"None","dailyROI":0.25241095890411,"yearlyROI":92.13},{"id":"5f685b38fcdfe7080cdd0fbb","name":"BakerySwap","platform":"Binance Smart Chain","webSite":"https://www.bakeryswap.org/","totalValueLocked":152765555.35,"hasNew":0,"poolId":107,"poolName":"Croissant","link":"https://www.bakeryswap.org/#/bakery/BUSD-BNB%20BLP","pair":"BUSD-BNB","totalStake":1826515.64,"totalStakeRatio":0.01195633,"rewards":[{"cryptoId":7064,"name":"BakeryToken","symbol":"BAKE","slug":"bakerytoken"}],"impermanentLoss":"High","dailyROI":0.20783561643836,"yearlyROI":75.86},{"id":"5f5b5b9cb761c05513d83567","name":"mStable","platform":"Ethereum","webSite":"https://app.mstable.org/earn","totalValueLocked":5804746.0755305,"auditList":[{"url":"https://diligence.consensys.net/audits/2020/07/mstable-1.1/","auditFirm":"Consensys Diligence"},{"url":"https://docs.mstable.org/protocol/security","auditFirm":"Bramah Systems"}],"hasNew":0,"poolId":8,"poolName":"Uniswap MTA/WETH 50/50","link":"https://app.mstable.org/earn/uniswap-mta-50-weth-50","pair":"MTA-wETH","totalStake":5804746.0755305,"totalStakeRatio":1,"rewards":[{"cryptoId":5748,"name":"mStable Governance Token: Meta (MTA)","symbol":"MTA","slug":"meta"},{"cryptoId":5728,"name":"Balancer","symbol":"BAL","slug":"balancer"}],"impermanentLoss":"High","dailyROI":0.1956397260274,"yearlyROI":71.4085},{"id":"5f86b154cc06881662044a5a","name":"PancakeSwap","platform":"Binance Smart Chain","webSite":"https://pancakeswap.finance/","totalValueLocked":8115393879.487392,"auditList":[{"url":"https://github.com/certikfoundation-shared/CertiK-Audits/blob/master/reports/REP-PancakeSwap-16_10_2020.pdf","auditFirm":"CertiK"}],"hasNew":0,"poolId":128,"poolName":"PancakeSWAP BUSD-BNB","link":"https://pancakeswap.finance/farms/BUSD-BNB%20FLIP","pair":"BUSD-WBNB","totalStake":562438359.9598755,"totalStakeRatio":0.06930512,"rewards":[{"cryptoId":7186,"name":"PancakeSwap","symbol":"CAKE","slug":"pancakeswap"}],"impermanentLoss":"High","dailyROI":0.19437424657534,"yearlyROI":70.9466},{"id":"5f86b154cc06881662044a5d","name":"S.Finance","platform":"Ethereum","webSite":"https://s.finance","totalValueLocked":235955.9682400575,"hasNew":0,"poolId":164,"poolName":"sUSD liquidity gauge","link":"https://s.finance/dao","pair":"DAI-USDT-USDC-sUSD","totalStake":117073.83291937767,"totalStakeRatio":0.49616814,"rewards":[{"cryptoId":7187,"name":"S.Finance","symbol":"SFG","slug":"s-finance"},{"cryptoId":6538,"name":"Curve DAO Token","symbol":"CRV","slug":"curve-dao-token"},{"cryptoId":2586,"name":"Synthetix","symbol":"SNX","slug":"synthetix-network-token"}],"impermanentLoss":"Low","dailyROI":0.18396849315068,"yearlyROI":67.1485},{"id":"5f86b154cc06881662044a5a","name":"PancakeSwap","platform":"Binance Smart Chain","webSite":"https://pancakeswap.finance/","totalValueLocked":8115393879.487392,"auditList":[{"url":"https://github.com/certikfoundation-shared/CertiK-Audits/blob/master/reports/REP-PancakeSwap-16_10_2020.pdf","auditFirm":"CertiK"}],"hasNew":0,"poolId":173,"poolName":"PancakeSWAP USDT-BNB","link":"https://pancakeswap.finance/farms/USDT-BNB%20FLP","pair":"USDT-BNB","totalStake":149461031.20067152,"totalStakeRatio":0.01841698,"rewards":[{"cryptoId":7186,"name":"PancakeSwap","symbol":"CAKE","slug":"pancakeswap"}],"impermanentLoss":"High","dailyROI":0.1829298630137,"yearlyROI":66.7694},{"id":"600004163c1b4b4fdf0bb038","name":"Saffron Finance","platform":"Ethereum","webSite":"https://saffron.finance","totalValueLocked":21830240.291052356,"hasNew":1,"poolId":215,"poolName":"SFI/ETH SushiSwap Pool","link":"https://saffron.finance","pair":"SFI-ETH","totalStake":2565031.6054000002,"totalStakeRatio":0.11749901,"rewards":[{"cryptoId":7617,"name":"saffron.finance","symbol":"SFI","slug":"saffron-finance"}],"impermanentLoss":"High","dailyROI":0.17238904109589,"yearlyROI":62.922},{"id":"5f5c6731037be201be4a7129","name":"Swerve","platform":"Ethereum","webSite":"https://swerve.fi/","totalValueLocked":25852843.680346794,"hasNew":0,"poolId":67,"poolName":"swUSD","link":"http://ipfs2.swerve.fi/#/swusd","pair":"DAI-USDC-USDT-TUSD","totalStake":25852843.680346794,"totalStakeRatio":1,"rewards":[{"cryptoId":6901,"name":"Swerve","symbol":"SWRV","slug":"swerve"}],"impermanentLoss":"Low","dailyROI":0.17115890410959,"yearlyROI":62.473},{"id":"600004163c1b4b4fdf0bb038","name":"Saffron Finance","platform":"Ethereum","webSite":"https://saffron.finance","totalValueLocked":21830240.291052356,"hasNew":1,"poolId":212,"poolName":"rSFI Staking Pool","link":"https://saffron.finance","pair":"rSFI","totalStake":2947294.6965,"totalStakeRatio":0.13500972,"rewards":[{"cryptoId":7617,"name":"saffron.finance","symbol":"SFI","slug":"saffron-finance"}],"impermanentLoss":"None","dailyROI":0.16889506849315,"yearlyROI":61.6467},{"id":"600004163c1b4b4fdf0bb038","name":"Saffron Finance","platform":"Ethereum","webSite":"https://saffron.finance","totalValueLocked":21830240.291052356,"hasNew":1,"poolId":209,"poolName":"SFI/ETH Uniswap LP Pool","link":"https://saffron.finance","pair":"SFI-ETH","totalStake":3489386.3873999994,"totalStakeRatio":0.15984187,"rewards":[{"cryptoId":7617,"name":"saffron.finance","symbol":"SFI","slug":"saffron-finance"}],"impermanentLoss":"High","dailyROI":0.16686767123288,"yearlyROI":60.9067},{"id":"600004163c1b4b4fdf0bb038","name":"Saffron Finance","platform":"Ethereum","webSite":"https://saffron.finance","totalValueLocked":21830240.291052356,"hasNew":1,"poolId":211,"poolName":"SFI/BTSE Pool","link":"https://saffron.finance","pair":"SFI-BTSE","totalStake":101941.8992,"totalStakeRatio":0.00466976,"rewards":[{"cryptoId":7617,"name":"saffron.finance","symbol":"SFI","slug":"saffron-finance"}],"impermanentLoss":"High","dailyROI":0.16043068493151,"yearlyROI":58.5572},{"id":"5f5b5b9cb761c05513d8356f","name":"Sushi","platform":"Ethereum","webSite":"https://sushiswap.org/","totalValueLocked":1834629015.881132,"auditList":[{"url":"https://github.com/quantstamp/sushiswap-security-review","auditFirm":"Quantstamp"},{"url":"https://github.com/peckshield/publications/blob/master/audit_reports/PeckShield-Audit-Report-SushiSwap-v1.0.pdf","auditFirm":"Peckshield"}],"hasNew":0,"poolId":61,"poolName":"Spartan Dollar","link":"https://sushiswapclassic.org/farms/SUSD-ETH%20SLP","pair":"SUSD-ETH","totalStake":19582315.906880725,"totalStakeRatio":0.01067372,"rewards":[{"cryptoId":6758,"name":"SushiSwap","symbol":"SUSHI","slug":"sushiswap"}],"impermanentLoss":"High","dailyROI":0.15646931506849,"yearlyROI":57.1113},{"id":"5f685b38fcdfe7080cdd0fbb","name":"BakerySwap","platform":"Binance Smart Chain","webSite":"https://www.bakeryswap.org/","totalValueLocked":152765555.35,"hasNew":0,"poolId":108,"poolName":"Toast","link":"https://www.bakeryswap.org/#/bakery/ETH-BNB%20BLP","pair":"ETH-BNB","totalStake":878328.51,"totalStakeRatio":0.00574952,"rewards":[{"cryptoId":7064,"name":"BakeryToken","symbol":"BAKE","slug":"bakerytoken"}],"impermanentLoss":"High","dailyROI":0.14405479452055,"yearlyROI":52.58},{"id":"5f5b5b9cb761c05513d8356f","name":"Sushi","platform":"Ethereum","webSite":"https://sushiswap.org/","totalValueLocked":1834629015.881132,"auditList":[{"url":"https://github.com/quantstamp/sushiswap-security-review","auditFirm":"Quantstamp"},{"url":"https://github.com/peckshield/publications/blob/master/audit_reports/PeckShield-Audit-Report-SushiSwap-v1.0.pdf","auditFirm":"Peckshield"}],"hasNew":0,"poolId":54,"poolName":"YFI Whale","link":"https://sushiswapclassic.org/farms/YFI-ETH%20SLP","pair":"YFI-ETH","totalStake":172670354.74848753,"totalStakeRatio":0.09411731,"rewards":[{"cryptoId":6758,"name":"SushiSwap","symbol":"SUSHI","slug":"sushiswap"}],"impermanentLoss":"High","dailyROI":0.1313,"yearlyROI":47.9245},{"id":"5f787c8daba1f33645724c99","name":"SUN","platform":"Tron","webSite":"https://sun.io/","totalValueLocked":181926764,"hasNew":0,"poolId":161,"poolName":"WIN/TRX LP Pool","link":"https://sun.io/#/sun","pair":"WIN-TRX","totalStake":2788547,"totalStakeRatio":0.01532785,"rewards":[{"cryptoId":6990,"name":"SUN","symbol":"SUN","slug":"sun"}],"impermanentLoss":"High","dailyROI":0.13036739726027,"yearlyROI":47.5841},{"id":"5f5b5b9cb761c05513d8356f","name":"Sushi","platform":"Ethereum","webSite":"https://sushiswap.org/","totalValueLocked":1834629015.881132,"auditList":[{"url":"https://github.com/quantstamp/sushiswap-security-review","auditFirm":"Quantstamp"},{"url":"https://github.com/peckshield/publications/blob/master/audit_reports/PeckShield-Audit-Report-SushiSwap-v1.0.pdf","auditFirm":"Peckshield"}],"hasNew":0,"poolId":57,"poolName":"Donald DAI","link":"https://sushiswapclassic.org/farms/DAI-ETH%20SLP","pair":"DAI-ETH","totalStake":286533359.5525954,"totalStakeRatio":0.15618054,"rewards":[{"cryptoId":6758,"name":"SushiSwap","symbol":"SUSHI","slug":"sushiswap"}],"impermanentLoss":"High","dailyROI":0.11805890410959,"yearlyROI":43.0915},{"id":"5f5b5b9cb761c05513d8356f","name":"Sushi","platform":"Ethereum","webSite":"https://sushiswap.org/","totalValueLocked":1834629015.881132,"auditList":[{"url":"https://github.com/quantstamp/sushiswap-security-review","auditFirm":"Quantstamp"},{"url":"https://github.com/peckshield/publications/blob/master/audit_reports/PeckShield-Audit-Report-SushiSwap-v1.0.pdf","auditFirm":"Peckshield"}],"hasNew":0,"poolId":52,"poolName":"Sushi Party!","link":"https://sushiswapclassic.org/farms/SUSHI-ETH%20SLP","pair":"SUSHI-ETH","totalStake":463172582.9797993,"totalStakeRatio":0.25246117,"rewards":[{"cryptoId":6758,"name":"SushiSwap","symbol":"SUSHI","slug":"sushiswap"}],"impermanentLoss":"High","dailyROI":0.11631315068493,"yearlyROI":42.4543},{"id":"5f787c8daba1f33645724c99","name":"SUN","platform":"Tron","webSite":"https://sun.io/","totalValueLocked":181926764,"hasNew":0,"poolId":153,"poolName":"SUN/TRX LP Pool","link":"https://sun.io/#/sun","pair":"SUN-TRX","totalStake":28208478,"totalStakeRatio":0.15505403,"rewards":[{"cryptoId":6990,"name":"SUN","symbol":"SUN","slug":"sun"}],"impermanentLoss":"High","dailyROI":0.11598712328767,"yearlyROI":42.3353},{"id":"5f5b5b9cb761c05513d8356f","name":"Sushi","platform":"Ethereum","webSite":"https://sushiswap.org/","totalValueLocked":1834629015.881132,"auditList":[{"url":"https://github.com/quantstamp/sushiswap-security-review","auditFirm":"Quantstamp"},{"url":"https://github.com/peckshield/publications/blob/master/audit_reports/PeckShield-Audit-Report-SushiSwap-v1.0.pdf","auditFirm":"Peckshield"}],"hasNew":0,"poolId":55,"poolName":"Tether Turtle","link":"https://sushiswapclassic.org/farms/USDT-ETH%20SLP","pair":"USDT-ETH","totalStake":245835421.13518074,"totalStakeRatio":0.13399735,"rewards":[{"cryptoId":6758,"name":"SushiSwap","symbol":"SUSHI","slug":"sushiswap"}],"impermanentLoss":"High","dailyROI":0.11527835616438,"yearlyROI":42.0766},{"id":"5f685b38fcdfe7080cdd0fbb","name":"BakerySwap","platform":"Binance Smart Chain","webSite":"https://www.bakeryswap.org/","totalValueLocked":152765555.35,"hasNew":0,"poolId":104,"poolName":"Doughnut","link":"https://www.bakeryswap.org/#/bakery/BAKE-BNB%20BLP","pair":"BAKE-BNB","totalStake":33278627.98,"totalStakeRatio":0.21784117,"rewards":[{"cryptoId":7064,"name":"BakeryToken","symbol":"BAKE","slug":"bakerytoken"}],"impermanentLoss":"High","dailyROI":0.11408219178082,"yearlyROI":41.64},{"id":"5f5b5b9cb761c05513d8356f","name":"Sushi","platform":"Ethereum","webSite":"https://sushiswap.org/","totalValueLocked":1834629015.881132,"auditList":[{"url":"https://github.com/quantstamp/sushiswap-security-review","auditFirm":"Quantstamp"},{"url":"https://github.com/peckshield/publications/blob/master/audit_reports/PeckShield-Audit-Report-SushiSwap-v1.0.pdf","auditFirm":"Peckshield"}],"hasNew":0,"poolId":50,"poolName":"Band-osaurus","link":"https://sushiswapclassic.org/farms/BAND-ETH%20SLP","pair":"BAND-ETH","totalStake":15682191.840735458,"totalStakeRatio":0.00854788,"rewards":[{"cryptoId":6758,"name":"SushiSwap","symbol":"SUSHI","slug":"sushiswap"}],"impermanentLoss":"High","dailyROI":0.10162767123288,"yearlyROI":37.0941},{"id":"5f787c8daba1f33645724c99","name":"SUN","platform":"Tron","webSite":"https://sun.io/","totalValueLocked":181926764,"hasNew":0,"poolId":163,"poolName":"USDJ/TRX LP Pool","link":"https://sun.io/#/sun","pair":"USDJ-TRX","totalStake":10905012,"totalStakeRatio":0.05994177,"rewards":[{"cryptoId":6990,"name":"SUN","symbol":"SUN","slug":"sun"}],"impermanentLoss":"High","dailyROI":0.1000095890411,"yearlyROI":36.5035},{"id":"5f5b5b9cb761c05513d8356f","name":"Sushi","platform":"Ethereum","webSite":"https://sushiswap.org/","totalValueLocked":1834629015.881132,"auditList":[{"url":"https://github.com/quantstamp/sushiswap-security-review","auditFirm":"Quantstamp"},{"url":"https://github.com/peckshield/publications/blob/master/audit_reports/PeckShield-Audit-Report-SushiSwap-v1.0.pdf","auditFirm":"Peckshield"}],"hasNew":0,"poolId":51,"poolName":"Synthetic Snake","link":"https://sushiswapclassic.org/farms/SNX-ETH%20SLP","pair":"SNX-ETH","totalStake":59848137.625209205,"totalStakeRatio":0.03262138,"rewards":[{"cryptoId":6758,"name":"SushiSwap","symbol":"SUSHI","slug":"sushiswap"}],"impermanentLoss":"High","dailyROI":0.09901808219178,"yearlyROI":36.1416},{"id":"5f86b154cc06881662044a5a","name":"PancakeSwap","platform":"Binance Smart Chain","webSite":"https://pancakeswap.finance/","totalValueLocked":8115393879.487392,"auditList":[{"url":"https://github.com/certikfoundation-shared/CertiK-Audits/blob/master/reports/REP-PancakeSwap-16_10_2020.pdf","auditFirm":"CertiK"}],"hasNew":0,"poolId":171,"poolName":"PancakeSWAP BTC-BNB","link":"https://pancakeswap.finance/farms/BTCB-BNB%20FLP","pair":"BTC-BNB","totalStake":293888612.3485444,"totalStakeRatio":0.03621372,"rewards":[{"cryptoId":7186,"name":"PancakeSwap","symbol":"CAKE","slug":"pancakeswap"}],"impermanentLoss":"High","dailyROI":0.09303150684932,"yearlyROI":33.9565},{"id":"5f86b154cc06881662044a5a","name":"PancakeSwap","platform":"Binance Smart Chain","webSite":"https://pancakeswap.finance/","totalValueLocked":8115393879.487392,"auditList":[{"url":"https://github.com/certikfoundation-shared/CertiK-Audits/blob/master/reports/REP-PancakeSwap-16_10_2020.pdf","auditFirm":"CertiK"}],"hasNew":0,"poolId":170,"poolName":"PancakeSWAP ETH-BNB","link":"https://pancakeswap.finance/farms/ETH-BNB%20FLP","pair":"ETH-BNB","totalStake":298987749.45881903,"totalStakeRatio":0.03684205,"rewards":[{"cryptoId":7186,"name":"PancakeSwap","symbol":"CAKE","slug":"pancakeswap"}],"impermanentLoss":"High","dailyROI":0.09144493150685,"yearlyROI":33.3774},{"id":"5f787c8daba1f33645724c99","name":"SUN","platform":"Tron","webSite":"https://sun.io/","totalValueLocked":181926764,"hasNew":0,"poolId":151,"poolName":"HT/TRX LP Pool","link":"https://sun.io/#/sun","pair":"HT-TRX","totalStake":9594999,"totalStakeRatio":0.052741,"rewards":[{"cryptoId":6990,"name":"SUN","symbol":"SUN","slug":"sun"}],"impermanentLoss":"High","dailyROI":0.09002465753425,"yearlyROI":32.859},{"id":"5f685b38fcdfe7080cdd0fbb","name":"BakerySwap","platform":"Binance Smart Chain","webSite":"https://www.bakeryswap.org/","totalValueLocked":152765555.35,"hasNew":0,"poolId":109,"poolName":"Cake","link":"https://www.bakeryswap.org/#/bakery/BTC-BNB%20BLP","pair":"BTC-BNB","totalStake":49416586.55,"totalStakeRatio":0.3234799,"rewards":[{"cryptoId":7064,"name":"BakeryToken","symbol":"BAKE","slug":"bakerytoken"}],"impermanentLoss":"High","dailyROI":0.08961643835616,"yearlyROI":32.71},{"id":"5f5b5b9cb761c05513d8356f","name":"Sushi","platform":"Ethereum","webSite":"https://sushiswap.org/","totalValueLocked":1834629015.881132,"auditList":[{"url":"https://github.com/quantstamp/sushiswap-security-review","auditFirm":"Quantstamp"},{"url":"https://github.com/peckshield/publications/blob/master/audit_reports/PeckShield-Audit-Report-SushiSwap-v1.0.pdf","auditFirm":"Peckshield"}],"hasNew":0,"poolId":58,"poolName":"Circle Snail","link":"https://sushiswapclassic.org/farms/USDC-ETH%20SLP","pair":"USDC-ETH","totalStake":370658425.058987,"totalStakeRatio":0.20203454,"rewards":[{"cryptoId":6758,"name":"SushiSwap","symbol":"SUSHI","slug":"sushiswap"}],"impermanentLoss":"High","dailyROI":0.08693424657534,"yearlyROI":31.731},{"id":"5f5b5b9cb761c05513d8356a","name":"Yearn","platform":"Ethereum","webSite":"https://yearn.finance/vaults","totalValueLocked":95063339.64427319,"auditList":[{"url":"https://github.com/iearn-finance/audits/blob/master/Certik%20-%20itoken-finance-audit-report-1.1.0.pdf","auditFirm":"Certik"},{"url":"https://github.com/iearn-finance/audits/blob/master/CryptoManiacs%20%20-%20Audit%20of%20iearn.finance%20by%20CryptoManiacs%20-%20HackMD.pdf","auditFirm":"CryptoManiacs"},{"url":"https://github.com/iearn-finance/audits/blob/master/Quantstamp%20-%20Yearn.Finance%20Security%20Review.pdf","auditFirm":"Quantstamp"},{"url":"https://github.com/iearn-finance/audits/blob/master/StrategyCurveYCRV.sol%20-%20HackMD.pdf","auditFirm":"HackMD"}],"hasNew":0,"poolId":23,"poolName":"TUSD Vault","link":"https://yearn.finance/vaults","pair":"TUSD","totalStake":3291172.260025648,"totalStakeRatio":0.03462084,"rewards":[{"cryptoId":2563,"name":"TrueUSD","symbol":"TUSD","slug":"trueusd"}],"impermanentLoss":"NONE","dailyROI":0.08531369863014,"yearlyROI":31.1395},{"id":"5f5b5b9cb761c05513d8356f","name":"Sushi","platform":"Ethereum","webSite":"https://sushiswap.org/","totalValueLocked":1834629015.881132,"auditList":[{"url":"https://github.com/quantstamp/sushiswap-security-review","auditFirm":"Quantstamp"},{"url":"https://github.com/peckshield/publications/blob/master/audit_reports/PeckShield-Audit-Report-SushiSwap-v1.0.pdf","auditFirm":"Peckshield"}],"hasNew":0,"poolId":59,"poolName":"Toadie Marine","link":"https://sushiswapclassic.org/farms/LINK-ETH%20SLP","pair":"LINK-ETH","totalStake":121388264.0122265,"totalStakeRatio":0.06616502,"rewards":[{"cryptoId":6758,"name":"SushiSwap","symbol":"SUSHI","slug":"sushiswap"}],"impermanentLoss":"High","dailyROI":0.08524821917808,"yearlyROI":31.1156},{"id":"5f5b5b9cb761c05513d8356a","name":"Yearn","platform":"Ethereum","webSite":"https://yearn.finance/vaults","totalValueLocked":95063339.64427319,"auditList":[{"url":"https://github.com/iearn-finance/audits/blob/master/Certik%20-%20itoken-finance-audit-report-1.1.0.pdf","auditFirm":"Certik"},{"url":"https://github.com/iearn-finance/audits/blob/master/CryptoManiacs%20%20-%20Audit%20of%20iearn.finance%20by%20CryptoManiacs%20-%20HackMD.pdf","auditFirm":"CryptoManiacs"},{"url":"https://github.com/iearn-finance/audits/blob/master/Quantstamp%20-%20Yearn.Finance%20Security%20Review.pdf","auditFirm":"Quantstamp"},{"url":"https://github.com/iearn-finance/audits/blob/master/StrategyCurveYCRV.sol%20-%20HackMD.pdf","auditFirm":"HackMD"}],"hasNew":0,"poolId":24,"poolName":"USDC Vault","link":"https://yearn.finance/vaults","pair":"USDC","totalStake":11117162.444132,"totalStakeRatio":0.11694479,"rewards":[{"cryptoId":3408,"name":"USD Coin","symbol":"USDC","slug":"usd-coin"}],"impermanentLoss":"NONE","dailyROI":0.08383506849315,"yearlyROI":30.5998},{"id":"5f5b5b9cb761c05513d8356a","name":"Yearn","platform":"Ethereum","webSite":"https://yearn.finance/vaults","totalValueLocked":95063339.64427319,"auditList":[{"url":"https://github.com/iearn-finance/audits/blob/master/Certik%20-%20itoken-finance-audit-report-1.1.0.pdf","auditFirm":"Certik"},{"url":"https://github.com/iearn-finance/audits/blob/master/CryptoManiacs%20%20-%20Audit%20of%20iearn.finance%20by%20CryptoManiacs%20-%20HackMD.pdf","auditFirm":"CryptoManiacs"},{"url":"https://github.com/iearn-finance/audits/blob/master/Quantstamp%20-%20Yearn.Finance%20Security%20Review.pdf","auditFirm":"Quantstamp"},{"url":"https://github.com/iearn-finance/audits/blob/master/StrategyCurveYCRV.sol%20-%20HackMD.pdf","auditFirm":"HackMD"}],"hasNew":0,"poolId":22,"poolName":"DAI Vault","link":"https://yearn.finance/vaults","pair":"DAI","totalStake":13178954.544678444,"totalStakeRatio":0.13863341,"rewards":[{"cryptoId":4943,"name":"Dai","symbol":"DAI","slug":"multi-collateral-dai"}],"impermanentLoss":"NONE","dailyROI":0.08123945205479,"yearlyROI":29.6524},{"id":"5f71c830edcba010f8a365b4","name":"Harvest","platform":"Ethereum","webSite":"https://harvest.finance/","totalValueLocked":270760747.9444821,"hasNew":0,"poolId":147,"poolName":"FARM Profit Sharing","link":"https://harvest.finance/","pair":"FARM","totalStake":80995582.79860535,"totalStakeRatio":0.29914079,"rewards":[{"cryptoId":6859,"name":"Harvest Finance","symbol":"FARM","slug":"harvest-finance"}],"impermanentLoss":"None","dailyROI":0.08038356164384,"yearlyROI":29.34},{"id":"5f5b5b9cb761c05513d8356a","name":"Yearn","platform":"Ethereum","webSite":"https://yearn.finance/vaults","totalValueLocked":95063339.64427319,"auditList":[{"url":"https://github.com/iearn-finance/audits/blob/master/Certik%20-%20itoken-finance-audit-report-1.1.0.pdf","auditFirm":"Certik"},{"url":"https://github.com/iearn-finance/audits/blob/master/CryptoManiacs%20%20-%20Audit%20of%20iearn.finance%20by%20CryptoManiacs%20-%20HackMD.pdf","auditFirm":"CryptoManiacs"},{"url":"https://github.com/iearn-finance/audits/blob/master/Quantstamp%20-%20Yearn.Finance%20Security%20Review.pdf","auditFirm":"Quantstamp"},{"url":"https://github.com/iearn-finance/audits/blob/master/StrategyCurveYCRV.sol%20-%20HackMD.pdf","auditFirm":"HackMD"}],"hasNew":0,"poolId":25,"poolName":"USDT Vault","link":"https://yearn.finance/vaults","pair":"USDT","totalStake":9617217.255204,"totalStakeRatio":0.10116641,"rewards":[{"cryptoId":825,"name":"Tether","symbol":"USDT","slug":"tether"}],"impermanentLoss":"NONE","dailyROI":0.07985452054795,"yearlyROI":29.1469},{"id":"5f86b154cc06881662044a5a","name":"PancakeSwap","platform":"Binance Smart Chain","webSite":"https://pancakeswap.finance/","totalValueLocked":8115393879.487392,"auditList":[{"url":"https://github.com/certikfoundation-shared/CertiK-Audits/blob/master/reports/REP-PancakeSwap-16_10_2020.pdf","auditFirm":"CertiK"}],"hasNew":0,"poolId":168,"poolName":"PancakeSWAP USDT-BUSD","link":"https://pancakeswap.finance/farms/USDT-BUSD%20FLIP","pair":"USDT-BUSD","totalStake":182728528.0371041,"totalStakeRatio":0.02251629,"rewards":[{"cryptoId":7186,"name":"PancakeSwap","symbol":"CAKE","slug":"pancakeswap"}],"impermanentLoss":"Low","dailyROI":0.07481287671233,"yearlyROI":27.3067},{"id":"5f5b5b9cb761c05513d8356f","name":"Sushi","platform":"Ethereum","webSite":"https://sushiswap.org/","totalValueLocked":1834629015.881132,"auditList":[{"url":"https://github.com/quantstamp/sushiswap-security-review","auditFirm":"Quantstamp"},{"url":"https://github.com/peckshield/publications/blob/master/audit_reports/PeckShield-Audit-Report-SushiSwap-v1.0.pdf","auditFirm":"Peckshield"}],"hasNew":0,"poolId":49,"poolName":"Umami Squid","link":"https://sushiswapclassic.org/farms/UMA-ETH%20SLP","pair":"UMA-ETH","totalStake":15042961.221545286,"totalStakeRatio":0.00819946,"rewards":[{"cryptoId":6758,"name":"SushiSwap","symbol":"SUSHI","slug":"sushiswap"}],"impermanentLoss":"High","dailyROI":0.0746101369863,"yearlyROI":27.2327},{"id":"5f787c8daba1f33645724c99","name":"SUN","platform":"Tron","webSite":"https://sun.io/","totalValueLocked":181926764,"hasNew":0,"poolId":154,"poolName":"JST/TRX LP Pool","link":"https://sun.io/#/sun","pair":"JST-TRX","totalStake":19554433,"totalStakeRatio":0.10748519,"rewards":[{"cryptoId":6990,"name":"SUN","symbol":"SUN","slug":"sun"}],"impermanentLoss":"High","dailyROI":0.07436383561644,"yearlyROI":27.1428},{"id":"5f787c8daba1f33645724c99","name":"SUN","platform":"Tron","webSite":"https://sun.io/","totalValueLocked":181926764,"hasNew":0,"poolId":156,"poolName":"SUN Pool","link":"https://sun.io/#/sun","pair":"SUN-TRX","totalStake":14941255,"totalStakeRatio":0.08212786,"rewards":[{"cryptoId":6990,"name":"SUN","symbol":"SUN","slug":"sun"}],"impermanentLoss":"High","dailyROI":0.07299287671233,"yearlyROI":26.6424},{"id":"5f5b5b9cb761c05513d8356f","name":"Sushi","platform":"Ethereum","webSite":"https://sushiswap.org/","totalValueLocked":1834629015.881132,"auditList":[{"url":"https://github.com/quantstamp/sushiswap-security-review","auditFirm":"Quantstamp"},{"url":"https://github.com/peckshield/publications/blob/master/audit_reports/PeckShield-Audit-Report-SushiSwap-v1.0.pdf","auditFirm":"Peckshield"}],"hasNew":0,"poolId":65,"poolName":"CRV Crocodile","link":"https://sushiswapclassic.org/farms/CRV-ETH%20SLP","pair":"CRV-ETH","totalStake":15828499.447976978,"totalStakeRatio":0.00862763,"rewards":[{"cryptoId":6758,"name":"SushiSwap","symbol":"SUSHI","slug":"sushiswap"}],"impermanentLoss":"High","dailyROI":0.07090739726027,"yearlyROI":25.8812},{"id":"5f5b5b9cb761c05513d83566","name":"dForce","platform":"Ethereum","webSite":"https://staking.dforce.network/dapp","totalValueLocked":85987737.45764147,"auditList":[{"url":"https://github.com/peckshield/publications#dforce-network","auditFirm":"Peckshield"}],"hasNew":0,"poolId":7,"poolName":"Uniswap GOLDx-USDx","link":"https://goldx.dforce.network/","pair":"GOLDx-USDx","totalStake":81038.7642697576,"totalStakeRatio":0.00094245,"rewards":[{"cryptoId":4758,"name":"dForce","symbol":"DF","slug":"dforce"}],"impermanentLoss":"None","dailyROI":0.07057068493151,"yearlyROI":25.7583},{"id":"5f787c8daba1f33645724c99","name":"SUN","platform":"Tron","webSite":"https://sun.io/","totalValueLocked":181926764,"hasNew":0,"poolId":155,"poolName":"USDT/TRX LP Pool","link":"https://sun.io/#/sun","pair":"USDT-TRX","totalStake":53329235,"totalStakeRatio":0.29313573,"rewards":[{"cryptoId":6990,"name":"SUN","symbol":"SUN","slug":"sun"}],"impermanentLoss":"High","dailyROI":0.06135123287671,"yearlyROI":22.3932},{"id":"5f5b5b9cb761c05513d8356f","name":"Sushi","platform":"Ethereum","webSite":"https://sushiswap.org/","totalValueLocked":1834629015.881132,"auditList":[{"url":"https://github.com/quantstamp/sushiswap-security-review","auditFirm":"Quantstamp"},{"url":"https://github.com/peckshield/publications/blob/master/audit_reports/PeckShield-Audit-Report-SushiSwap-v1.0.pdf","auditFirm":"Peckshield"}],"hasNew":0,"poolId":60,"poolName":"Compound Truffle","link":"https://sushiswapclassic.org/farms/COMP-ETH%20SLP","pair":"COMP-ETH","totalStake":28482879.66249029,"totalStakeRatio":0.01552514,"rewards":[{"cryptoId":6758,"name":"SushiSwap","symbol":"SUSHI","slug":"sushiswap"}],"impermanentLoss":"High","dailyROI":0.05871287671233,"yearlyROI":21.4302},{"id":"5f5b5b9cb761c05513d8356f","name":"Sushi","platform":"Ethereum","webSite":"https://sushiswap.org/","totalValueLocked":1834629015.881132,"auditList":[{"url":"https://github.com/quantstamp/sushiswap-security-review","auditFirm":"Quantstamp"},{"url":"https://github.com/peckshield/publications/blob/master/audit_reports/PeckShield-Audit-Report-SushiSwap-v1.0.pdf","auditFirm":"Peckshield"}],"hasNew":0,"poolId":64,"poolName":"REN Rhino","link":"https://sushiswapclassic.org/farms/REN-ETH%20SLP","pair":"ren-ETH","totalStake":19903622.689017594,"totalStakeRatio":0.01084885,"rewards":[{"cryptoId":6758,"name":"SushiSwap","symbol":"SUSHI","slug":"sushiswap"}],"impermanentLoss":"High","dailyROI":0.0563895890411,"yearlyROI":20.5822},{"id":"5f5b5b9cb761c05513d83566","name":"dForce","platform":"Ethereum","webSite":"https://staking.dforce.network/dapp","totalValueLocked":85987737.45764147,"auditList":[{"url":"https://github.com/peckshield/publications#dforce-network","auditFirm":"Peckshield"}],"hasNew":0,"poolId":5,"poolName":"Uniswap DF-USDx","link":"https://usr.dforce.network/","pair":"DF-USDx","totalStake":532663.9133717071,"totalStakeRatio":0.00619465,"rewards":[{"cryptoId":4758,"name":"dForce","symbol":"DF","slug":"dforce"}],"impermanentLoss":"None","dailyROI":0.04866876712329,"yearlyROI":17.7641},{"id":"600004163c1b4b4fdf0bb038","name":"Saffron Finance","platform":"Ethereum","webSite":"https://saffron.finance","totalValueLocked":21830240.291052356,"hasNew":1,"poolId":210,"poolName":"SFI Staking Pool","link":"https://saffron.finance","pair":"SFI","totalStake":12550338.600799998,"totalStakeRatio":0.57490611,"rewards":[{"cryptoId":7617,"name":"saffron.finance","symbol":"SFI","slug":"saffron-finance"}],"impermanentLoss":"None","dailyROI":0.0484501369863,"yearlyROI":17.6843},{"id":"5f787c8daba1f33645724c99","name":"SUN","platform":"Tron","webSite":"https://sun.io/","totalValueLocked":181926764,"hasNew":0,"poolId":150,"poolName":"HT Pool","link":"https://sun.io/#/sun","pair":"HT","totalStake":42604805,"totalStakeRatio":0.23418657,"rewards":[{"cryptoId":6990,"name":"SUN","symbol":"SUN","slug":"sun"}],"impermanentLoss":"None","dailyROI":0.04730684931507,"yearlyROI":17.267},{"id":"5f71c830edcba010f8a365b4","name":"Harvest","platform":"Ethereum","webSite":"https://harvest.finance/","totalValueLocked":270760747.9444821,"hasNew":0,"poolId":137,"poolName":"DAI Vault","link":"https://harvest.finance/","pair":"DAI","totalStake":13152912.37259854,"totalStakeRatio":0.04857762,"rewards":[{"cryptoId":6859,"name":"Harvest Finance","symbol":"FARM","slug":"harvest-finance"},{"cryptoId":6538,"name":"Curve DAO Token","symbol":"CRV","slug":"curve-dao-token"}],"impermanentLoss":"High","dailyROI":0.04397260273973,"yearlyROI":16.05},{"id":"5f685b38fcdfe7080cdd0fbb","name":"BakerySwap","platform":"Binance Smart Chain","webSite":"https://www.bakeryswap.org/","totalValueLocked":152765555.35,"hasNew":0,"poolId":103,"poolName":"Bread","link":"https://www.bakeryswap.org/#/bakery/BAKE","pair":"BAKE","totalStake":63556465.93,"totalStakeRatio":0.41603924,"rewards":[{"cryptoId":7064,"name":"BakeryToken","symbol":"BAKE","slug":"bakerytoken"}],"impermanentLoss":"High","dailyROI":0.04180821917808,"yearlyROI":15.26},{"id":"5f5b5b9cb761c05513d8356d","name":"Curve","platform":"Ethereum","webSite":"https://www.curve.fi/","totalValueLocked":1854776987.4432564,"auditList":[{"url":"https://www.curve.fi/curve_audits/00-ToB.pdf","auditFirm":"Trail of Bits"},{"url":"https://www.curve.fi/curve_audits/curve-dao-quantstamp.pdf","auditFirm":"Quantstamp"}],"hasNew":0,"poolId":38,"poolName":"sUSD","link":"https://www.curve.fi/susdv2","pair":"DAI-USDC-USDT-sUSD","totalStake":199434597.04514995,"totalStakeRatio":0.10752484,"rewards":[{"cryptoId":6538,"name":"Curve DAO Token","symbol":"CRV","slug":"curve-dao-token"}],"impermanentLoss":"Low","dailyROI":0.04020493150685,"yearlyROI":14.6748},{"id":"5f71c830edcba010f8a365b4","name":"Harvest","platform":"Ethereum","webSite":"https://harvest.finance/","totalValueLocked":270760747.9444821,"hasNew":0,"poolId":138,"poolName":"USDC Vault","link":"https://harvest.finance/","pair":"USDC","totalStake":49368387.681626,"totalStakeRatio":0.18233214,"rewards":[{"cryptoId":6859,"name":"Harvest Finance","symbol":"FARM","slug":"harvest-finance"},{"cryptoId":6538,"name":"Curve DAO Token","symbol":"CRV","slug":"curve-dao-token"}],"impermanentLoss":"Low","dailyROI":0.0401095890411,"yearlyROI":14.64},{"id":"5f71c830edcba010f8a365b4","name":"Harvest","platform":"Ethereum","webSite":"https://harvest.finance/","totalValueLocked":270760747.9444821,"hasNew":0,"poolId":139,"poolName":"USDT Vault","link":"https://harvest.finance/","pair":"USDT","totalStake":6412426.405836,"totalStakeRatio":0.023683,"rewards":[{"cryptoId":6859,"name":"Harvest Finance","symbol":"FARM","slug":"harvest-finance"},{"cryptoId":6538,"name":"Curve DAO Token","symbol":"CRV","slug":"curve-dao-token"}],"impermanentLoss":"Low","dailyROI":0.03890410958904,"yearlyROI":14.2},{"id":"5f5b5b9cb761c05513d8356a","name":"Yearn","platform":"Ethereum","webSite":"https://yearn.finance/vaults","totalValueLocked":95063339.64427319,"auditList":[{"url":"https://github.com/iearn-finance/audits/blob/master/Certik%20-%20itoken-finance-audit-report-1.1.0.pdf","auditFirm":"Certik"},{"url":"https://github.com/iearn-finance/audits/blob/master/CryptoManiacs%20%20-%20Audit%20of%20iearn.finance%20by%20CryptoManiacs%20-%20HackMD.pdf","auditFirm":"CryptoManiacs"},{"url":"https://github.com/iearn-finance/audits/blob/master/Quantstamp%20-%20Yearn.Finance%20Security%20Review.pdf","auditFirm":"Quantstamp"},{"url":"https://github.com/iearn-finance/audits/blob/master/StrategyCurveYCRV.sol%20-%20HackMD.pdf","auditFirm":"HackMD"}],"hasNew":0,"poolId":26,"poolName":"yCRV Vault","link":"https://yearn.finance/vaults","pair":"yCRV","totalStake":43339857.72372348,"totalStakeRatio":0.45590506,"rewards":[{"cryptoId":6538,"name":"Curve DAO Token","symbol":"CRV","slug":"curve-dao-token"}],"impermanentLoss":"NONE","dailyROI":0.03170356164384,"yearlyROI":11.5718},{"id":"5f5b5b9cb761c05513d8356d","name":"Curve","platform":"Ethereum","webSite":"https://www.curve.fi/","totalValueLocked":1854776987.4432564,"auditList":[{"url":"https://www.curve.fi/curve_audits/00-ToB.pdf","auditFirm":"Trail of Bits"},{"url":"https://www.curve.fi/curve_audits/curve-dao-quantstamp.pdf","auditFirm":"Quantstamp"}],"hasNew":0,"poolId":34,"poolName":"Compound","link":"https://www.curve.fi/compound","pair":"DAI-USDC","totalStake":142911560.83606184,"totalStakeRatio":0.07705054,"rewards":[{"cryptoId":6538,"name":"Curve DAO Token","symbol":"CRV","slug":"curve-dao-token"}],"impermanentLoss":"Low","dailyROI":0.03104602739726,"yearlyROI":11.3318},{"id":"5fcf5b00c5adb439ad44e3d3","name":"Venus","platform":"Binance Smart Chain","webSite":"https://venus.io/","totalValueLocked":9766742349.3,"auditList":[{"url":"https://certik.foundation/projects/swipe","auditFirm":"Certik"}],"hasNew":1,"poolId":193,"poolName":"vXVS-XVS Lending","link":"https://app.venus.io/dashboard","pair":"vXVS-XVS","totalStake":399209896.65,"totalStakeRatio":0.04087442,"rewards":[{"cryptoId":7288,"name":"Venus","symbol":"XVS","slug":"venus"}],"impermanentLoss":"None","dailyROI":0.02638356164384,"yearlyROI":9.63},{"id":"5f5b5b9cb761c05513d8356d","name":"Curve","platform":"Ethereum","webSite":"https://www.curve.fi/","totalValueLocked":1854776987.4432564,"auditList":[{"url":"https://www.curve.fi/curve_audits/00-ToB.pdf","auditFirm":"Trail of Bits"},{"url":"https://www.curve.fi/curve_audits/curve-dao-quantstamp.pdf","auditFirm":"Quantstamp"}],"hasNew":0,"poolId":37,"poolName":"bUSD","link":"https://www.curve.fi/busd","pair":"DAI-USDC-USDT-BUSD","totalStake":89658512.22955135,"totalStakeRatio":0.04833924,"rewards":[{"cryptoId":6538,"name":"Curve DAO Token","symbol":"CRV","slug":"curve-dao-token"}],"impermanentLoss":"Low","dailyROI":0.01985287671233,"yearlyROI":7.2463},{"id":"5f5b5b9cb761c05513d8356d","name":"Curve","platform":"Ethereum","webSite":"https://www.curve.fi/","totalValueLocked":1854776987.4432564,"auditList":[{"url":"https://www.curve.fi/curve_audits/00-ToB.pdf","auditFirm":"Trail of Bits"},{"url":"https://www.curve.fi/curve_audits/curve-dao-quantstamp.pdf","auditFirm":"Quantstamp"}],"hasNew":0,"poolId":41,"poolName":"hBTC","link":"https://www.curve.fi/hbtc","pair":"hBTC-wBTC","totalStake":480045188.0476562,"totalStakeRatio":0.25881558,"rewards":[{"cryptoId":6538,"name":"Curve DAO Token","symbol":"CRV","slug":"curve-dao-token"}],"impermanentLoss":"Low","dailyROI":0.01870383561644,"yearlyROI":6.8269},{"id":"5fcf5b00c5adb439ad44e3d3","name":"Venus","platform":"Binance Smart Chain","webSite":"https://venus.io/","totalValueLocked":9766742349.3,"auditList":[{"url":"https://certik.foundation/projects/swipe","auditFirm":"Certik"}],"hasNew":1,"poolId":202,"poolName":"vSXP-SXP Lending","link":"https://app.venus.io/dashboard","pair":"vSXP-SXP","totalStake":268024106.26,"totalStakeRatio":0.02744253,"rewards":[{"cryptoId":7288,"name":"Venus","symbol":"XVS","slug":"venus"}],"impermanentLoss":"None","dailyROI":0.01819178082192,"yearlyROI":6.64},{"id":"5f71c830edcba010f8a365b4","name":"Harvest","platform":"Ethereum","webSite":"https://harvest.finance/","totalValueLocked":270760747.9444821,"hasNew":0,"poolId":136,"poolName":"WETH Vault","link":"https://harvest.finance/","pair":"WETH","totalStake":14317185.480822224,"totalStakeRatio":0.05287763,"rewards":[{"cryptoId":6859,"name":"Harvest Finance","symbol":"FARM","slug":"harvest-finance"},{"cryptoId":6193,"name":"Cream Finance","symbol":"CREAM","slug":"cream-finance"}],"impermanentLoss":"None","dailyROI":0.018,"yearlyROI":6.57},{"id":"5fcf5b00c5adb439ad44e3d3","name":"Venus","platform":"Binance Smart Chain","webSite":"https://venus.io/","totalValueLocked":9766742349.3,"auditList":[{"url":"https://certik.foundation/projects/swipe","auditFirm":"Certik"}],"hasNew":1,"poolId":200,"poolName":"vUSDT-USDT Lending","link":"https://app.venus.io/dashboard","pair":"vUSDT-USDT","totalStake":1063997012.91,"totalStakeRatio":0.10894083,"rewards":[{"cryptoId":7288,"name":"Venus","symbol":"XVS","slug":"venus"}],"impermanentLoss":"None","dailyROI":0.01556164383562,"yearlyROI":5.68},{"id":"5f685b27fcdfe7080cdd0fba","name":"Fortube","platform":"Ethereum","webSite":"https://for.tube","totalValueLocked":22788623,"hasNew":0,"poolId":82,"poolName":"FOR Vault","link":"https://for.tube/bank/home","pair":"FOR","totalStake":5097528,"totalStakeRatio":0.22368741,"rewards":[{"cryptoId":4118,"name":"ForTube","symbol":"FOR","slug":"the-force-protocol"}],"impermanentLoss":"None","dailyROI":0.01422273972603,"yearlyROI":5.1913},{"id":"600004163c1b4b4fdf0bb037","name":"Mithril Cash","platform":"Ethereum","webSite":"https://mith.cash/","totalValueLocked":836937,"hasNew":1,"poolId":207,"poolName":"MIS_USDT-SUSHI-LPV2","link":"https://mith.cash/","pair":"MIS-USDT","totalStake":118434,"totalStakeRatio":0.14150886,"rewards":[{"cryptoId":8141,"name":"Mithril Share","symbol":"MIS","slug":"mithril-share"}],"impermanentLoss":"High","dailyROI":0.01376410958904,"yearlyROI":5.0239},{"id":"5f5b5b9cb761c05513d83568","name":"Synthetix","platform":"Ethereum","webSite":"https://mintr.synthetix.io/","totalValueLocked":192146030.16113365,"auditList":[{"url":"https://docs.synthetix.io/contracts/audits/","auditFirm":"Iosiro"}],"hasNew":0,"poolId":18,"poolName":"Curve sUSD","link":"https://mintr.synthetix.io/","pair":"sUSD","totalStake":192146030.16113365,"totalStakeRatio":1,"rewards":[{"cryptoId":2586,"name":"Synthetix","symbol":"SNX","slug":"synthetix-network-token"},{"cryptoId":6538,"name":"Curve DAO Token","symbol":"CRV","slug":"curve-dao-token"}],"impermanentLoss":"None","dailyROI":0.01129369863014,"yearlyROI":4.1222},{"id":"5fcf5b00c5adb439ad44e3d3","name":"Venus","platform":"Binance Smart Chain","webSite":"https://venus.io/","totalValueLocked":9766742349.3,"auditList":[{"url":"https://certik.foundation/projects/swipe","auditFirm":"Certik"}],"hasNew":1,"poolId":197,"poolName":"vBNB-BNB Lending","link":"https://app.venus.io/dashboard","pair":"vBNB-BNB","totalStake":1621405283.35,"totalStakeRatio":0.16601291,"rewards":[{"cryptoId":7288,"name":"Venus","symbol":"XVS","slug":"venus"}],"impermanentLoss":"None","dailyROI":0.01106849315068,"yearlyROI":4.04},{"id":"5f86b154cc06881662044a5c","name":"Flamincome","platform":"Ethereum","webSite":"https://flamincome.finance/","totalValueLocked":102436324.81345797,"hasNew":0,"poolId":184,"poolName":"WBTC VAULT","link":"https://app.flamincome.finance/","pair":"WBTC","totalStake":47152065.97592938,"totalStakeRatio":0.46030611,"rewards":[{"cryptoId":3717,"name":"Wrapped Bitcoin","symbol":"WBTC","slug":"wrapped-bitcoin"}],"impermanentLoss":"None","dailyROI":0.01076712328767,"yearlyROI":3.93},{"id":"5fcf5b00c5adb439ad44e3d3","name":"Venus","platform":"Binance Smart Chain","webSite":"https://venus.io/","totalValueLocked":9766742349.3,"auditList":[{"url":"https://certik.foundation/projects/swipe","auditFirm":"Certik"}],"hasNew":1,"poolId":194,"poolName":"vETH-ETH Lending","link":"https://app.venus.io/dashboard","pair":"vETH-ETH","totalStake":917734767.89,"totalStakeRatio":0.09396529,"rewards":[{"cryptoId":7288,"name":"Venus","symbol":"XVS","slug":"venus"}],"impermanentLoss":"None","dailyROI":0.00978082191781,"yearlyROI":3.57},{"id":"5f86b154cc06881662044a5c","name":"Flamincome","platform":"Ethereum","webSite":"https://flamincome.finance/","totalValueLocked":102436324.81345797,"hasNew":0,"poolId":183,"poolName":"USDT VAULT","link":"https://app.flamincome.finance/","pair":"USDT","totalStake":33057976.21681692,"totalStakeRatio":0.32271732,"rewards":[{"cryptoId":825,"name":"Tether","symbol":"USDT","slug":"tether"}],"impermanentLoss":"None","dailyROI":0.00950684931507,"yearlyROI":3.47},{"id":"5f685b27fcdfe7080cdd0fba","name":"Fortube","platform":"Ethereum","webSite":"https://for.tube","totalValueLocked":22788623,"hasNew":0,"poolId":78,"poolName":"USDT Vault","link":"https://for.tube/bank/home","pair":"USDT","totalStake":9588306,"totalStakeRatio":0.42074969,"rewards":[{"cryptoId":4118,"name":"ForTube","symbol":"FOR","slug":"the-force-protocol"}],"impermanentLoss":"None","dailyROI":0.00948191780822,"yearlyROI":3.4609},{"id":"5f685b27fcdfe7080cdd0fba","name":"Fortube","platform":"Ethereum","webSite":"https://for.tube","totalValueLocked":22788623,"hasNew":0,"poolId":79,"poolName":"USDC Vault","link":"https://for.tube/bank/home","pair":"USDC","totalStake":1367397,"totalStakeRatio":0.06000349,"rewards":[{"cryptoId":4118,"name":"ForTube","symbol":"FOR","slug":"the-force-protocol"}],"impermanentLoss":"None","dailyROI":0.00948191780822,"yearlyROI":3.4609},{"id":"5f685b27fcdfe7080cdd0fba","name":"Fortube","platform":"Ethereum","webSite":"https://for.tube","totalValueLocked":22788623,"hasNew":0,"poolId":80,"poolName":"BUSD Vault","link":"https://for.tube/bank/home","pair":"BUSD","totalStake":1100342,"totalStakeRatio":0.04828471,"rewards":[{"cryptoId":4118,"name":"ForTube","symbol":"FOR","slug":"the-force-protocol"}],"impermanentLoss":"None","dailyROI":0.00948191780822,"yearlyROI":3.4609},{"id":"5f685b27fcdfe7080cdd0fba","name":"Fortube","platform":"Ethereum","webSite":"https://for.tube","totalValueLocked":22788623,"hasNew":0,"poolId":81,"poolName":"DAI Vault","link":"https://for.tube/bank/home","pair":"DAI","totalStake":152322,"totalStakeRatio":0.00668412,"rewards":[{"cryptoId":4118,"name":"ForTube","symbol":"FOR","slug":"the-force-protocol"}],"impermanentLoss":"None","dailyROI":0.00948191780822,"yearlyROI":3.4609},{"id":"5f685b27fcdfe7080cdd0fba","name":"Fortube","platform":"Ethereum","webSite":"https://for.tube","totalValueLocked":22788623,"hasNew":0,"poolId":85,"poolName":"YYDAI+YUSDC+YUSDT+YTUSD Vault","link":"https://for.tube/bank/home","pair":"yyDAI+yUSDC+yUSDT+yTUSD","totalStake":48595,"totalStakeRatio":0.00213242,"rewards":[{"cryptoId":4118,"name":"ForTube","symbol":"FOR","slug":"the-force-protocol"}],"impermanentLoss":"None","dailyROI":0.00948191780822,"yearlyROI":3.4609},{"id":"5fcf5b00c5adb439ad44e3d3","name":"Venus","platform":"Binance Smart Chain","webSite":"https://venus.io/","totalValueLocked":9766742349.3,"auditList":[{"url":"https://certik.foundation/projects/swipe","auditFirm":"Certik"}],"hasNew":1,"poolId":199,"poolName":"vLTC-LTC Lending","link":"https://app.venus.io/dashboard","pair":"vLTC-LTC","totalStake":40506476.01,"totalStakeRatio":0.00414739,"rewards":[{"cryptoId":7288,"name":"Venus","symbol":"XVS","slug":"venus"}],"impermanentLoss":"None","dailyROI":0.00882191780822,"yearlyROI":3.22},{"id":"5fcf5b00c5adb439ad44e3d3","name":"Venus","platform":"Binance Smart Chain","webSite":"https://venus.io/","totalValueLocked":9766742349.3,"auditList":[{"url":"https://certik.foundation/projects/swipe","auditFirm":"Certik"}],"hasNew":1,"poolId":195,"poolName":"vBUSD-BUSD Lending","link":"https://app.venus.io/dashboard","pair":"vBUSD-BUSD","totalStake":1655735746.75,"totalStakeRatio":0.16952794,"rewards":[{"cryptoId":7288,"name":"Venus","symbol":"XVS","slug":"venus"}],"impermanentLoss":"None","dailyROI":0.00871232876712,"yearlyROI":3.18},{"id":"5fcf5b00c5adb439ad44e3d3","name":"Venus","platform":"Binance Smart Chain","webSite":"https://venus.io/","totalValueLocked":9766742349.3,"auditList":[{"url":"https://certik.foundation/projects/swipe","auditFirm":"Certik"}],"hasNew":1,"poolId":196,"poolName":"vBTC-BTCB Lending","link":"https://app.venus.io/dashboard","pair":"vBTC-BTCB","totalStake":1927687841.25,"totalStakeRatio":0.19737265,"rewards":[{"cryptoId":7288,"name":"Venus","symbol":"XVS","slug":"venus"}],"impermanentLoss":"None","dailyROI":0.00865753424658,"yearlyROI":3.16},{"id":"600004163c1b4b4fdf0bb037","name":"Mithril Cash","platform":"Ethereum","webSite":"https://mith.cash/","totalValueLocked":836937,"hasNew":1,"poolId":208,"poolName":"MIC_USDT-SUSHI-LPV2","link":"https://mith.cash/","pair":"MIC-USDT","totalStake":718503,"totalStakeRatio":0.85849114,"rewards":[{"cryptoId":8141,"name":"Mithril Share","symbol":"MIS","slug":"mithril-share"}],"impermanentLoss":"High","dailyROI":0.00860821917808,"yearlyROI":3.142},{"id":"5fcf5b00c5adb439ad44e3d3","name":"Venus","platform":"Binance Smart Chain","webSite":"https://venus.io/","totalValueLocked":9766742349.3,"auditList":[{"url":"https://certik.foundation/projects/swipe","auditFirm":"Certik"}],"hasNew":1,"poolId":201,"poolName":"vUSDC-USDC Lending","link":"https://app.venus.io/dashboard","pair":"vUSDC-USDC","totalStake":1251335369.19,"totalStakeRatio":0.12812208,"rewards":[{"cryptoId":7288,"name":"Venus","symbol":"XVS","slug":"venus"}],"impermanentLoss":"None","dailyROI":0.00849315068493,"yearlyROI":3.1},{"id":"5fcf5b00c5adb439ad44e3d3","name":"Venus","platform":"Binance Smart Chain","webSite":"https://venus.io/","totalValueLocked":9766742349.3,"auditList":[{"url":"https://certik.foundation/projects/swipe","auditFirm":"Certik"}],"hasNew":1,"poolId":205,"poolName":"vLINK-LINK Lending","link":"https://app.venus.io/dashboard","pair":"vLINK-LINK","totalStake":83810578.65,"totalStakeRatio":0.00858122,"rewards":[{"cryptoId":7288,"name":"Venus","symbol":"XVS","slug":"venus"},{"cryptoId":1975,"name":"Chainlink","symbol":"LINK","slug":"chainlink"}],"impermanentLoss":"None","dailyROI":0.00783561643836,"yearlyROI":2.86},{"id":"5fcf5b00c5adb439ad44e3d3","name":"Venus","platform":"Binance Smart Chain","webSite":"https://venus.io/","totalValueLocked":9766742349.3,"auditList":[{"url":"https://certik.foundation/projects/swipe","auditFirm":"Certik"}],"hasNew":1,"poolId":204,"poolName":"vDOT-DOT Lending","link":"https://app.venus.io/dashboard","pair":"vDOT-DOT","totalStake":179096892.91,"totalStakeRatio":0.01833742,"rewards":[{"cryptoId":7288,"name":"Venus","symbol":"XVS","slug":"venus"},{"cryptoId":6636,"name":"Polkadot","symbol":"DOT","slug":"polkadot-new"}],"impermanentLoss":"None","dailyROI":0.00750684931507,"yearlyROI":2.74},{"id":"5f71c830edcba010f8a365b4","name":"Harvest","platform":"Ethereum","webSite":"https://harvest.finance/","totalValueLocked":270760747.9444821,"hasNew":0,"poolId":142,"poolName":"CRVRENWBTC Vault","link":"https://harvest.finance/","pair":"CRV-RENBTC","totalStake":104608567.18765447,"totalStakeRatio":0.38635056,"rewards":[{"cryptoId":6859,"name":"Harvest Finance","symbol":"FARM","slug":"harvest-finance"},{"cryptoId":6538,"name":"Curve DAO Token","symbol":"CRV","slug":"curve-dao-token"}],"impermanentLoss":"Low","dailyROI":0.00602739726027,"yearlyROI":2.2},{"id":"5f5b5b9cb761c05513d8356d","name":"Curve","platform":"Ethereum","webSite":"https://www.curve.fi/","totalValueLocked":1854776987.4432564,"auditList":[{"url":"https://www.curve.fi/curve_audits/00-ToB.pdf","auditFirm":"Trail of Bits"},{"url":"https://www.curve.fi/curve_audits/curve-dao-quantstamp.pdf","auditFirm":"Quantstamp"}],"hasNew":0,"poolId":40,"poolName":"sBTC","link":"https://www.curve.fi/sbtc","pair":"renBTC-wBTC-sBTC","totalStake":425205110.03057575,"totalStakeRatio":0.22924864,"rewards":[{"cryptoId":6538,"name":"Curve DAO Token","symbol":"CRV","slug":"curve-dao-token"}],"impermanentLoss":"Low","dailyROI":0.00577726027397,"yearlyROI":2.1087},{"id":"5f5b5b9cb761c05513d8356d","name":"Curve","platform":"Ethereum","webSite":"https://www.curve.fi/","totalValueLocked":1854776987.4432564,"auditList":[{"url":"https://www.curve.fi/curve_audits/00-ToB.pdf","auditFirm":"Trail of Bits"},{"url":"https://www.curve.fi/curve_audits/curve-dao-quantstamp.pdf","auditFirm":"Quantstamp"}],"hasNew":0,"poolId":39,"poolName":"renBTC","link":"https://www.curve.fi/ren","pair":"renBTC-wBTC","totalStake":517522019.25426126,"totalStakeRatio":0.27902116,"rewards":[{"cryptoId":6538,"name":"Curve DAO Token","symbol":"CRV","slug":"curve-dao-token"}],"impermanentLoss":"Low","dailyROI":0.00483287671233,"yearlyROI":1.764},{"id":"5f71c830edcba010f8a365b4","name":"Harvest","platform":"Ethereum","webSite":"https://harvest.finance/","totalValueLocked":270760747.9444821,"hasNew":0,"poolId":141,"poolName":"WBTC Vault","link":"https://harvest.finance/","pair":"WBTC","totalStake":1905686.0173395,"totalStakeRatio":0.00703827,"rewards":[{"cryptoId":6859,"name":"Harvest Finance","symbol":"FARM","slug":"harvest-finance"},{"cryptoId":6538,"name":"Curve DAO Token","symbol":"CRV","slug":"curve-dao-token"}],"impermanentLoss":"Low","dailyROI":0.00430136986301,"yearlyROI":1.57},{"id":"5f685b27fcdfe7080cdd0fba","name":"Fortube","platform":"Ethereum","webSite":"https://for.tube","totalValueLocked":22788623,"hasNew":0,"poolId":83,"poolName":"ETH Vault","link":"https://for.tube/bank/home","pair":"ETH","totalStake":3176820,"totalStakeRatio":0.13940377,"rewards":[{"cryptoId":4118,"name":"ForTube","symbol":"FOR","slug":"the-force-protocol"}],"impermanentLoss":"None","dailyROI":0.00355561643836,"yearlyROI":1.2978},{"id":"5f685b27fcdfe7080cdd0fba","name":"Fortube","platform":"Ethereum","webSite":"https://for.tube","totalValueLocked":22788623,"hasNew":0,"poolId":84,"poolName":"HBTC Vault","link":"https://for.tube/bank/home","pair":"HBTC","totalStake":1938891,"totalStakeRatio":0.08508153,"rewards":[{"cryptoId":4118,"name":"ForTube","symbol":"FOR","slug":"the-force-protocol"}],"impermanentLoss":"None","dailyROI":0.00355561643836,"yearlyROI":1.2978},{"id":"5f685b27fcdfe7080cdd0fba","name":"Fortube","platform":"Ethereum","webSite":"https://for.tube","totalValueLocked":22788623,"hasNew":0,"poolId":77,"poolName":"WBTC Vault","link":"https://for.tube/bank/home","pair":"WBTC","totalStake":218726,"totalStakeRatio":0.00959803,"rewards":[{"cryptoId":4118,"name":"ForTube","symbol":"FOR","slug":"the-force-protocol"}],"impermanentLoss":"None","dailyROI":0.00355561643836,"yearlyROI":1.2978},{"id":"5f5b5b9cb761c05513d83566","name":"dForce","platform":"Ethereum","webSite":"https://staking.dforce.network/dapp","totalValueLocked":85987737.45764147,"auditList":[{"url":"https://github.com/peckshield/publications#dforce-network","auditFirm":"Peckshield"}],"hasNew":0,"poolId":6,"poolName":"dUSDT/dUSDC/dDAI","link":"https://markets.dforce.network/","pair":"dUSDT-dUSDC-dDAI","totalStake":85374034.78,"totalStakeRatio":0.9928629,"rewards":[{"cryptoId":4758,"name":"dForce","symbol":"DF","slug":"dforce"}],"impermanentLoss":"None","dailyROI":0.00320767123288,"yearlyROI":1.1708},{"id":"5fcf5b00c5adb439ad44e3d3","name":"Venus","platform":"Binance Smart Chain","webSite":"https://venus.io/","totalValueLocked":9766742349.3,"auditList":[{"url":"https://certik.foundation/projects/swipe","auditFirm":"Certik"}],"hasNew":1,"poolId":198,"poolName":"vXRP-XRP Lending","link":"https://app.venus.io/dashboard","pair":"vXRP-XRP","totalStake":144934387.11,"totalStakeRatio":0.01483958,"rewards":[{"cryptoId":7288,"name":"Venus","symbol":"XVS","slug":"venus"}],"impermanentLoss":"None","dailyROI":0.00271232876712,"yearlyROI":0.99},{"id":"5fcf5b00c5adb439ad44e3d3","name":"Venus","platform":"Binance Smart Chain","webSite":"https://venus.io/","totalValueLocked":9766742349.3,"auditList":[{"url":"https://certik.foundation/projects/swipe","auditFirm":"Certik"}],"hasNew":1,"poolId":203,"poolName":"vBCH-BCH Lending","link":"https://app.venus.io/dashboard","pair":"vBCH-BCH","totalStake":33493073.45,"totalStakeRatio":0.0034293,"rewards":[{"cryptoId":7288,"name":"Venus","symbol":"XVS","slug":"venus"},{"cryptoId":1831,"name":"Bitcoin Cash","symbol":"BCH","slug":"bitcoin-cash"}],"impermanentLoss":"None","dailyROI":0.00197260273973,"yearlyROI":0.72},{"id":"5f86b154cc06881662044a5c","name":"Flamincome","platform":"Ethereum","webSite":"https://flamincome.finance/","totalValueLocked":102436324.81345797,"hasNew":0,"poolId":185,"poolName":"WETH VAULT","link":"https://app.flamincome.finance/","pair":"WETH","totalStake":22226282.620711666,"totalStakeRatio":0.21697657,"rewards":[{"cryptoId":2396,"name":"WETH","symbol":"WETH","slug":"weth"}],"impermanentLoss":"None","dailyROI":0.00090410958904,"yearlyROI":0.33},{"id":"5f685b27fcdfe7080cdd0fba","name":"Fortube","platform":"Ethereum","webSite":"https://for.tube","totalValueLocked":22788623,"hasNew":0,"poolId":87,"poolName":"YFII Vault","link":"https://for.tube/bank/home","pair":"YFII","totalStake":99696,"totalStakeRatio":0.00437481,"rewards":[{"cryptoId":4118,"name":"ForTube","symbol":"FOR","slug":"the-force-protocol"}],"impermanentLoss":"None","dailyROI":0.00071123287671,"yearlyROI":0.2596},{"id":"5f5b5b9cb761c05513d8356a","name":"Yearn","platform":"Ethereum","webSite":"https://yearn.finance/vaults","totalValueLocked":95063339.64427319,"auditList":[{"url":"https://github.com/iearn-finance/audits/blob/master/Certik%20-%20itoken-finance-audit-report-1.1.0.pdf","auditFirm":"Certik"},{"url":"https://github.com/iearn-finance/audits/blob/master/CryptoManiacs%20%20-%20Audit%20of%20iearn.finance%20by%20CryptoManiacs%20-%20HackMD.pdf","auditFirm":"CryptoManiacs"},{"url":"https://github.com/iearn-finance/audits/blob/master/Quantstamp%20-%20Yearn.Finance%20Security%20Review.pdf","auditFirm":"Quantstamp"},{"url":"https://github.com/iearn-finance/audits/blob/master/StrategyCurveYCRV.sol%20-%20HackMD.pdf","auditFirm":"HackMD"}],"hasNew":0,"poolId":21,"poolName":"aLINK Vault","link":"https://yearn.finance/vaults","pair":"aLINK","totalStake":14518975.416509617,"totalStakeRatio":0.15272949,"rewards":[{"cryptoId":5751,"name":"Aave LINK","symbol":"ALINK","slug":"aave-link"}],"impermanentLoss":"NONE","dailyROI":0.00000849315068,"yearlyROI":0.0031}],"reqLang":"en","globalMetrics":{"numCryptocurrencies":9346,"numMarkets":38795,"activeExchanges":368,"marketCap":2018264334555.5337,"marketCapChange":-3.012128,"totalVol":235287814861.01,"stablecoinVol":192823039016.39703,"stablecoinChange":2.389374107176,"totalVolChange":1.504849,"defiVol":18417992390.78092,"defiChange":6.497555663692,"defiMarketCap":99209843715.31325,"derivativesVol":267414605731.3849,"derivativeChange":22.190413399144,"btcDominance":51.716184758464,"btcDominanceChange":0.440898658464,"ethDominance":12.47819404483,"etherscanGas":{"lastBlock":"12276806","slowPrice":"151","slowConfirmationTime":"975","standardPrice":"159","standardConfirmationTime":"202","fastPrice":"256","fastConfirmationTime":"45"}},"pageSize":100,"namespacesRequired":["common"]}

In [29]:
farming_list = json['yieldFarmingList']

In [40]:
farming_data = []
for item in farming_list:
    pool_list = item['poolList']
    for pool_item in pool_list:
        rewards = [f"{reward['symbol']}/{reward['name']}" for reward in pool_item['rewards']]
        farming_data.append([pool_item['name'], pool_item['pair'], pool_item['totalStake'], pool_item['yearlyROI'], pool_item['impermanentLoss'], ",".join(rewards)])

In [41]:
df = pd.DataFrame(farming_data, columns=['name','pair', 'tvl', 'APY', 'impermanent loass', 'rewards'])

In [42]:
df

name                pair           tvl       APY  \
0       vBTC-BTCB Lending           vBTC-BTCB  1.927688e+09    3.1600   
1      vBUSD-BUSD Lending          vBUSD-BUSD  1.655736e+09    3.1800   
2        vBNB-BNB Lending            vBNB-BNB  1.621405e+09    4.0400   
3      vUSDC-USDC Lending          vUSDC-USDC  1.251335e+09    3.1000   
4      vUSDT-USDT Lending          vUSDT-USDT  1.063997e+09    5.6800   
..                    ...                 ...           ...       ...   
116   MIC_USDT-SUSHI-LPV2            MIC-USDT  7.185030e+05    3.1420   
117   MIS_USDT-SUSHI-LPV2            MIS-USDT  1.184340e+05    5.0239   
118  sUSD liquidity gauge  DAI-USDT-USDC-sUSD  1.170738e+05   67.1485   
119   dfi liquidity gauge       DAI-USDC-USDT  1.038863e+05  280.3962   
120   SFG liquidity gauge             SFG-DAI  1.499582e+04  523.6465   

    impermanent loass                                          rewards  
0                None                                        XVS/Venus  
1                None                                        XVS/Venus  
2                None                                        XVS/Venus  
3                None                                        XVS/Venus  
4                None                                        XVS/Venus  
..                ...                                              ...  
116              High                                MIS/Mithril Share  
117              High                                MIS/Mithril Share  
118               Low  SFG/S.Finance,CRV/Curve DAO Token,SNX/Synthetix  
119               Low                                    SFG/S.Finance  
120              High                                    SFG/S.Finance  

[121 rows x 6 columns]

In [43]:
df.to_csv('farming_data_cmc.csv')